In [10]:
import torch
from tqdm import tqdm, trange
import torch.nn as nn
from transformers import RobertaTokenizer, RobertaConfig, RobertaModel, AdamW
import transformers
import torch.nn.functional as F
from torch.nn import CrossEntropyLoss
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
import numpy as np
import random
from sklearn import metrics
import torch.nn as nn
import argparse
import torch.distributed as dist
import torch.utils.data.distributed
import os
import numpy as np
from sklearn.metrics import f1_score
from utils import (compute_metrics, convert_examples_to_features,
                        output_modes, processors)
from torch.utils.data import (DataLoader, RandomSampler, SequentialSampler,
                              TensorDataset)
from transformers import (WEIGHTS_NAME, get_linear_schedule_with_warmup, AdamW,
                          RobertaConfig,
                          RobertaForSequenceClassification,
                          RobertaTokenizer)
from CodeBertModel import TextCNNClassifer_pair,TextCNNClassifer_pair_nofeature
import os
# for i in range(58):
#     os.system('python3 run_classifier.py --model_type roberta --model_name_or_path microsoft/codebert-base --task_name codesearch --do_predict --output_dir ../data/codesearch/test/ --data_dir ../data/codesearch/test/ --max_seq_length 512 --per_gpu_train_batch_size 32 --per_gpu_eval_batch_size 32 --learning_rate 1e-5 --num_train_epochs 8 --test_file aspectj_'+str(i)+'.txt  --pred_model_dir ./models/java/checkpoint-best/ --test_result_dir ./results/java/batch_result_'+str(i)+'.txt')
from more_itertools import chunked
def calculate_same_value(labels_sorted, test_p_sorted, start_pos):
    i = start_pos
    num_same = 0
    num_p = 0
    while test_p_sorted[start_pos] == test_p_sorted[i]:
        num_same = num_same + 1
        if labels_sorted[i] ==1 : num_p = num_p + 1
        i = i + 1
        if i == len(labels_sorted ): break
    return num_p, num_same
def eval_mrr(test_p, labels):#在第二维相似度得分，真实标签
    test_p_sorted = test_p
    test_p_index = sorted(range(len(test_p_sorted)), key=lambda k: test_p_sorted[k], reverse=True)  # 降序排序
    test_p_sorted = sorted(test_p, reverse=True)

    labels_sorted = []
    for index in test_p_index:
        labels_sorted.append(labels[index])

    top_num = 10
    top10rank = 0
    for i in range(top_num):
        if (labels_sorted[i] == 1):
            '''
            num_p, num_s = calculate_same_value(labels_sorted, test_p_sorted, i)
            num_r = top_num - i
            if num_p > (num_s-num_r):
                top10rank = 1
                break
            v1 = perm(num_s-num_r, num_p)*perm(num_s-num_p,num_s-num_p)
            v2 = perm(num_s,num_s)
            top10rank = 1-(float)((float)(v1)/(float)(v2))
            if top10rank > 1: top10rank=1
            if top10rank!=top10rank: top10rank=1
            break

    return top10rank

    '''
            top10rank = 1
            break
    num_p, num_s = calculate_same_value(labels_sorted, test_p_sorted, 10)
    if (num_p >= 1): top10rank = 1  # 统计在第十位并列排名相同的文件中，是否含有相关文件

    MRRrank = 0.0
    for i in range(len(labels_sorted)):
        if (labels_sorted[i] == 1):
            MRRrank = MRRrank + float(1 / (i + 1))

    MAPrank = 0.0
    pos_num = 0
    for i in range(len(labels_sorted)):
        if (labels_sorted[i] == 1):
            pos_num = pos_num + 1
            MAPrank = MAPrank + float(pos_num / (i + 1))
    if pos_num==0:
        print('出现不存在pos的例子')
        pos_num=1
    MAPrank = float(MAPrank / pos_num)
    MRRrank = float(MRRrank / pos_num)

    return top10rank, MRRrank, MAPrank

def simple_accuracy(preds, labels):
#     print(type(preds),type(labels))
    return (preds == labels).mean()


def acc_and_f1(preds, labels):
    acc = simple_accuracy(preds, labels)
    f1 = f1_score(y_true=labels, y_pred=preds)
    return {
        "acc": acc,
        "f1": f1,
        "acc_and_f1": (acc + f1) / 2,
    }


def compute_metrics(preds, labels):
    assert len(preds) == len(labels)

    return acc_and_f1(preds, labels)
#设置种子，为了结果复现
def set_seed(args):
    random.seed(args.seed)
    np.random.seed(args.seed)
    torch.manual_seed(args.seed)

In [293]:
class args(object):
    """A single set of features of data."""

    def __init__(self):
        self.model_type = 'roberta'
        self.output_dir='/data/hdj/data/CodeBERT/codesearch/models/java'
        self.test_result_dir='/data/hdj/tracking_buggy_files/joblib_memmap_eclipse/notebook_0607_test_2hard_2_data.txt'
        self.start_epoch=0
        self.config_name=''
        self.model_name_or_path=None
        self.task_name='codesearch'
        self.tokenizer_name=''
        self.model_name_or_path='microsoft/codebert-base'
        self.do_lower_case=True
        self.seed=42
        self.gradient_accumulation_steps=1
        self.weight_decay=0.0
        self.max_grad_norm=1.0
        self.learning_rate=2e-5#1e-6 5e-5
        self.adam_epsilon=1e-8
        self.warmup_steps=0
        self.max_steps=-1
        self.num_train_epochs=4
# class args(object):
#     """A single set of features of data."""

#     def __init__(self):
#         self.model_type = 'codesearch'
#         self.output_dir='/data/hdj/data/CodeBERT/codesearch/models/java'
#         self.test_result_dir='/data/hdj/data/CodeBERT/codesearch/results/java/test_v1_0414.txt'
#         self.start_epoch=0
#         self.num_train_epochs=1
#         self.model_type='roberta'
args=args()
#带权重的交叉熵
# weights=torch.tensor([0.2,0.8]).cuda()
# loss_fun=CrossEntropyLoss(weight=weights)
#不带权重的交叉熵
loss_fun=CrossEntropyLoss()
#设置种子 复现结果
set_seed(args)

In [311]:
#加载数据并保存在cache里

class InputFeatures_hdj(object):
    """A single training/test features for a example."""
    def __init__(self,
                 code_tokens,
                 code_ids,
                 code_mask,
                 nl_tokens,
                 nl_ids,
                 nl_mask,
                 label_id,

    ):
        self.code_tokens = code_tokens
        self.code_ids = code_ids
        self.code_mask=code_mask
        self.nl_tokens = nl_tokens
        self.nl_ids = nl_ids
        self.nl_mask=nl_mask
        self.label_id=label_id
def convert_examples_to_features_hdj(examples,label_list,max_len,tokenizer):
    #code
    label_map = {'0':-1,'1':1}

    features = []
    for (ex_index, example) in enumerate(examples):
        if ex_index % 10000 == 0:
            print("Writing example %d of %d" % (ex_index, len(examples)))
            
        code=example.text_b
        code_tokens=tokenizer.tokenize(code)[:max_len-2]
        code_tokens =[tokenizer.cls_token]+code_tokens+[tokenizer.sep_token]
        code_ids =  tokenizer.convert_tokens_to_ids(code_tokens)
        code_input_mask = [1] * len(code_ids)
        padding_length = max_len - len(code_ids)
        code_ids+=[tokenizer.pad_token_id]*padding_length
        code_input_mask+=[0]*padding_length

        nl=example.text_a
        nl_tokens=tokenizer.tokenize(nl)[:max_len-2]
        nl_tokens =[tokenizer.cls_token]+nl_tokens+[tokenizer.sep_token]
        nl_ids =  tokenizer.convert_tokens_to_ids(nl_tokens)
        nl_input_mask = [1] * len(nl_ids)
        padding_length = max_len - len(nl_ids)
        nl_ids+=[tokenizer.pad_token_id]*padding_length
        nl_input_mask+=[0]*padding_length
        label_id = label_map[example.label]
        print('code_tokens :',code_tokens)
        print('code_ids :',code_ids)
        print('code_mask :',code_input_mask)
        features.append(
            InputFeatures_hdj(code_tokens = code_tokens,
                            code_ids = code_ids,
                            code_mask=code_input_mask,
                            nl_tokens = nl_tokens,
                            nl_ids = nl_ids,
                            nl_mask=nl_input_mask,
                            label_id=label_id))
    return features
def load_and_cache_examples_hdj(file_prefix,data_dir,train_file,dev_file,test_file, task, tokenizer,max_seq_length, ttype='train',need_feature=False):
    '''
        data_dir:数据目录
        train_file:训练文件
        dev_file:验证文件
        test_file:测试文件
        task:任务名 固定为codesearch
        tokenizer:分词器
        max_seq_length:最大序列长度 convert_examples_to_features使用到了
        ttype:类型 train dev test
        
        return：包装好的数据集 [all_input_ids, all_input_mask, all_segment_ids, all_label_ids]
    '''
    processor = processors[task]()#拿到CodesearchProcessor
    output_mode = output_modes[task]#输出模式 固定为 classification
    # if os.path.exists(cached_features_file):

    label_list = processor.get_labels()#固定为 ["0","1"]

    '''
        example结构：[InputExample(uid 'test-1',report,code,label)]
    '''
    if ttype == 'train':
        file_name = train_file.split('.')[0]
    elif ttype == 'dev':
        file_name = dev_file.split('.')[0]
    elif ttype == 'test':
        file_name = test_file.split('.')[0]
    cached_features_file = os.path.join(data_dir, 'cached_{}_{}_{}_{}_{}'.format(
        ttype,
        file_name,
        list(filter(None, args.model_name_or_path.split('/'))).pop(),
        str(max_seq_length),
        str(task)))
    try:
        print('直接加载cache文件')
        print('cached_features_file :',cached_features_file)
        features = torch.load(cached_features_file)
        if ttype == 'test':
            examples, instances = processor.get_test_examples(data_dir, test_file)
    except Exception as e:
        print(e)
        print('生成cache文件')
        examples=None
        if ttype == 'train':
            examples = processor.get_train_examples(data_dir, train_file)
        elif ttype == 'dev':
            examples = processor.get_dev_examples(data_dir=data_dir, dev_file= dev_file)
        elif ttype == 'test':
            #如果是test的话，instances就是[每一行是一条代测试的数据]
            examples, instances = processor.get_test_examples(data_dir, test_file)

        '''
            example:[[uid,report,code,label],[]...]
            label_list:['0','1']
            max_seq_length:200
            tokenizer:分词器
            output_mode:输出模式 固定为 classification
            cls_token:用来分类的token     '<s>', 0, 
            sep_token:用来分割语句的token '</s>', 2

            return：[  [       ( input_ids=input_ids,
                              input_mask=input_mask,
                              segment_ids=segment_ids,
                              label_id=label_id)
                        ]
                    ]
                    instances：[["0","5222","i am a noy","public class"],[],,]
        '''
    #     features = convert_examples_to_features(examples, label_list, max_seq_length, tokenizer, output_mode,
    #                                             cls_token=tokenizer.cls_token,
    #                                             sep_token=tokenizer.sep_token,
    #                                            )
        features =convert_examples_to_features_hdj(examples, label_list, max_seq_length, tokenizer)
        torch.save(features, cached_features_file)
    # Convert to Tensors and build dataset
    all_code_input_ids = torch.tensor([f.code_ids for f in features], dtype=torch.long)
    all_code_input_mask = torch.tensor([f.code_mask for f in features], dtype=torch.long)
    all_nl_input_ids = torch.tensor([f.nl_ids for f in features], dtype=torch.long)
    all_nl_input_mask = torch.tensor([f.nl_mask for f in features], dtype=torch.long)
    if output_mode == "classification":
        all_label_ids = torch.tensor([f.label_id for f in features], dtype=torch.long)
    if need_feature:
        feature=torch.tensor([f.feature for f in features],dtype=torch.float16)
        print('human_feature :',feature)
        dataset = TensorDataset(all_code_input_ids, all_code_input_mask, all_nl_input_ids, all_nl_input_mask,all_label_ids,feature)
    else:
        dataset = TensorDataset(all_code_input_ids, all_code_input_mask, all_nl_input_ids, all_nl_input_mask, all_label_ids)
    if (ttype == 'test'):
        return dataset, instances
    else:
        return dataset
# tokenizer = RobertaTokenizer.from_pretrained("microsoft/codebert-base",do_lower_case=False)

In [312]:
#数据集的配置参数
project='eclipse'
file_prefix='/data/hdj/tracking_buggy_files/'+project+'/'+project
data_dir = "/data/hdj/tracking_buggy_files/joblib_memmap_"+project+"/one_vs_two/"
test_dir="/data/hdj/tracking_buggy_files/joblib_memmap_"+project+"/one_vs_two/" #注意目前测试集的目录是单独的，更换测试数据需要更改
# train_file = "aspectj_train_small.txt"
# dev_file = "aspectj_val_small.txt"
test_file = "test_2hard_2_2tok5meth_data.txt"#目前只使用一个例子来进行测试，后期增加数据量
# train_file='aspectj_train_oversample.txt'
train_file='train_2hard_1_train_source_nomethod.txt'
# dev_file = "aspectj_val_oversample.txt"
dev_file = "train_2hard_1_val_source_nomethod_less.txt"
task_name = "codesearch"
max_seq_length = 256#关键参数设置 整个序列的最大长度
need_feature=False
val_set=load_and_cache_examples_hdj(file_prefix,data_dir,train_file,dev_file,test_file,task_name,tokenizer,max_seq_length,'dev')

直接加载cache文件
cached_features_file : /data/hdj/tracking_buggy_files/joblib_memmap_eclipse/one_vs_two/cached_dev_train_2hard_1_val_source_nomethod_less_codebert-base_256_codesearch
[Errno 2] No such file or directory: '/data/hdj/tracking_buggy_files/joblib_memmap_eclipse/one_vs_two/cached_dev_train_2hard_1_val_source_nomethod_less_codebert-base_256_codesearch'
生成cache文件
Writing example 0 of 100
code_tokens : ['<s>', 'package', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġe', '4', 'Ġ.', 'Ġu', 'i', 'Ġ.', 'Ġmodel', 'Ġ.', 'Ġapplication', 'Ġ.', 'Ġutil', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġe', '4', 'Ġ.', 'Ġu', 'i', 'Ġ.', 'Ġmodel', 'Ġ.', 'Ġapplication', 'Ġ.', 'Ġ*', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġem', 'f', 'Ġ.', 'Ġcommon', 'Ġ.', 'Ġnotify', 'Ġ.', 'ĠAdapter', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġem', 'f', 'Ġ.', 'Ġcommon', 'Ġ.', 'Ġnotify', 'Ġ.', 'ĠNot', 'ifier', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġem', 'f', 'Ġ.', 'Ġcommon', 'Ġ.', 'Ġnotify', 'Ġ.', 

code_tokens : ['<s>', 'package', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġu', 'i', 'Ġ.', 'Ġexamples', 'Ġ.', 'Ġfield', 'ass', 'ist', 'Ġ;', 'Ġimport', 'Ġjava', 'Ġ.', 'Ġtext', 'Ġ.', 'ĠMessage', 'Format', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġcore', 'Ġ.', 'Ġruntime', 'Ġ.', 'ĠI', 'Status', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġcore', 'Ġ.', 'Ġruntime', 'Ġ.', 'ĠStatus', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġbindings', 'Ġ.', 'Ġkeys', 'Ġ.', 'ĠKey', 'St', 'ro', 'ke', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġbindings', 'Ġ.', 'Ġkeys', 'Ġ.', 'ĠPar', 'se', 'Exception', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġdialog', 's', 'Ġ.', 'ĠDial', 'og', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġdialog', 's', 'Ġ.', 'ĠID', 'ial', 'og', 'Const', 'ants', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġdialog', 's', 'Ġ.', 'ĠMessage', 'Dialog', 'Ġ;', 'Ġi

code_tokens : ['<s>', 'package', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġu', 'i', 'Ġ.', 'Ġexamples', 'Ġ.', 'Ġjobs', 'Ġ.', 'Ġviews', 'Ġ;', 'Ġimport', 'Ġjava', 'Ġ.', 'Ġlang', 'Ġ.', 'Ġreflect', 'Ġ.', 'ĠInv', 'ocation', 'Target', 'Exception', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġcore', 'Ġ.', 'Ġresources', 'Ġ.', 'ĠI', 'Works', 'pace', 'Run', 'n', 'able', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġcore', 'Ġ.', 'Ġresources', 'Ġ.', 'ĠResources', 'Plugin', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġcore', 'Ġ.', 'Ġruntime', 'Ġ.', 'Ġ*', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġcore', 'Ġ.', 'Ġruntime', 'Ġ.', 'Ġjobs', 'Ġ.', 'ĠJob', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġaction', 'Ġ.', 'ĠAction', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġdialog', 's', 'Ġ.', 'ĠID', 'ial', 'og', 'Const', 'ants', 'Ġ;', 'Ġimport', 'Ġorg', 'Ġ.', 'Ġeclipse', 'Ġ.', 'Ġj', 'face', 'Ġ.', 'Ġdialog', 's', 'Ġ.', 'ĠMessage', 'Dialog', '

In [306]:
val_set.tensors[0]

tensor([[    0, 46181, 31118,  ...,   305, 14269,     2],
        [    0, 46181, 31118,  ...,  1717,   118,     2],
        [    0, 46181, 31118,  ...,    36,  4839,     2],
        ...,
        [    0, 46181, 31118,  ...,  1717,   118,     2],
        [    0, 46181, 31118,  ...,    36, 26602,     2],
        [    0, 46181, 31118,  ..., 12956,   479,     2]])

In [14]:
import re
import pandas as pd
import nltk
import string
import glob
import string
import inflection
import json
import subprocess
from unqlite import UnQLite
import pickle
from scipy import sparse
import re
import numpy as np
from nltk.corpus import stopwords
from collections import Counter
from nltk import wordpunct_tokenize
from nltk.stem.porter import PorterStemmer
from re import finditer
stemmer = PorterStemmer()

from transformers import (WEIGHTS_NAME, get_linear_schedule_with_warmup, AdamW,
                          RobertaConfig,
                          RobertaForSequenceClassification,
                          RobertaTokenizer)
from skopt import *
class CorpusParser:

	def __init__(self, filename):
		self.filename = filename
		self.regex = re.compile('^#\s*\d+')
		self.corpus = dict()

	def parse(self):
		with open(self.filename) as f:
			s = ''.join(f.readlines())
		blobs = s.split('#')[1:]
		for x in blobs:
			text = x.split()
			docid = text.pop(0)
			self.corpus[docid] = text

	def get_corpus(self):
		return self.corpus


class QueryParser:

	def __init__(self, filename):
		self.filename = filename
		self.queries = []

	def parse(self):
		with open(self.filename) as f:
			lines = ''.join(f.readlines())
		self.queries = [x.rstrip().split() for x in lines.split('\n')[:-1]]

	def get_queries(self):
		return self.queries


# if __name__ == '__main__':
#     qp = QueryParser('/data/hdj/BM25/text/queries.txt')
#     qp.parse()
#     print (qp.get_queries())
#     cp=CorpusParser('/data/hdj/BM25/text/corpus.txt')
#     cp.parse()
    
    

In [4]:
def _process_notes(note,note_not_tokenize, repository_path):
    #ea6b85284ac8a5b67421bafebe99a7cc2ca6d73e 00001f23f4c6321b7b4468d2eae6b4a1e0e24bce
    (note_content_sha, note_object_sha) = note.split(' ')
    (note_content_sha_not_tokenize, note_object_sha_not_tokenize) = note_not_tokenize.split(' ')

    note_content = cat_file_blob(repository_path, note_content_sha)
    note_content_not_tokenize = cat_file_blob(repository_path, note_content_sha_not_tokenize)
    ast_extraction_result = json.loads(note_content)
    ast_extraction_result_not_tokenize = json.loads(note_content_not_tokenize)
    ast_extraction_result['methodContent']=ast_extraction_result_not_tokenize['methodContent']
    return note_object_sha, ast_extraction_result
def cat_file_blob(repository_path, sha, encoding='latin-1'):
    #git -C /data/hdj/SourceFile/tracking_buggy_files_tomcat_dataset cat-file blob ea6b85284ac8a5b67421bafebe99a7cc2ca6d73e > note_content.txt
    #返回所有文件相关的信息 包括分割好的方法和源码 dict格式
    cmd = ' '.join(['git', '-C', repository_path, 'cat-file', 'blob', sha])
    cat_file_process = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE)
    result = cat_file_process.stdout.read().decode(encoding)
    return result

def _f(args):
    return _process_notes(args[0], args[1],args[2])
def list_notes(repository_path, refs='refs/notes/commits'):
    #当ref=='refs/notes/tokenized_counters'时，解析出来的就是tokenized后的文件
    #git -C /data/hdj/SourceFile/tracking_buggy_files_tomcat_dataset notes --ref refs/notes/commits list
    #返回一堆 shas
    cmd = ' '.join(['git', '-C', repository_path, 'notes', '--ref', refs, 'list'])
    notes_lines = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE).stdout.read().decode('latin-1').split('\n')
    return notes_lines

In [107]:
tokenized_refs = 'refs/notes/tokenized_counters'
ast_notes = list_notes(repository_path, refs=tokenized_refs)
ast_notes_not_tokenize=list_notes(repository_path)
print("existing tokenized notes ", len(ast_notes))
print("existing not tokenized notes ", len(ast_notes_not_tokenize))

existing tokenized notes  22080
existing not tokenized notes  22080


In [ ]:
ast_notes[:2],ast_notes_not_tokenize[:2]

In [112]:

note_object_sha=None
ast_extraction_result=None
for note,note_not_tokenize in zip(ast_notes,ast_notes_not_tokenize):
    note_object_sha, ast_extraction_result=_f([note,note_not_tokenize, repository_path])
    break

In [117]:
note_object_sha

'00001f23f4c6321b7b4468d2eae6b4a1e0e24bce'

In [21]:
# ast_extraction_result

In [160]:

repository_path='/data/hdj/SourceFile/tracking_buggy_files_eclipse_platform_ui_dataset'
# refs='refs/notes/commits'
refs='refs/notes/tokenized_counters'
cmd = ' '.join(['git', '-C', repository_path, 'notes', '--ref', refs, 'list'])
notes_lines = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE).stdout.read().decode('latin-1').split('\n')

In [161]:
len(notes_lines)

76927

In [162]:
repository_path='/data/hdj/SourceFile/tracking_buggy_files_eclipse_platform_ui_dataset'
refs_not_tokenize='refs/notes/commits'
cmd = ' '.join(['git', '-C', repository_path, 'notes', '--ref', refs_not_tokenize, 'list'])
notes_lines_not_tokenize = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE).stdout.read().decode('latin-1').split('\n')

In [163]:
len(notes_lines_not_tokenize)

76927

In [169]:
notes_lines_not_tokenize[0],notes_lines[0]

('edd8bf1796f80787e10e0e26553473bb388a1296 00015890f7b977548664ea333a2f35351dbb6b11',
 '66b4978066ef931b2e37d99f76a57d5725d58c1f 00015890f7b977548664ea333a2f35351dbb6b11')

In [170]:
sha='edd8bf1796f80787e10e0e26553473bb388a1296'
encoding='latin-1'
cmd = ' '.join(['git', '-C', repository_path, 'cat-file', 'blob', sha])
cat_file_process = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE)
result = cat_file_process.stdout.read().decode(encoding)

In [167]:
result

''

In [171]:
for key,val in eval(result).items():
    print(key,val)

classNames ['org.eclipse.ui.menus.AbstractWorkbenchTrimWidget']
superclassNames ['org.eclipse.jface.menus.AbstractTrimWidget']
interfaceNames ['IWorkbenchWidget']
methodNames ['init', 'getPreferredSize', 'getWorkbenchWindow', 'AbstractWorkbenchTrimWidget']
variableNames ['wbWindow']
methodContent ['/**\n\t * \n\t */\n\tpublic AbstractWorkbenchTrimWidget() {\n\t\tsuper();\n\t}', '/**\n\t * Define the IWorkbenchWindow that this trim is being hosted in.\n\t * Note that subclasses may extend but should not override. The\n\t * base implementation caches the value for access through the\n\t * <code>getWorkbenchWindow</code> method.\n\t * \n\t * @see org.eclipse.ui.menus.IWorkbenchWidget#init(org.eclipse.ui.IWorkbenchWindow)\n\t */\n\tpublic void init(IWorkbenchWindow workbenchWindow) {\n\t\twbWindow = workbenchWindow;\n\t}', '/**\n\t * Convenience method to get the IWorkbenchWindow that is\n\t * hosting this widget.\n\t * \n\t * @return The IWorkbenchWindow hosting this widget.\n\t */\n\tpub

In [172]:
sha_not_tokenize='66b4978066ef931b2e37d99f76a57d5725d58c1f'
encoding='latin-1'
cmd = ' '.join(['git', '-C', repository_path, 'cat-file', 'blob', sha_not_tokenize])
cat_file_process = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE)
result_not_tokenize = cat_file_process.stdout.read().decode(encoding)

In [173]:
for key,val in eval(result_not_tokenize).items():
    print(key,val)

tokenizedVariableNames [{'window': 1, 'wb': 1, 'wbwindow': 1}]
superclassNames ['org.eclipse.jface.menus.AbstractTrimWidget']
interfaceNames ['IWorkbenchWidget']
tokenizedMethodNames [{'init': 1}, {'getpreferreds': 1, 'size': 1, 'prefer': 1, 'get': 1}, {'workbench': 1, 'getworkbenchwindow': 1, 'window': 1, 'get': 1}, {'trim': 1, 'widget': 1, 'abstract': 1, 'workbench': 1, 'abstractworkbenchtrimwidget': 1}]
methodVariableTypes [[], ['org.eclipse.ui.IWorkbenchWindow'], [], []]
tokenizedSuperclassNames [{'trim': 1, 'widget': 1, 'jface': 1, 'menu': 1, 'abstract': 1, 'abstracttrimwidget': 1, 'org': 1, 'eclips': 1}]
classNames ['org.eclipse.ui.menus.AbstractWorkbenchTrimWidget']
tokenizedSource {'trim': 6, 'overrid': 1, 'www': 1, 'right': 1, 'super': 1, 'point': 3, 'item': 1, 'abstract': 5, 'prefer': 2, 'workbench': 18, 'getworkbenchwindow': 2, 'return': 4, 'packag': 1, 'see': 1, 'api': 1, 'wb': 3, 'subclass': 1, 'contributor': 1, 'reserv': 1, 'getpreferreds': 1, 'contribut': 2, 'code': 4, '

In [20]:
# eval(result_not_tokenize)

In [19]:
# eval(result)

In [18]:
# notes_lines

In [150]:

# bug_report_files_collection_db = UnQLite("/data/hdj/tracking_buggy_files/tomcat/tomcat_bug_report_files_collection_db",
#                                              flags=0x00000100 | 0x00000001)
ast_cache_collection_db=UnQLite("/data/hdj/tracking_buggy_files/eclipse/eclipse_ast_cache_collection_db",
                                             flags=0x00000100 | 0x00000001)

In [31]:
type(bug_report_files_collection_db),type(tomcat_ast_cache_collection_db)

(unqlite.UnQLite, unqlite.UnQLite)

In [155]:
# bug_report_files=[item for item in bug_report_files_collection_db]
ast=[item for item in ast_cache_collection_db]

In [135]:
len(ast),#len(bug_report_files_collection_db)

(19380,)

In [184]:
# ast[2]

In [144]:
# bug_report_files[0]
train_k=pd.read_csv('/data/hdj/tracking_buggy_files/joblib_memmap_eclipse/one_vs_two/train_2hard_1_train.csv')
train_k.set_index(['bid','fid'], inplace = True)
all_ast_index=list(train_k.index.get_level_values(1).unique())


In [146]:
all_ast_index[:10]

['0b29d74ed59f8d0d492e994967430632b295d10e',
 '9bf12a372b2c5bad5a3eb44305c8612c437de1e5',
 '2d34364f931430cc1d85ea88b234686d56b9ff2b',
 '58abea562f92d3a37269efb04a0a9c08acfd9da5',
 '8815221697d7cc3eb503e24b6672e6e70b2cd50d',
 '160f729dece568731a1aa010fae846c5dbd36962',
 'a6d3fbbfd8cee11f3d49a7ad4fceefc9f2bf8a4f',
 'a7d75f1a43116d704418be6b1bd5f4a7f7e509c6',
 'b041dc69f08a5f49a6fb05000e81d8acac5f058c',
 '0cd492fedc97e4c346bdb48c3944c7425c0dde8e']

In [185]:
# len(all_ast_index) 
# ast_file = pickle.loads(ast_cache_collection_db['4c0dff6321b652932b5c55043ccd01f63f6648ec'])
# ast_file

In [154]:
notfou=0
for key in all_ast_index:
    try:
        ast_file = pickle.loads(ast_cache_collection_db[key])
    except:
        notfou+=1
#         continue
print(notfou)

18708


In [186]:
# type(ast_file)
# # ast=[item for item in ast_cache_collection_db]
# for key,val in ast_file.items():
#     print(key,type(val),val)

In [144]:
# len(tomcat_ast_file['tokenizedMethods'])
ast_file['methodContent']

['public Relationship(\n\t\tString name, \n\t\tKind kind,\n\t\tString sourceHandle,\n\t\tList targets,\n\t\tboolean runtimeTest) {\n\t\t\t\n\t\tthis.name = name;\n\t\tthis.isAffects = \n\t\t\tname.equals("advises") || \n\t        name.equals("declares on") || \n\t        name.equals("softens") ||\n\t        name.equals("matched by") || \n\t        name.equals("declared on") || \n\t        name.equals("annotates");\n\t\tthis.kind = kind;\n\t\tthis.sourceHandle = sourceHandle;\n\t\tthis.targets = targets;\n\t\tthis.hasRuntimeTest = runtimeTest;\n\t}',
 'public String getName() {\n\t\treturn name;\n\t}',
 'public Kind getKind() {\n\t\treturn kind;\n\t}',
 'public String toString() {\n\t\treturn name;\n\t}',
 'public String getSourceHandle() {\n\t\treturn sourceHandle;\n\t}',
 'public List getTargets() {\n\t\treturn targets;\n\t}',
 'public void addTarget(String handle) {\n\t\tif (targets.contains(handle)) return;\n\t\ttargets.add(handle);\n\t}',
 'public boolean hasRuntimeTest() {\n\t\tre

In [16]:
# tomcat_ast_file['methodContent'][:10]

In [11]:
# tomcat_ast_file['tokenizedSource']

In [12]:
# tomcat_ast[:1]

In [55]:
# bug_report_files[:1]

In [141]:
import pickle
current_files = pickle.loads(bug_report_files_collection_db['1cc6641c54f6b0d2dd69ab5323487ffa51f9df9d'])
# bug_report_files_collection_db.close()

In [142]:
type(current_files)
for key,val in current_files.items():
    print(key,type(val),len(val))

shas <class 'list'> 1131
class_name_to_sha <class 'dict'> 1497
sha_to_file_name <class 'dict'> 1131


In [13]:
# current_files['shas']

In [14]:
# current_files['sha_to_file_name']

In [15]:
# current_files['class_name_to_sha']

# 检查vectorize_ast生成的数据格式

In [44]:
data_prefix='/data/hdj/tracking_buggy_files/tomcat/tomcat'
asts = UnQLite(data_prefix+"_ast_index_collection_index_db", flags = 0x00000100 | 0x00000001)
types = UnQLite(data_prefix+"_ast_types_collection_index_db", flags = 0x00000100 | 0x00000001)
bug_report_index_collection = UnQLite(data_prefix+"_bug_report_index_collection_index_db")
raw_count_data = sparse.load_npz(data_prefix+'_raw_count_data.npz')
feature_names=json.load(open(data_prefix+'_feature_names_dict'))
ast_index=[item for item in asts]
ast_types=[item for item in types]
bug_report_index=[item for item in bug_report_index_collection]

In [55]:
# bug_report_index
raw_count_data.shape
raw_count_data[0]

<1x32066 sparse matrix of type '<class 'numpy.float64'>'
	with 283 stored elements in Compressed Sparse Row format>

In [48]:
print(ast_index[0][0],len(ast_index))
print(ast_types[0][0],len(ast_types))
print(bug_report_index[0][0],len(bug_report_index))
ast_index_files = pickle.loads(asts[ast_index[0][0]])
ast_types_files = pickle.loads(types[ast_types[0][0]])
bug_report_index_files = pickle.loads(bug_report_index_collection[bug_report_index[0][0]])

f6a1d096154083210153a69e24000e8f47028f97 22079
ebc8fbfa0b2fa6a61fef2955583440192785e6fb 22079
6cce550 1056


In [53]:
len(feature_names),
# feature_names

(32066,)

In [49]:
print('ast_index_files :',ast_index_files)
print('ast_types_files :',ast_types_files)
print('bug_report_index_files :',bug_report_index_files)

ast_index_files : {'source': 964, 'methodsStart': 965, 'methodsEnd': 967, 'classNamesStart': 968, 'classNamesEnd': 968, 'methodNamesStart': 969, 'methodNamesEnd': 971, 'variableNamesStart': 972, 'variableNamesEnd': 973, 'commentsStart': 974, 'commentsEnd': 981}
ast_types_files : {'superclassNames': [], 'interfaceNames': ['org.apache.catalina.LifecycleListener', 'java.rmi.server.RMIClientSocketFactory', 'java.io.Serializable'], 'methodVariableTypes': [[], ['int'], [], ['int'], [], ['int'], [], ['int'], [], ['boolean'], ['org.apache.catalina.util.StringManager'], ['org.apache.catalina.LifecycleEvent', 'HashMap', 'Object', 'java.rmi.server.RMIServerSocketFactory', 'String', 'java.rmi.server.RMIClientSocketFactory'], ['StringBuffer', 'HashMap', 'java.net.MalformedURLException', 'javax.management.MBeanServer', 'Object', 'java.io.IOException', 'org.apache.catalina.util.StringManager', 'String', 'javax.management.remote.JMXServiceURL', 'javax.management.remote.JMXConnectorServer', 'int', 'jav

In [62]:
#检查 _partial_enriched_api_index_lookup
bug_report_id='0ae33cb'
feature_names=json.load(open(data_prefix+'_'+bug_report_id+'_partial_enriched_api_index_lookup'))

In [64]:
len(feature_names)

1523

In [58]:
from sklearn.feature_extraction import DictVectorizer

data = [ {'city':'Dubai','temperature':33.},
    {'city':'London','temperature':12.},
    {'city':'San Fransisco','temperature':18.},]
dictVector = DictVectorizer()
vectorize_data=dictVector.fit_transform(data)
print(vectorize_data)
print(dictVector.feature_names_)


  (0, 0)	1.0
  (0, 3)	33.0
  (1, 1)	1.0
  (1, 3)	12.0
  (2, 2)	1.0
  (2, 3)	18.0
['city=Dubai', 'city=London', 'city=San Fransisco', 'temperature']


In [59]:
type(vectorize_data),vectorize_data

(scipy.sparse.csr.csr_matrix,
 <3x4 sparse matrix of type '<class 'numpy.float64'>'
 	with 6 stored elements in Compressed Sparse Row format>)

In [57]:
dictVector.inverse_transform(vectorize_data)

[{'city=Dubai': 1.0, 'temperature': 33.0},
 {'city=London': 1.0, 'temperature': 12.0},
 {'city=San Fransisco': 1.0, 'temperature': 18.0}]

In [72]:
from scipy.sparse import coo_matrix, hstack,vstack
a1=coo_matrix([1,1,1,1])
b1=coo_matrix([2,2,2,2])
c1=coo_matrix([3,3,3,3])
rows=[a1,b1,c1]
matrix=sparse.vstack(rows)

In [73]:
matrix.toarray()

array([[1, 1, 1, 1],
       [2, 2, 2, 2],
       [3, 3, 3, 3]])

# 检查vectorize_ast结束

# 检查convert_tf_idf

In [84]:
raw_count_data = sparse.load_npz(data_prefix+'_0ae2f34_tf_idf_data.npz')
bug_report_id='0ae2f34'
feature_names=json.load(open(data_prefix+'_'+bug_report_id+'_tf_idf_index_lookup'))

In [85]:
print(raw_count_data.shape)
print(len(feature_names))
for i,(key,val) in enumerate(feature_names.items()):
    if i<=1780:
        continue
    print(key,val)

(102832, 32066)
1786
2787f3aa87c9c458f2b8c1ecc778d23fd77352f3 {'source': 102619, 'methodsStart': 102620, 'methodsEnd': 102626, 'classNamesStart': 102627, 'classNamesEnd': 102627, 'methodNamesStart': 102628, 'methodNamesEnd': 102634, 'variableNamesStart': 102635, 'variableNamesEnd': 102649, 'commentsStart': 102650, 'commentsEnd': 102651}
5b664b62ff3fdc645021f3c904c7a7d237d711ae {'source': 102652, 'methodsStart': 102653, 'methodsEnd': 102660, 'classNamesStart': 102661, 'classNamesEnd': 102661, 'methodNamesStart': 102662, 'methodNamesEnd': 102669, 'variableNamesStart': 102670, 'variableNamesEnd': 102676, 'commentsStart': 102677, 'commentsEnd': 102678}
abdf02d69e66f140e0f88725a2b800d2031a0ee4 {'source': 102679, 'methodsStart': 102680, 'methodsEnd': 102689, 'classNamesStart': 102690, 'classNamesEnd': 102690, 'methodNamesStart': 102691, 'methodNamesEnd': 102700, 'variableNamesStart': 102701, 'variableNamesEnd': 102731, 'commentsStart': 102732, 'commentsEnd': 102753}
4ea737a735275e5efb94519ed

# 检查convert_tf_idf结束

# 检查calculate_feature_3

In [86]:
raw_count_data = sparse.load_npz(data_prefix+'_0ae2f34_feature_3_data.npz')
bug_report_id='0ae2f34'
feature_names=json.load(open(data_prefix+'_'+bug_report_id+'_feature_3_index_lookup'))

In [89]:
# feature_names
python3 fix_and_augment.py /data/hdj/tracking_buggy_files/swt/swt_base.json /data/hdj/SourceFile/tracking_buggy_files_swt_dataset/ > swt_aug.json

In [87]:
print(raw_count_data.shape)
print(len(feature_names))
for i,(key,val) in enumerate(feature_names.items()):
    if i<=1780:
        continue
    print(key,val)

(1786, 32066)
1785
2787f3aa87c9c458f2b8c1ecc778d23fd77352f3 1781
5b664b62ff3fdc645021f3c904c7a7d237d711ae 1782
abdf02d69e66f140e0f88725a2b800d2031a0ee4 1783
4ea737a735275e5efb94519ed09477ea7c87987a 1784


In [97]:
len(sum(raw_count_data.toarray()))
for num in sum(raw_count_data.toarray()):
    if num!=0:
        print(num)

0.3779644730092272
0.3779644730092272
0.3779644730092272
0.3779644730092272
0.3779644730092272
0.3779644730092272
0.3779644730092272


In [ ]:
raw_count_data = sparse.load_npz(data_prefix+'_0ae2f34_feature_3_data.npz')

# 检查calculate_feature_3结束

# 检查save_normalized_fold_dataframes.py

In [98]:
file_path = '/data/hdj/tracking_buggy_files/swt/swt_fe06bdb_features.npz'
features_data = sparse.load_npz(file_path).tocsr()

In [101]:
print(features_data.shape)
features_data.toarray()

(2454, 20)


array([[0.00000000e+00, 0.00000000e+00, 4.09260456e-02, ...,
        0.00000000e+00, 2.78526591e-05, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 4.09260456e-02, ...,
        2.49496923e-04, 9.45204709e-04, 0.00000000e+00],
       [7.88478842e-04, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       ...,
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        9.56944768e-06, 1.80527623e-04, 0.00000000e+00],
       [1.39194950e-02, 0.00000000e+00, 0.00000000e+00, ...,
        7.18652237e-05, 6.61278400e-05, 0.00000000e+00],
       [4.10699047e-02, 0.00000000e+00, 0.00000000e+00, ...,
        7.18652237e-05, 1.35573739e-03, 0.00000000e+00]])

In [108]:
file_path='/data/hdj/tracking_buggy_files/swt/swt_fe06bdb_files'
filenames=None
with open(file_path, 'r') as f:
    files_list = json.load(f)
#     return files_list
    print(type(files_list))
    filenames=files_list

<class 'list'>


In [109]:
df = pd.DataFrame(features_data.todense(), index=filenames)
df.columns = ['f1', 'f2', 'f3', 'f4', 'f5', 'f6', 'f7', 'f8', 'f9', 'f10', 'f11', 'f12', 'f13', 'f14', 'f15',
                      'f16', 'f17', 'f18', 'f19', 'used_in_fix']

In [111]:
print(df.shape)
df.head()

(2454, 20)


f1   f2        f3   f4  \
3c1339e33e20cb5d898bdd085af4b2647b6614ae  0.000000  0.0  0.040926  0.0   
ebfc775bf31d66adab107f1d0cfc0ef2de8b6170  0.000000  0.0  0.040926  0.0   
01a4fca4c302ba60248c4d9fdc23aed44941c10c  0.000788  0.0  0.000000  0.0   
4c1e333d45aafb285712f0a1c384b93d119ae2e3  0.000000  0.0  0.000000  0.0   
f25f11d156e83f76afb6a871a1f61de3e00986a9  0.000000  0.0  0.000000  0.0   

                                                f5     f6   f7   f8        f9  \
3c1339e33e20cb5d898bdd085af4b2647b6614ae  0.025641  0.005  0.0  0.0  0.000000   
ebfc775bf31d66adab107f1d0cfc0ef2de8b6170  0.025641  0.005  0.0  0.0  0.000000   
01a4fca4c302ba60248c4d9fdc23aed44941c10c  0.000000  0.000  0.0  0.0  0.415947   
4c1e333d45aafb285712f0a1c384b93d119ae2e3  0.000000  0.000  0.0  0.0  0.000000   
f25f11d156e83f76afb6a871a1f61de3e00986a9  0.000000  0.000  0.0  0.0  0.000000   

                                               f10  f11  f12       f13  \
3c1339e33e20cb5d898bdd085af4b2647b6614ae  0.000000  0.0  0.0  0.000000   
ebfc775bf31d66adab107f1d0cfc0ef2de8b6170  0.000000  0.0  0.0  0.000000   
01a4fca4c302ba60248c4d9fdc23aed44941c10c  0.415947  0.0  0.0  0.212277   
4c1e333d45aafb285712f0a1c384b93d119ae2e3  0.000000  0.0  0.0  0.000000   
f25f11d156e83f76afb6a871a1f61de3e00986a9  0.000000  0.0  0.0  0.000000   

                                               f14  f15   f16       f17  \
3c1339e33e20cb5d898bdd085af4b2647b6614ae  0.000000  0.0   3.0  0.000138   
ebfc775bf31d66adab107f1d0cfc0ef2de8b6170  0.000000  3.0  35.0  0.000157   
01a4fca4c302ba60248c4d9fdc23aed44941c10c  0.212277  0.0   0.0  0.000000   
4c1e333d45aafb285712f0a1c384b93d119ae2e3  0.000000  0.0   0.0  0.000000   
f25f11d156e83f76afb6a871a1f61de3e00986a9  0.000000  4.0   1.0  0.000161   

                                               f18           f19  used_in_fix  
3c1339e33e20cb5d898bdd085af4b2647b6614ae  0.000000  2.785266e-05          0.0  
ebfc775bf31d66adab107f1d0cfc0ef2de8b6170  0.000249  9.452047e-04          0.0  
01a4fca4c302ba60248c4d9fdc23aed44941c10c  0.000000  0.000000e+00          0.0  
4c1e333d45aafb285712f0a1c384b93d119ae2e3  0.000000  0.000000e+00          0.0  
f25f11d156e83f76afb6a871a1f61de3e00986a9  0.000300  4.923481e-07          0.0

In [3]:
swt_normalized_training_fold_0=pd.read_pickle('/data/hdj/tracking_buggy_files/swt/swt_normalized_training_fold_0')

In [33]:
print(swt_normalized_training_fold_0.index.get_level_values(0).unique().shape[0])
print(swt_normalized_training_fold_0.index.get_level_values(1).unique().shape[0])
#虽然每个report都对应200+个文档，但是文档是有重复的，去重后的个数为7186个

500
7186


In [43]:
index=list(swt_normalized_training_fold_0.index.get_level_values(1).unique())

In [47]:
index=sorted(index)
index[:10],index[7180:]

([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], [7180, 7181, 7182, 7183, 7184, 7185])

In [36]:
max_level_0=500
max_level_1=7186
fold=0
#将第一维的索引从0开始重新索引
swt_normalized_training_fold_0.index.set_levels(range(fold * max_level_0, (fold + 1) * max_level_0), level=0, inplace=True)
# swt_normalized_training_fold_0.index.set_levels(range(fold * max_level_1, (fold + 1) * max_level_1), level=1, inplace=True)

In [38]:
swt_normalized_training_fold_0.tail()

f1        f2        f3  \
499 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.016591  0.037999  0.272661   
    3e4cac7453e1315a26c8542e13899a688fc7d265  0.018465  0.037999  0.272661   
    e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.021243  0.037098  0.000000   
    dc52a6a4701375236460a7e752eaebfe1f363e0e  0.065562  0.037098  0.000000   
    a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.019104  0.034676  0.000000   

                                               f4        f5     f6   f7   f8  \
499 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.0  0.142857  0.025  0.0  0.0   
    3e4cac7453e1315a26c8542e13899a688fc7d265  0.0  0.142857  0.025  0.0  0.0   
    e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.0  0.000000  0.000  0.0  0.0   
    dc52a6a4701375236460a7e752eaebfe1f363e0e  0.0  0.000000  0.000  0.0  0.0   
    a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.0  0.000000  0.000  0.0  0.0   

                                               f9  f10       f11       f12  \
499 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.0  0.0  0.235599  0.005200   
    3e4cac7453e1315a26c8542e13899a688fc7d265  0.0  0.0  0.235599  0.005200   
    e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.0  0.0  0.152437  0.002281   
    dc52a6a4701375236460a7e752eaebfe1f363e0e  0.0  0.0  0.219169  0.095327   
    a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.0  0.0  0.141786  0.027632   

                                                   f13       f14       f15  \
499 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.011659  0.089488  0.004310   
    3e4cac7453e1315a26c8542e13899a688fc7d265  0.006148  0.089488  0.004310   
    e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.050641  0.089488  0.000000   
    dc52a6a4701375236460a7e752eaebfe1f363e0e  0.000691  0.089488  0.021552   
    a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.010049  0.089488  0.034483   

                                                   f16       f17       f18  \
499 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.093458  0.017198  0.002109   
    3e4cac7453e1315a26c8542e13899a688fc7d265  0.093458  0.017198  0.002109   
    e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.046729  0.016424  0.000000   
    dc52a6a4701375236460a7e752eaebfe1f363e0e  0.042056  0.020406  0.007911   
    a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.046729  0.045398  0.008755   

                                                   f19  used_in_fix  
499 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.161792          0.0  
    3e4cac7453e1315a26c8542e13899a688fc7d265  0.161792          0.0  
    e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.065427          0.0  
    dc52a6a4701375236460a7e752eaebfe1f363e0e  0.007665          0.0  
    a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.110790          0.0

In [41]:
swt_normalized_training_fold_0.tail()

f1        f2        f3   f4        f5     f6   f7   f8   f9  \
499 6190  0.016591  0.037999  0.272661  0.0  0.142857  0.025  0.0  0.0  0.0   
    1725  0.018465  0.037999  0.272661  0.0  0.142857  0.025  0.0  0.0  0.0   
    6541  0.021243  0.037098  0.000000  0.0  0.000000  0.000  0.0  0.0  0.0   
    6181  0.065562  0.037098  0.000000  0.0  0.000000  0.000  0.0  0.0  0.0   
    4555  0.019104  0.034676  0.000000  0.0  0.000000  0.000  0.0  0.0  0.0   

          f10       f11       f12       f13       f14       f15       f16  \
499 6190  0.0  0.235599  0.005200  0.011659  0.089488  0.004310  0.093458   
    1725  0.0  0.235599  0.005200  0.006148  0.089488  0.004310  0.093458   
    6541  0.0  0.152437  0.002281  0.050641  0.089488  0.000000  0.046729   
    6181  0.0  0.219169  0.095327  0.000691  0.089488  0.021552  0.042056   
    4555  0.0  0.141786  0.027632  0.010049  0.089488  0.034483  0.046729   

               f17       f18       f19  used_in_fix  
499 6190  0.017198  0.002109  0.161792          0.0  
    1725  0.017198  0.002109  0.161792          0.0  
    6541  0.016424  0.000000  0.065427          0.0  
    6181  0.020406  0.007911  0.007665          0.0  
    4555  0.045398  0.008755  0.110790          0.0

In [39]:
swt_normalized_training_fold_0.index.set_levels(range(fold * max_level_1, (fold + 1) * max_level_1), level=1, inplace=True)

In [35]:
swt_normalized_training_fold_0.loc['1839d9b'].shape

(201, 20)

In [34]:
print(swt_normalized_training_fold_0.shape)
swt_normalized_training_fold_0.head()

(100819, 20)


f1        f2   f3  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.406456  0.129748  0.0   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.109654  0.157129  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.070893  0.152813  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.070893  0.152813  0.0   
        265eaac47f32827e3d4fd93150f58ad723630743  0.115202  0.152813  0.0   

                                                   f4   f5   f6   f7  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.0  0.0  0.0  0.0   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.0  0.0  0.0  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.0  0.0  0.0  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.0  0.0  0.0  0.0   
        265eaac47f32827e3d4fd93150f58ad723630743  0.0  0.0  0.0  0.0   

                                                        f8        f9  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.476397  0.621264   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.000000  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.000000  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.000000  0.000000   
        265eaac47f32827e3d4fd93150f58ad723630743  0.179682  0.403532   

                                                       f10       f11  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.364697  0.149520   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.178768  0.022845   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.162364  0.054235   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.162364  0.054235   
        265eaac47f32827e3d4fd93150f58ad723630743  0.144059  0.054235   

                                                       f12       f13  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.337319  0.443883   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.097496  0.381096   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.020132  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.020132  0.000000   
        265eaac47f32827e3d4fd93150f58ad723630743  0.049521  0.315797   

                                                       f14       f15  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.409832  0.004310   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.323006  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.094988  0.077586   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.094988  0.077586   
        265eaac47f32827e3d4fd93150f58ad723630743  0.096047  0.077586   

                                                       f16       f17  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.140187  0.020093   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.285047  0.019490   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.210280  0.043195   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.210280  0.043195   
        265eaac47f32827e3d4fd93150f58ad723630743  0.210280  0.043195   

                                                       f18       f19  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.003372  0.246023   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.000000  0.059225   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.053756  0.276555   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.053756  0.276555   
        265eaac47f32827e3d4fd93150f58ad723630743  0.053756  0.276555   

                                                  used_in_fix  
1839d9b 8640d87eebe944043533a62885e33b04d5475d53          1.0  
        b69d15b681617992661eeb85524ee27b02ef6c9c          0.0  
        d93c35d2f683ad071fd31cb749e5496fa1dda022          0.0  
        d93c35d2f683ad071fd31cb749e5496fa1dda022          0.0  
        265eaac47f32827e3d4fd93150f58ad723630743          0.0

In [31]:
swt_normalized_training_fold_0[swt_normalized_training_fold_0['used_in_fix']==1].shape

(819, 20)

In [9]:
type(swt_normalized_training_fold_0.loc['1839d9b'])

pandas.core.frame.DataFrame

In [8]:
swt_normalized_training_fold_0.loc['b067e67']

f1        f2        f3   f4  \
94065bf02a63710434075209886f06f9464ed3a1  0.034385  0.041428  0.060631  0.0   
8d7063afbecfe86cb9ec5be3e059633a488a1c4f  0.089133  0.000000  0.053303  0.0   
f1094fad9d66d9e8307bb67af87e2ac260238990  0.035475  0.212376  0.000000  0.0   
c216cd61b9c395d354b896711e96615239552ecf  0.049634  0.207175  0.000000  0.0   
f58494b754424c8e3b42d7528ae9eb8d88993254  0.068303  0.203158  0.000000  0.0   
...                                            ...       ...       ...  ...   
dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.016591  0.037999  0.272661  0.0   
3e4cac7453e1315a26c8542e13899a688fc7d265  0.018465  0.037999  0.272661  0.0   
e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.021243  0.037098  0.000000  0.0   
dc52a6a4701375236460a7e752eaebfe1f363e0e  0.065562  0.037098  0.000000  0.0   
a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.019104  0.034676  0.000000  0.0   

                                                f5     f6   f7   f8        f9  \
94065bf02a63710434075209886f06f9464ed3a1  0.500000  0.075  0.0  0.0  0.000000   
8d7063afbecfe86cb9ec5be3e059633a488a1c4f  0.250000  0.075  0.0  0.0  0.175455   
f1094fad9d66d9e8307bb67af87e2ac260238990  0.000000  0.000  0.0  0.0  0.000000   
c216cd61b9c395d354b896711e96615239552ecf  0.000000  0.000  0.0  0.0  0.000000   
f58494b754424c8e3b42d7528ae9eb8d88993254  0.000000  0.000  0.0  0.0  0.000000   
...                                            ...    ...  ...  ...       ...   
dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.142857  0.025  0.0  0.0  0.000000   
3e4cac7453e1315a26c8542e13899a688fc7d265  0.142857  0.025  0.0  0.0  0.000000   
e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.000000  0.000  0.0  0.0  0.000000   
dc52a6a4701375236460a7e752eaebfe1f363e0e  0.000000  0.000  0.0  0.0  0.000000   
a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.000000  0.000  0.0  0.0  0.000000   

                                          f10       f11       f12       f13  \
94065bf02a63710434075209886f06f9464ed3a1  0.0  0.161413  0.040884  0.095571   
8d7063afbecfe86cb9ec5be3e059633a488a1c4f  0.0  0.391174  0.052716  0.049962   
f1094fad9d66d9e8307bb67af87e2ac260238990  0.0  0.110651  0.023517  0.095571   
c216cd61b9c395d354b896711e96615239552ecf  0.0  0.227797  0.039809  0.036894   
f58494b754424c8e3b42d7528ae9eb8d88993254  0.0  0.229254  0.005200  0.290873   
...                                       ...       ...       ...       ...   
dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.0  0.235599  0.005200  0.011659   
3e4cac7453e1315a26c8542e13899a688fc7d265  0.0  0.235599  0.005200  0.006148   
e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.0  0.152437  0.002281  0.050641   
dc52a6a4701375236460a7e752eaebfe1f363e0e  0.0  0.219169  0.095327  0.000691   
a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.0  0.141786  0.027632  0.010049   

                                               f14       f15       f16  \
94065bf02a63710434075209886f06f9464ed3a1  0.099579  0.004310  0.224299   
8d7063afbecfe86cb9ec5be3e059633a488a1c4f  0.089488  0.025862  0.135514   
f1094fad9d66d9e8307bb67af87e2ac260238990  0.089488  0.004310  0.247664   
c216cd61b9c395d354b896711e96615239552ecf  0.089488  0.000000  0.182243   
f58494b754424c8e3b42d7528ae9eb8d88993254  0.089488  0.008621  0.088785   
...                                            ...       ...       ...   
dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.089488  0.004310  0.093458   
3e4cac7453e1315a26c8542e13899a688fc7d265  0.089488  0.004310  0.093458   
e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.089488  0.000000  0.046729   
dc52a6a4701375236460a7e752eaebfe1f363e0e  0.089488  0.021552  0.042056   
a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.089488  0.034483  0.046729   

                                               f17       f18       f19  \
94065bf02a63710434075209886f06f9464ed3a1  0.016738  0.002789  0.213973   
8d7063afbecfe86cb9ec5be3e059633a488a1c4f  0.050480  0.000614  0.009573   
f1094fad9d66d9e8307bb67af87e2ac260238990  0.016708  0.002519  0.19

In [6]:
swt_normalized_training_fold_0.shape
swt_normalized_training_fold_0[swt_normalized_training_fold_0['used_in_fix']==1]
swt_normalized_training_fold_0.head(10)

f1        f2   f3  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.406456  0.129748  0.0   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.109654  0.157129  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.070893  0.152813  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.070893  0.152813  0.0   
        265eaac47f32827e3d4fd93150f58ad723630743  0.115202  0.152813  0.0   
        8554847dfac7efb89bc06c22426137213060f78d  0.068573  0.152813  0.0   
        46067ede780f2fd822736501f6acb343278a5cce  0.115202  0.152813  0.0   
        d6f26064d6f489ae6e1a681139e58eb7223837a0  0.033993  0.140270  0.0   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.097265  0.129043  0.0   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.097265  0.129043  0.0   

                                                   f4   f5   f6   f7  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.0  0.0  0.0  0.0   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.0  0.0  0.0  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.0  0.0  0.0  0.0   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.0  0.0  0.0  0.0   
        265eaac47f32827e3d4fd93150f58ad723630743  0.0  0.0  0.0  0.0   
        8554847dfac7efb89bc06c22426137213060f78d  0.0  0.0  0.0  0.0   
        46067ede780f2fd822736501f6acb343278a5cce  0.0  0.0  0.0  0.0   
        d6f26064d6f489ae6e1a681139e58eb7223837a0  0.0  0.0  0.0  0.0   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.0  0.0  0.0  0.0   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.0  0.0  0.0  0.0   

                                                        f8        f9  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.476397  0.621264   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.000000  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.000000  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.000000  0.000000   
        265eaac47f32827e3d4fd93150f58ad723630743  0.179682  0.403532   
        8554847dfac7efb89bc06c22426137213060f78d  0.000000  0.000000   
        46067ede780f2fd822736501f6acb343278a5cce  0.548469  0.403532   
        d6f26064d6f489ae6e1a681139e58eb7223837a0  0.000000  0.000000   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.000000  0.000000   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.000000  0.000000   

                                                       f10       f11  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.364697  0.149520   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.178768  0.022845   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.162364  0.054235   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.162364  0.054235   
        265eaac47f32827e3d4fd93150f58ad723630743  0.144059  0.054235   
        8554847dfac7efb89bc06c22426137213060f78d  0.243481  0.054235   
        46067ede780f2fd822736501f6acb343278a5cce  0.271378  0.054235   
        d6f26064d6f489ae6e1a681139e58eb7223837a0  0.000000  0.025092   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.000000  0.149520   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.000000  0.149520   

                                                       f12       f13  \
1839d9b 8640d87eebe944043533a62885e33b04d5475d53  0.337319  0.443883   
        b69d15b681617992661eeb85524ee27b02ef6c9c  0.097496  0.381096   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.020132  0.000000   
        d93c35d2f683ad071fd31cb749e5496fa1dda022  0.020132  0.000000   
        265eaac47f32827e3d4fd93150f58ad723630743  0.049521  0.315797   
        8554847dfac7efb89bc06c22426137213060f78d  0.020132  0.038715   
        46067ede780f2fd822736501f6acb343278a5cce  0.074819  0.106346   
        d6f26064d6f489ae6e1a681139e58eb7223837a0  0.097496  0.000000   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.081217  0.121495   
        04cf611eaada6f2a06a0af197cb4146c4ab6e4b4  0.081217  0.121495   

                                    

In [7]:
swt_normalized_training_fold_0.tail()

f1        f2  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.016591  0.037999   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.018465  0.037999   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.021243  0.037098   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.065562  0.037098   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.019104  0.034676   

                                                        f3   f4        f5  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.272661  0.0  0.142857   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.272661  0.0  0.142857   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.000000  0.0  0.000000   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.000000  0.0  0.000000   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.000000  0.0  0.000000   

                                                     f6   f7   f8   f9  f10  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.025  0.0  0.0  0.0  0.0   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.025  0.0  0.0  0.0  0.0   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.000  0.0  0.0  0.0  0.0   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.000  0.0  0.0  0.0  0.0   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.000  0.0  0.0  0.0  0.0   

                                                       f11       f12  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.235599  0.005200   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.235599  0.005200   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.152437  0.002281   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.219169  0.095327   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.141786  0.027632   

                                                       f13       f14  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.011659  0.089488   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.006148  0.089488   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.050641  0.089488   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.000691  0.089488   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.010049  0.089488   

                                                       f15       f16  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.004310  0.093458   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.004310  0.093458   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.000000  0.046729   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.021552  0.042056   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.034483  0.046729   

                                                       f17       f18  \
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.017198  0.002109   
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.017198  0.002109   
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.016424  0.000000   
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.020406  0.007911   
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.045398  0.008755   

                                                       f19  used_in_fix  
b067e67 dcb5e1189cf30f98c28e3f7e02f3bd61f286ce5d  0.161792          0.0  
        3e4cac7453e1315a26c8542e13899a688fc7d265  0.161792          0.0  
        e8d3e3a67e2b54cef78b5348755252586d51bfaa  0.065427          0.0  
        dc52a6a4701375236460a7e752eaebfe1f363e0e  0.007665          0.0  
        a1ed589a9f443d1ce5cb0abbb25aa06d42d0c1a4  0.110790          0.0

In [112]:
df[df['used_in_fix']==1]

f1   f2        f3   f4   f5  \
e4149970c957900a7a1c807ed6cc28d4f35cc5d7  0.190565  0.0  0.385557  0.0  1.0   

                                            f6        f7        f8        f9  \
e4149970c957900a7a1c807ed6cc28d4f35cc5d7  0.03  0.456333  0.616549  0.105104   

                                               f10       f11       f12  \
e4149970c957900a7a1c807ed6cc28d4f35cc5d7  0.173948  0.252043  0.340534   

                                               f13       f14  f15   f16  \
e4149970c957900a7a1c807ed6cc28d4f35cc5d7  0.116102  0.192151  0.0  66.0   

                                               f17  f18      f19  used_in_fix  
e4149970c957900a7a1c807ed6cc28d4f35cc5d7  0.000138  0.0  0.00115          1.0

# 检查save_normalized_fold_dataframes.py结束

In [14]:
src_addresses = glob.glob(str('/data/hdj/tracking_buggy_files/swt') + '/**/*.npz', recursive=True)

In [22]:
len(src_addresses),len(size)
size1=[v[0] for v in size]

In [27]:
max(size1),min(size1),sum(size1),len(src_addresses),sum(size1)/len(src_addresses)

(2795, 1037, 8405016, 4151, 2024.817152493375)

In [23]:
# raw_count_data.toarray()

In [30]:
size=[]
for file in src_addresses:
    raw_count_data = sparse.load_npz(file)
    print(raw_count_data.shape)
    size.append(raw_count_data.shape)
    break

In [16]:

data_filename_memmap='/data/hdj/tracking_buggy_files/joblib_memmap_tomcat/tomcat/data_memmap'
fold_number, fold_testing, fold_training = load(data_filename_memmap, mmap_mode="r")

In [23]:
fold_number,type(fold_testing),type(fold_training)

(2, dict, dict)

In [22]:
# for i,(key ,val) in enumerate(fold_training.items()):
#     if i<=1:
# #         break
#         continue
#     print(key)
#     print(type(val),val.shape)
#     print(val)

In [21]:
# for i,(key ,val) in enumerate(fold_testing.items()):
#     if i<=1:
# #         break
#         continue
#     print(key)
#     print(type(val),val.shape)
#     print(val)

In [8]:
print(cp.get_corpus()['2'])

['extract', 'of', 'root', 'by', 'repeat', 'subtract', 'for', 'digit', 'comput', 'cacm', 'decemb', '1958', 'sugai', 'i', 'ca581202', 'jb', 'march', '22', '1978', '8', '29', 'pm', '2', '5', '2', '2', '5', '2', '2', '5', '2']


In [9]:
corpus=cp.get_corpus()

In [14]:
for i,(key,val) in enumerate(corpus.items()):
    print(key,val)
    if i==2:
        break

1 ['preliminari', 'report', 'intern', 'algebra', 'languag', 'cacm', 'decemb', '1958', 'perli', 'a', 'j', 'samelson', 'k', 'ca581203', 'jb', 'march', '22', '1978', '8', '28', 'pm', '100', '5', '1', '123', '5', '1', '164', '5', '1', '1', '5', '1', '1', '5', '1', '1', '5', '1', '205', '5', '1', '210', '5', '1', '214', '5', '1', '1982', '5', '1', '398', '5', '1', '642', '5', '1', '669', '5', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '1', '6', '1', '165', '6', '1', '196', '6', '1', '196', '6', '1', '1273', '6', '1', '1883', '6', '1', '324', '6', '1', '43', '6', '1', '53', '6', '1', '91', '6', '1', '410', '6', '1', '3184', '6', '1']
2 ['extract', 'of', 'root', 'by', 'repeat', 'subtract', 'for', 'digit', 'comput', 'cacm', 'decemb', '1958', 'sugai', 'i', 'ca581202', 'jb', 'march', '22', '1978', '8', '29', 'pm', '2', '5', '2', '2', '5', '2', '2', '5', '2']
3 ['techniqu', 'depart', 'on', 'matrix', '

In [1]:
#将数据组织成dict格式
#query {bug_id:{'summary':string,'description':string,'fixed_files':string}}
#code {code_path:string}
query=dict()

with open('/data/hdj/SourceFile/data/sourceFile_aspectj/bugreport.txt','r',encoding='utf-8') as f_in:
    for i, line in enumerate(f_in) :
        if i==0:
            continue
#         print(line.strip().split('\t'))
        contents=line.strip().split('\t')
        bug_id=contents[1]
        summary=contents[2]
        description=contents[3]
        #处理files，添加commit
        fixed_list=[]
        for file_path in contents[9].split(' '):
            if ':' in file_path:
                continue
#             str_list=file_path.split('/')
#             str_list[-1]=contents[7]+' '+str_list[-1]
# #             print(str_list)
#             new_string='/'.join(str_list)
#             fixed_list.append(new_string)
            fixed_list.append(file_path)
        query[bug_id]={'summary':summary,'description':description,'fixed_files':fixed_list}
#         print(query)
#         break

In [3]:
# query

In [4]:
def _split_camelcase(tokens):

    # Copy tokens
    returning_tokens = tokens[:]
    for token in tokens:
        split_tokens = re.split(fr'[{string.punctuation}]+', token)
        # If token is split into some other tokens
        if len(split_tokens) > 1:
            returning_tokens.remove(token)
            # Camel case detection for new tokens
            for st in split_tokens:
                camel_split = inflection.underscore(st).split('_')
                if len(camel_split) > 1:
                    returning_tokens.append(st)
                    returning_tokens += camel_split
                else:
                    returning_tokens.append(st)
        else:
            camel_split = inflection.underscore(token).split('_')
            if len(camel_split) > 1:
                returning_tokens += camel_split

    return returning_tokens

In [30]:
split_tokens = re.split(fr'[{string.punctuation}]+', 'java.lang.VerifyError')

In [31]:
split_tokens

['java', 'lang', 'VerifyError']

In [24]:
# query['251326']

In [7]:
#准备code
aspectj_test=pd.read_csv('/data/hdj/SourceFile/data/sourceFile_aspectj/aspectj_test_pos_neg.csv')
aspectj_test.head()

id                                               path  label
0  251326  tests/bugs163/pr251326/pkgA/f1a83b5 Listener.java      1
1  251326    tests/bugs163/pr251326/pkgA/f1a83b5 Target.java      1
2  251326  tests/src/org/aspectj/systemtest/ajc163/f1a83b...      1
3  251326  weaver/src/org/aspectj/weaver/patterns/936459c...      0
4  251326  ajde/src/org/aspectj/ajde/ui/f1deb9c Structure...      0

In [28]:
#queries准备完成
queries=[]
bugid_set=set()
for bug_id in aspectj_test['id'].values:
#     print(key,val)
    if bug_id in bugid_set:
        continue
#     if bug_id==256400:
    bugid_set.add(bug_id)
    summary=query[str(bug_id)]['summary']
    summary_list=_split_camelcase(nltk.wordpunct_tokenize(summary))
    summary_list = [x for x in summary_list if x != '']
    queries.append(summary_list)

#         break
# print(queries[:2])
# print(queries)

In [37]:
len(queries)

119

In [9]:
aspectj_root_path='/data/hdj/SourceFile/tracking_buggy_files_aspectj_dataset/'
# path_set=set()
# for path in aspectj_test['path'].values:
#     path_set.add(path)

In [2]:
def code_pre(outstring):
    #主要目的是去除所有的注释 ，import， 替换回车换行符 ，过滤掉词长度小于3，最终返回数据格式是list
    m = re.compile(r'/\*.*?\*/', re.S)
    outtmp = re.sub(m, '', outstring)
    outstring = outtmp
    m = re.compile(r'//.*')
    outtmp = re.sub(m, '', outstring)
    outstring = outtmp
    m=re.compile(r'import.*')
    outtmp=re.sub(m,'',outstring)
    outstring = outtmp
    m = re.compile(r'package.*')
    outtmp = re.sub(m, '', outstring)
    outstring = outtmp
    m = re.compile(r'#.*')
    outtmp = re.sub(m, ' ', outstring)
    outstring = outtmp
    for char in ['\r\n', '\r', '\n']:
        outstring = outstring.replace(char, ' ')
    list_str=outstring.split()
    list_str=[t for t in list_str if len(t)>=3]
    # outstring = ' '.join(list_str)
    return list_str

In [11]:
src_addresses = glob.glob(str('/data/hdj/SourceFile/tracking_buggy_files_aspectj_dataset') + '/**/*.java', recursive=True)
len(src_addresses)


7067

In [13]:
reg='/data/hdj/SourceFile/tracking_buggy_files_aspectj_dataset/'
'/data/hdj/SourceFile/tracking_buggy_files_aspectj_dataset/weaver/testsrc/org/aspectj/weaver/CommonsTraceTest.java'.split(reg)

['', 'weaver/testsrc/org/aspectj/weaver/CommonsTraceTest.java']

In [29]:
path_set=set()
reg='/data/hdj/SourceFile/tracking_buggy_files_aspectj_dataset/'
for path in src_addresses:
    path_set.add(path.split(reg)[1])
#     src_addresses[:10]

In [22]:
# len(path_set.)
# 'asm/src/org/aspectj/asm/internal/JDTLikeHandleProvider.java' in path_set
path_filter=[]
for i,path in enumerate(path_set):
    path_filter.append(path)
    if i==1000:
        break

In [32]:
len(path_set)
# 'asm/src/org/aspectj/asm/internal/JDTLikeHandleProvider.java' in path_filter

7067

In [33]:
# len(path_set)
# path_set=aspectj_test_pos_neg['path'][1000:1000+1000]

# path_set
corpus=dict()
for path in path_set:
#     print(path)
    code_path=aspectj_root_path+path
    rf = open(code_path, 'r', encoding='utf-8', errors='ignore')
    data = rf.read()
    code = ' '.join(code_pre(data))
#     print(code)
    code_list=_split_camelcase(nltk.wordpunct_tokenize(code))
    code_list = [x for x in code_list if x != '']
#     print(code_list)
    corpus[path]=code_list
#     break

In [36]:
len(corpus),type(corpus)

(7067, dict)

In [82]:
# for i,(key,val) in enumerate(corpus.items()):
# #     if i==10:
# #         break
#     print(key)

In [83]:
import pickle
with open('/data/hdj/SourceFile/data/sourceFile_eclipseUI/corpus.pickle', 'wb') as file:
        pickle.dump(corpus, file, protocol=pickle.HIGHEST_PROTOCOL)

In [35]:
with open('/data/hdj/SourceFile/data/sourceFile_eclipseUI/querys.pickle', 'wb') as file:
        pickle.dump(queries, file, protocol=pickle.HIGHEST_PROTOCOL)

In [59]:
token=['Bug', '423257', 'LTW', 'java', 'lang', 'VerifyError', 'Bad', 'return', 'type', 'with', 'generics', 'and', 'local', 'variables', '', '', '', '', '', 'verify', 'error', '', '']
token.remove('')

# 检查指标的计算过程，最终找出前50个文件，获得bid fid 与db之间关系

In [153]:
import pickle
project='eclipse'
# all_results_df_after=pickle.load(open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/all_results_df_after.pickle', 'rb'))
all_results_df_before=pickle.load(open('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/all_results_df_before.pickle', 'rb'))

In [175]:
# print(all_results_df_before.index.s)
all_ast_index=list(all_results_df_before.index.get_level_values(0).unique())
len(all_ast_index)

5940

In [176]:
5940*0.8,5940*0.2

(4752.0, 1188.0)

In [167]:
# all_results_df_before.loc['7efd5bf']

# 生成训练数据 pos vs neg

In [177]:
#
import pandas as pd
from collections import defaultdict
k=10
fold=4752
train_fold = defaultdict(list)
for i,(bug_report, bug_report_files_dataframe)  in enumerate(all_results_df_before.groupby(level=0, sort=False)):
    print(i)
    sorted_df = bug_report_files_dataframe.sort_values(ascending=False, by=['result'])
#     print(sorted_df)
    used_in_fix=sorted_df[sorted_df['used_in_fix']==1.0]
    not_used_in_fix=sorted_df[sorted_df['used_in_fix']==0.0]
#     print(used_in_fix)
    used_in_fix_k=used_in_fix.shape[0]
#     not_used_in_fix_k=k-used_in_fix_k
    not_used_in_fix_k=used_in_fix_k
#     if not_used_in_fix_k<=0:
#         not_used_in_fix_k=used_in_fix_k
#     print(used_in_fix.shape)
    if used_in_fix.shape[0]==0:
        continue
    train=pd.concat([used_in_fix,not_used_in_fix[:not_used_in_fix_k*2]])
#     print(train.shape)
#     train_fold[i//3500].append(train)
    train_fold[i//4752].append(train)
#     print(len(train_fold[i//500]))
#     if i==2:
#         break

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095


3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756
3757
3758
3759
3760
3761
3762
3763
3764
3765
3766
3767
3768
3769
3770
3771
3772
3773
3774
3775
3776
3777
3778
3779
3780
3781
3782
3783
3784
3785
3786
3787
3788
3789
3790


5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349
5350
5351
5352
5353
5354
5355
5356
5357
5358
5359
5360
5361
5362
5363
5364
5365
5366
5367
5368
5369
5370
5371
5372
5373
5374
5375
5376
5377
5378
5379
5380
5381
5382
5383
5384
5385
5386
5387
5388
5389
5390
5391
5392
5393
5394
5395
5396
5397
5398
5399
5400
5401
5402
5403
5404
5405
5406
5407
5408
5409
5410
5411
5412
5413
5414
5415
5416
5417
5418
5419
5420
5421
5422
5423
5424
5425
5426
5427
5428
5429
5430
5431
5432
5433
5434
5435
5436
5437
5438
5439
5440
5441
5442
5443
5444
5445
5446
5447
5448
5449
5450
5451
5452
5453
5454
5455
5456
5457
5458
5459
5460


In [173]:
len(train_fold),len(train_fold[0])

(1, 5940)

In [178]:
print(len(train_fold))
for key,val in train_fold.items():
    print(key,len(val))
    data=pd.concat(train_fold[key])
    data.to_csv('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_'+str(key+1)+'.csv',index=True)

2
0 4752
1 1188


In [179]:
#分割成train val集
train_1=pd.read_csv('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1.csv')
train_len=int(train_1.shape[0]*0.9)
val_len=train_1.shape[0]-train_len
train=train_1.head(train_len)
val=train_1.tail(val_len)
train.shape,val.shape,train.shape[0]+val.shape[0],train_1.shape[0]
train.to_csv('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1_train.csv')
val.to_csv('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1_val.csv')

In [181]:
train_1=pd.read_csv('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1.csv')
print(train_1['used_in_fix'].sum()/train_1.shape[0])
train_1.head(10)

0.3333333333333333


bid                                       fid  used_in_fix        f1  \
0  7efd5bf  0b29d74ed59f8d0d492e994967430632b295d10e          1.0  0.823629   
1  7efd5bf  9bf12a372b2c5bad5a3eb44305c8612c437de1e5          0.0  0.488563   
2  7efd5bf  2d34364f931430cc1d85ea88b234686d56b9ff2b          0.0  0.434284   
3  a431c62  58abea562f92d3a37269efb04a0a9c08acfd9da5          1.0  0.514475   
4  a431c62  8815221697d7cc3eb503e24b6672e6e70b2cd50d          0.0  0.184717   
5  a431c62  160f729dece568731a1aa010fae846c5dbd36962          0.0  0.423033   
6  abdda26  a6d3fbbfd8cee11f3d49a7ad4fceefc9f2bf8a4f          1.0  0.672715   
7  abdda26  a7d75f1a43116d704418be6b1bd5f4a7f7e509c6          0.0  0.382862   
8  abdda26  b041dc69f08a5f49a6fb05000e81d8acac5f058c          0.0  0.545671   
9  09ab34d  0cd492fedc97e4c346bdb48c3944c7425c0dde8e          1.0  0.653061   

     result  
0  1.333432  
1  1.041635  
2  1.003380  
3  1.072069  
4  0.993735  
5  0.990413  
6  0.991804  
7  1.084254  
8  1.064085  
9  1.114656

In [182]:
print(train_1['used_in_fix'].sum()/train_1.shape[0],train_1['used_in_fix'].sum(),train_1.shape[0])
print(train['used_in_fix'].sum()/train.shape[0],train['used_in_fix'].sum(),train.shape[0])
print(val['used_in_fix'].sum()/val.shape[0],val['used_in_fix'].sum(),val.shape[0])

0.3333333333333333 12055.0 36165
0.3334152636106673 10852.0 32548
0.3325960740945535 1203.0 3617


# 生成训练数据 pos vs neg 1:3结束

# 生成top-50测试数据

In [183]:
#
import pandas as pd
from collections import defaultdict
k=50
import pickle
fold=4752
# all_results_df_after=pickle.load(open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/all_results_df_after.pickle', 'rb'))
all_results_df_before=pickle.load(open('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/all_results_df_before.pickle', 'rb'))
train_fold = defaultdict(list)
for i,(bug_report, bug_report_files_dataframe)  in enumerate(all_results_df_before.groupby(level=0, sort=False)):
    sorted_df = bug_report_files_dataframe.sort_values(ascending=False, by=['result'])
    #生成简单的测试集
    used_in_fix=sorted_df[sorted_df['used_in_fix']==1.0]
    if used_in_fix.shape[0]==0:
        print('没有label=1 的数据')
        continue
        
#     not_used_in_fix=sorted_df[sorted_df['used_in_fix']==0.0]
    
#     not_used_in_fix_k_easy=(k-used_in_fix.shape[0])//2
#     not_used_in_fix_k_hard=k-not_used_in_fix_k_easy-used_in_fix.shape[0]
#     train=pd.concat([used_in_fix,not_used_in_fix[:not_used_in_fix_k_hard],not_used_in_fix[-not_used_in_fix_k_easy:]])
# #     if not_used_in_fix_k<0:
# #         train=used_in_fix[:k]
#     if train.shape[0]!=50:
#         print('train shape :',train.shape,used_in_fix.shape,not_used_in_fix.shape,not_used_in_fix_k_easy,not_used_in_fix_k_hard)
#         train=sorted_df[:50]
#     train_fold[i//3500].append(train)
    train=sorted_df[:k]
    train_fold[i//fold].append(train)
    print(len(train_fold[i//fold]))
#     if i==2:
#         break
print(len(train_fold))
for key,val in train_fold.items():
    print(key,len(val))
    data=pd.concat(train_fold[key])
    data.to_csv('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/test_2hard_'+str(key+1)+'.csv',index=True)
    #data.to_csv('/data/hdj/tracking_buggy_files/joblib_memmap_swt/test_easy_'+str(key+1)+'.csv',index=True)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097
2098
2099
2100
2101
2102
2103
2104
2105
2106
2107
2108
2109
2110
2111
2112
2113
2114
2115
2116
2117
2118
2119
2120
2121
2122
2123
2124
2125
2126
2127
2128
2129
2130
2131
2132
2133
2134
2135
2136
2137
2138
2139
2140
2141
2142
2143
2144
2145
2146
2147
2148
2149
2150
2151
2152
2153
2154
2155
2156
2157
2158
2159
2160
2161
2162
2163
2164
2165
2166
2167
2168
2169
2170
2171
2172
2173
2174
2175
2176
2177


3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756
3757
3758
3759
3760
3761
3762
3763
3764
3765
3766
3767
3768
3769
3770
3771
3772
3773
3774
3775
3776
3777
3778
3779
3780
3781
3782
3783
3784
3785
3786
3787
3788
3789
3790
3791
3792
3793
3794
3795
3796
3797
3798
3799
3800
3801
3802
3803
3804
3805
3806
3807
3808
3809
3810
3811
3812
3813
3814
3815
3816
3817
3818
3819
3820
3821
3822
3823
3824
3825
3826
3827
3828
3829
3830
3831
3832
3833
3834
3835
3836
3837
3838
3839
3840
3841
3842
3843
3844
3845
3846
3847
3848
3849
3850
3851
3852
3853
3854
3855
3856
3857
3858
3859
3860
3861
3862
3863
3864
3865
3866
3867
3868
3869
3870
3871
3872
3873
3874
3875
3876
3877
3878
3879
3880
3881
3882
3883
3884
3885
3886
3887
3888
3889
3890
3891
3892
3893
3894
3895
3896
3897
3898
3899
3900
3901
3902
3903
3904
3905
3906
3907
3908
3909
3910
3911
3912
3913
3914
3915
3916
3917
3918
3919
3920
3921
3922
3923
3924
3925
3926
3927
3928


827
828
829
830
831
832
833
834
835
836
837
838
839
840
841
842
843
844
845
846
847
848
849
850
851
852
853
854
855
856
857
858
859
860
861
862
863
864
865
866
867
868
869
870
871
872
873
874
875
876
877
878
879
880
881
882
883
884
885
886
887
888
889
890
891
892
893
894
895
896
897
898
899
900
901
902
903
904
905
906
907
908
909
910
911
912
913
914
915
916
917
918
919
920
921
922
923
924
925
926
927
928
929
930
931
932
933
934
935
936
937
938
939
940
941
942
943
944
945
946
947
948
949
950
951
952
953
954
955
956
957
958
959
960
961
962
963
964
965
966
967
968
969
970
971
972
973
974
975
976
977
978
979
980
981
982
983
984
985
986
987
988
989
990
991
992
993
994
995
996
997
998
999
1000
1001
1002
1003
1004
1005
1006
1007
1008
1009
1010
1011
1012
1013
1014
1015
1016
1017
1018
1019
1020
1021
1022
1023
1024
1025
1026
1027
1028
1029
1030
1031
1032
1033
1034
1035
1036
1037
1038
1039
1040
1041
1042
1043
1044
1045
1046
1047
1048
1049
1050
1051
1052
1053
1054
1055
1056
1057
1058
1059
1060
106

In [184]:
# #最后平均得分 top10rank, MRRrank, MAPrank : 0.212 0.08386737159603685 0.08130901352903222 用的tracking数据预训练的模型
# #最后平均得分 top10rank, MRRrank, MAPrank : 0.308 0.10942885958858604 0.09805982264520696 用的之前预训练保存的模型
# #最后平均得分 top10rank, MRRrank, MAPrank : 0.342 0.14929821137611463 0.1260024167896456
# with open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/0521_sumDes_tokSour_50_rawmodel.txt','r',encoding='utf-8') as f_in:
#     for i,line in enumerate(f_in):
# #         print(line)
#         contents=line.split('<CODESPLIT>')
#         print(contents[0],contents[1],contents[5],contents[6])
#         if i==5:
#             break

# 生成top-50测试数据结束

# 计算前k个的recall，将前k个文件保存起来开始

In [185]:
sum_val=0
average_precision_per_bug_report = []
reciprocal_ranks = []
k_range=range(1, 21)
bug_report_number = 0
accuracy_at_k = dict.fromkeys(k_range, 0)
top_k_list=[]
all_pos_list=[]
recall_list=[]
all_results_df_top_k=[]
k=50
left_len=[]
for i,(bug_report, bug_report_files_dataframe)  in enumerate(all_results_df_before.groupby(level=0, sort=False)):
    print('index :',i,bug_report,bug_report_files_dataframe.shape[0])
    sum_val+=bug_report_files_dataframe.shape[0]
#     print(bug_report_files_dataframe)
#     min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
#     bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
#     print('取fix得分最小值之前的所有文件 ',bug_report_files_dataframe2.shape,' 过滤前大小 :',bug_report_files_dataframe.shape,
#           ' min_fix_result :',min_fix_result)
#     sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
    sorted_df = bug_report_files_dataframe.sort_values(ascending=False, by=['result'])
    #假如过滤后没有值，直接用原始的dataframe
    if sorted_df.shape[0] == 0:
        sorted_df = bug_report_files_dataframe.copy().sort_values(ascending=False, by=['result'])
#     print(sorted_df)
    top_k=sorted_df[:k]
    top_k_pos=top_k['used_in_fix'].sum()
    all_pos=sorted_df['used_in_fix'].sum()
    recall=top_k_pos/all_pos
    print('top_k :',top_k_pos,' all :',all_pos,' recall :',recall)
    top_k_list.append(top_k_pos)
    all_pos_list.append(all_pos)
    recall_list.append(recall)
    all_results_df_top_k.append(top_k)
    left_len.append(top_k.shape[0])
#     if i==10:
#         break
sum(recall_list)/len(recall_list),len(recall_list)
#10 (0.6132802407120562, 3645)
#20 (0.7098751551130549, 3645)
#30 (0.7619124531045822, 3645)
#50 (0.8176689635982688, 3645)
#60 (0.8375844719269108, 3645)
#70 (0.8500262484623857, 3645)
#80 (0.8607365838268616, 3645)
#90 (0.8704146788592242, 3645)
#100 (0.8796385848682644, 3645
#150 (0.9100992868124254, 3645)
#200 (0.9261051897470557, 3645)
#300 (0.9458304773765746, 3645)

index : 0 7efd5bf 1159
top_k : 1.0  all : 1.0  recall : 1.0
index : 1 a431c62 1345
top_k : 1.0  all : 1.0  recall : 1.0
index : 2 abdda26 1276
top_k : 1.0  all : 1.0  recall : 1.0
index : 3 09ab34d 1228
top_k : 3.0  all : 3.0  recall : 1.0
index : 4 68b5ac3 1356
top_k : 1.0  all : 1.0  recall : 1.0
index : 5 3c1e96c 1062
top_k : 1.0  all : 1.0  recall : 1.0
index : 6 3e760ad 1142
top_k : 1.0  all : 1.0  recall : 1.0
index : 7 cad3665 871
top_k : 1.0  all : 1.0  recall : 1.0
index : 8 3927ef7 1044
top_k : 2.0  all : 6.0  recall : 0.3333333333333333
index : 9 9ddba76 1150
top_k : 1.0  all : 1.0  recall : 1.0
index : 10 e9fc99c 1005
top_k : 1.0  all : 1.0  recall : 1.0
index : 11 4b2738f 1175
top_k : 1.0  all : 1.0  recall : 1.0
index : 12 165fc85 1010
top_k : 1.0  all : 2.0  recall : 0.5
index : 13 391d669 1164
top_k : 1.0  all : 1.0  recall : 1.0
index : 14 79ddf03 1060
top_k : 1.0  all : 1.0  recall : 1.0
index : 15 bd25eaf 893
top_k : 0.0  all : 3.0  recall : 0.0
index : 16 33635b8 11

top_k : 1.0  all : 1.0  recall : 1.0
index : 193 b9ca532 1007
top_k : 1.0  all : 1.0  recall : 1.0
index : 194 6f1c007 990
top_k : 1.0  all : 1.0  recall : 1.0
index : 195 1249a6d 1174
top_k : 1.0  all : 1.0  recall : 1.0
index : 196 2530a21 841
top_k : 3.0  all : 3.0  recall : 1.0
index : 197 bb965b0 1135
top_k : 1.0  all : 1.0  recall : 1.0
index : 198 e0e0fd7 728
top_k : 1.0  all : 1.0  recall : 1.0
index : 199 fed4b08 1056
top_k : 1.0  all : 1.0  recall : 1.0
index : 200 50ceb57 1241
top_k : 1.0  all : 2.0  recall : 0.5
index : 201 ee6ab88 1025
top_k : 1.0  all : 1.0  recall : 1.0
index : 202 eecb923 966
top_k : 1.0  all : 1.0  recall : 1.0
index : 203 c2c7530 1009
top_k : 1.0  all : 1.0  recall : 1.0
index : 204 3dbcb97 1117
top_k : 1.0  all : 1.0  recall : 1.0
index : 205 b104a86 1182
top_k : 1.0  all : 1.0  recall : 1.0
index : 206 6eade39 1363
top_k : 2.0  all : 2.0  recall : 1.0
index : 207 995a5d4 826
top_k : 1.0  all : 1.0  recall : 1.0
index : 208 664efbb 1779
top_k : 12.0 

top_k : 2.0  all : 2.0  recall : 1.0
index : 360 804474c 1646
top_k : 1.0  all : 2.0  recall : 0.5
index : 361 4e2d6cb 1687
top_k : 1.0  all : 1.0  recall : 1.0
index : 362 6adf749 1380
top_k : 1.0  all : 2.0  recall : 0.5
index : 363 abbbd1d 1683
top_k : 1.0  all : 1.0  recall : 1.0
index : 364 5f43353 1701
top_k : 1.0  all : 1.0  recall : 1.0
index : 365 3ab4184 1274
top_k : 1.0  all : 1.0  recall : 1.0
index : 366 0a69655 1015
top_k : 2.0  all : 2.0  recall : 1.0
index : 367 edd4f9e 1391
top_k : 1.0  all : 2.0  recall : 0.5
index : 368 7df55d5 1126
top_k : 1.0  all : 1.0  recall : 1.0
index : 369 256d662 1178
top_k : 0.0  all : 1.0  recall : 0.0
index : 370 1a9cecd 1700
top_k : 1.0  all : 1.0  recall : 1.0
index : 371 754cdea 1700
top_k : 1.0  all : 1.0  recall : 1.0
index : 372 fef7aa2 1700
top_k : 1.0  all : 1.0  recall : 1.0
index : 373 77f776e 2859
top_k : 1.0  all : 1.0  recall : 1.0
index : 374 4d3dfed 1578
top_k : 0.0  all : 1.0  recall : 0.0
index : 375 71796c7 4566
top_k : 

top_k : 1.0  all : 1.0  recall : 1.0
index : 583 0289d1e 2402
top_k : 2.0  all : 2.0  recall : 1.0
index : 584 bb06070 1445
top_k : 0.0  all : 1.0  recall : 0.0
index : 585 84b7a0b 2616
top_k : 1.0  all : 4.0  recall : 0.25
index : 586 848a28e 1465
top_k : 1.0  all : 1.0  recall : 1.0
index : 587 67b2b1a 1451
top_k : 1.0  all : 4.0  recall : 0.25
index : 588 114554a 1607
top_k : 1.0  all : 1.0  recall : 1.0
index : 589 cdc5900 1366
top_k : 3.0  all : 6.0  recall : 0.5
index : 590 8994831 1552
top_k : 6.0  all : 7.0  recall : 0.8571428571428571
index : 591 e27f21a 1764
top_k : 1.0  all : 1.0  recall : 1.0
index : 592 e0ca3cd 1577
top_k : 0.0  all : 1.0  recall : 0.0
index : 593 50f485e 1501
top_k : 1.0  all : 1.0  recall : 1.0
index : 594 fe50358 1812
top_k : 1.0  all : 1.0  recall : 1.0
index : 595 a28eb1e 1511
top_k : 3.0  all : 8.0  recall : 0.375
index : 596 944bab9 1927
top_k : 1.0  all : 1.0  recall : 1.0
index : 597 82a0ad6 1651
top_k : 1.0  all : 1.0  recall : 1.0
index : 598 55

top_k : 28.0  all : 51.0  recall : 0.5490196078431373
index : 787 ea1b989 1911
top_k : 3.0  all : 7.0  recall : 0.42857142857142855
index : 788 110a443 1638
top_k : 1.0  all : 1.0  recall : 1.0
index : 789 448e052 2772
top_k : 1.0  all : 2.0  recall : 0.5
index : 790 ec7b745 1824
top_k : 0.0  all : 1.0  recall : 0.0
index : 791 c400e9b 1903
top_k : 1.0  all : 1.0  recall : 1.0
index : 792 b98f3f6 1907
top_k : 1.0  all : 1.0  recall : 1.0
index : 793 68513f9 1907
top_k : 4.0  all : 4.0  recall : 1.0
index : 794 243d3a3 1814
top_k : 1.0  all : 1.0  recall : 1.0
index : 795 6ea103a 2359
top_k : 0.0  all : 1.0  recall : 0.0
index : 796 01c74c7 1617
top_k : 1.0  all : 1.0  recall : 1.0
index : 797 61343cd 1798
top_k : 2.0  all : 3.0  recall : 0.6666666666666666
index : 798 3f1cf50 1641
top_k : 0.0  all : 3.0  recall : 0.0
index : 799 96af426 1868
top_k : 3.0  all : 9.0  recall : 0.3333333333333333
index : 800 b4afc26 1536
top_k : 2.0  all : 3.0  recall : 0.6666666666666666
index : 801 3dae5

...

index : 5408 83cfde5 5811
top_k : 0.0  all : 1.0  recall : 0.0
index : 5409 73671b1 5742
top_k : 1.0  all : 1.0  recall : 1.0
index : 5410 4304678 5157
top_k : 1.0  all : 1.0  recall : 1.0
index : 5411 726f6f1 5175
top_k : 1.0  all : 3.0  recall : 0.3333333333333333
index : 5412 3462407 6243
top_k : 2.0  all : 154.0  recall : 0.012987012987012988
index : 5413 473fc66 5869
top_k : 0.0  all : 1.0  recall : 0.0
index : 5414 d3494b9 6089
top_k : 0.0  all : 1.0  recall : 0.0
index : 5415 d0b509b 6089
top_k : 2.0  all : 2.0  recall : 1.0
index : 5416 7c5ba07 5291
top_k : 1.0  all : 1.0  recall : 1.0
index : 5417 f462593 5286
top_k : 1.0  all : 2.0  recall : 0.5
index : 5418 5eec2b0 6038
top_k : 1.0  all : 1.0  recall : 1.0
index : 5419 aa667ca 5802
top_k : 1.0  all : 1.0  recall : 1.0
index : 5420 7b3e5c6 5861
top_k : 1.0  all : 1.0  recall : 1.0
index : 5421 2e8342a 5724
top_k : 0.0  all : 2.0  recall : 0.0
index : 5422 6118bac 6089
top_k : 1.0  all : 1.0  recall : 1.0
index : 5423 c4832ba 

top_k : 1.0  all : 1.0  recall : 1.0
index : 5574 13442be 6025
top_k : 1.0  all : 1.0  recall : 1.0
index : 5575 f563078 6110
top_k : 2.0  all : 3.0  recall : 0.6666666666666666
index : 5576 d8f9b6b 6124
top_k : 1.0  all : 1.0  recall : 1.0
index : 5577 48126a2 6111
top_k : 1.0  all : 1.0  recall : 1.0
index : 5578 f876fca 6109
top_k : 1.0  all : 1.0  recall : 1.0
index : 5579 435a105 5634
top_k : 1.0  all : 2.0  recall : 0.5
index : 5580 65f3b42 6012
top_k : 0.0  all : 8.0  recall : 0.0
index : 5581 990da1f 5588
top_k : 3.0  all : 4.0  recall : 0.75
index : 5582 f7cb780 4966
top_k : 1.0  all : 2.0  recall : 0.5
index : 5583 5c04519 5500
top_k : 1.0  all : 1.0  recall : 1.0
index : 5584 6ad021a 6112
top_k : 2.0  all : 2.0  recall : 1.0
index : 5585 5d63a0b 5798
top_k : 0.0  all : 1.0  recall : 0.0
index : 5586 7f5a131 5245
top_k : 1.0  all : 1.0  recall : 1.0
index : 5587 6fd0c2f 5786
top_k : 0.0  all : 1.0  recall : 0.0
index : 5588 1436a6a 6056
top_k : 1.0  all : 2.0  recall : 0.5
in

top_k : 3.0  all : 5.0  recall : 0.6
index : 5723 dd65342 5764
top_k : 1.0  all : 1.0  recall : 1.0
index : 5724 5fdc1da 4699
top_k : 2.0  all : 2.0  recall : 1.0
index : 5725 2a99470 4931
top_k : 1.0  all : 1.0  recall : 1.0
index : 5726 d961dc6 4763
top_k : 0.0  all : 1.0  recall : 0.0
index : 5727 ba96c49 5368
top_k : 1.0  all : 1.0  recall : 1.0
index : 5728 c5d7187 4960
top_k : 1.0  all : 1.0  recall : 1.0
index : 5729 83bff71 6053
top_k : 1.0  all : 1.0  recall : 1.0
index : 5730 d546e79 5525
top_k : 1.0  all : 1.0  recall : 1.0
index : 5731 4a6de6d 6152
top_k : 2.0  all : 2.0  recall : 1.0
index : 5732 0fbbfb1 4571
top_k : 1.0  all : 2.0  recall : 0.5
index : 5733 0c314f5 6162
top_k : 1.0  all : 1.0  recall : 1.0
index : 5734 22ada80 4978
top_k : 0.0  all : 1.0  recall : 0.0
index : 5735 7cf4116 4729
top_k : 1.0  all : 1.0  recall : 1.0
index : 5736 b517497 4714
top_k : 1.0  all : 1.0  recall : 1.0
index : 5737 09a5578 5275
top_k : 1.0  all : 1.0  recall : 1.0
index : 5738 99541

top_k : 1.0  all : 1.0  recall : 1.0
index : 5879 642ec7b 5846
top_k : 2.0  all : 3.0  recall : 0.6666666666666666
index : 5880 d46d127 5539
top_k : 1.0  all : 1.0  recall : 1.0
index : 5881 1d2a487 4979
top_k : 1.0  all : 1.0  recall : 1.0
index : 5882 7100b54 4943
top_k : 1.0  all : 1.0  recall : 1.0
index : 5883 758c1cb 5854
top_k : 1.0  all : 1.0  recall : 1.0
index : 5884 9a67c52 4210
top_k : 1.0  all : 1.0  recall : 1.0
index : 5885 15e344c 6111
top_k : 0.0  all : 1.0  recall : 0.0
index : 5886 bb702b0 6162
top_k : 0.0  all : 2.0  recall : 0.0
index : 5887 363bf2f 5062
top_k : 3.0  all : 3.0  recall : 1.0
index : 5888 6ed2236 5633
top_k : 6.0  all : 6.0  recall : 1.0
index : 5889 819e6ff 6158
top_k : 4.0  all : 10.0  recall : 0.4
index : 5890 c1156eb 5709
top_k : 1.0  all : 1.0  recall : 1.0
index : 5891 31c790f 6161
top_k : 4.0  all : 5.0  recall : 0.8
index : 5892 47c1b8d 6161
top_k : 2.0  all : 4.0  recall : 0.5
index : 5893 f04f4c0 6161
top_k : 1.0  all : 1.0  recall : 1.0
in

(0.7772850220270753, 5940)

In [24]:
# sorted(left_len,reverse=True)
data=pd.DataFrame()
data['len']=left_len
data['len'].value_counts()
# for key,val in data['len'].value_counts().items():当输出内容太多被折叠时，自己手动打印值
#     print(key,val)

50    3645
Name: len, dtype: int64

In [25]:
all_results_df_top_k = pd.concat(all_results_df_top_k)

In [31]:
print(all_results_df_top_k.loc['a0c9251'].shape)
all_results_df_top_k

(50, 3)


used_in_fix        f1  \
bid     fid                                                               
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b          0.0  0.185988   
        6f547898bd6d011af1e621a2c002f10c39856cd4          0.0  0.159427   
        b759c9f92786cc5b07329d303f2bfe37239d0db3          0.0  0.159427   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a          1.0  0.159427   
        638a1fbe3d9de7b7623c1fac1260408526230971          0.0  0.233812   
...                                                       ...       ...   
9cdad39 0896598a924a8db1a1fa9a7f3708a3bc7bdfc12e          0.0  0.272489   
        ea022fdfdbb594cd2c5fe0e7ebadcb9755efe6fc          0.0  0.275422   
        488b7e42175a742b9feb15a594fbe5237868e3c4          0.0  0.103119   
        eb9389695ab26051d4654a791647da3c9a607c16          0.0  0.226009   
        2341a2cf1b153ea1de156fa3ff8cee98a7bb6b3c          0.0  0.264271   

                                                    result  
bid     fid                                                 
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  0.940310  
        6f547898bd6d011af1e621a2c002f10c39856cd4  0.928099  
        b759c9f92786cc5b07329d303f2bfe37239d0db3  0.926931  
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  0.926125  
        638a1fbe3d9de7b7623c1fac1260408526230971  0.924647  
...                                                    ...  
9cdad39 0896598a924a8db1a1fa9a7f3708a3bc7bdfc12e  0.636562  
        ea022fdfdbb594cd2c5fe0e7ebadcb9755efe6fc  0.636156  
        488b7e42175a742b9feb15a594fbe5237868e3c4  0.635649  
        eb9389695ab26051d4654a791647da3c9a607c16  0.635119  
        2341a2cf1b153ea1de156fa3ff8cee98a7bb6b3c  0.634755  

[182250 rows x 3 columns]

In [157]:
# all_results_df_test_fold=dict()
# rows=0
# file_prefix='/data/hdj/tracking_buggy_files/joblib_memmap_swt/swt'
# for i in range(8):
#     all_results_df_test_fold[i+1]=all_results_df_top_k.loc[(i+1)*500:(i+2)*500-1]
#     all_results_df_test_fold[i+1].to_pickle(file_prefix + '_second_testing_fold_' + str(i+1))
#     rows+=all_results_df_test_fold[i+1].shape[0]

In [ ]:
rows,all_results_df_top_k.shape

# 根据bid 和fid获取相应的字符

In [27]:
# fold_number, fold_testing, fold_training = load('/data/hdj/tracking_buggy_files/joblib_memmap_swt/swt/data_memmap', mmap_mode="r")

In [4]:
#获取bug_report TODO
import json
def load_bug_reports(bug_report_file_path):
    """load bug report file (the one generated from xml)"""
    with open(bug_report_file_path) as bug_report_file:
        bug_reports = json.load(bug_report_file)
        return bug_reports
# bug_report_file_path='/data/hdj/tracking_buggy_files/'+swt+'.json'
bug_report_file_path='/data/hdj/tracking_buggy_files/eclipse/eclipse_platform_ui.json'
bug_reports = load_bug_reports(bug_report_file_path)
#这个是原始的report ，我还可以获取经过分词的report
bug_report_id='a694733'
current_bug_report = bug_reports[bug_report_id]['bug_report']
current_bug_report

{'status': 'verified fixed',
 'description': 'N20050224-0010\n\nThanks for fixing the leak in WorkbenchContextSupport.  However, there is now a\nwidget is disposed exception in unregisterShell.  This can happen if the shell\nbeing unregistered is already disposed (which is perfectly legitimate).\n\nThe test case is to use the Next/Previous editor dialogs (CyclePartAction).',
 'timestamp': '1109260000',
 'summary': 'Bug 86474  Widget is disposed in WorkbenchContextSupport.unregisterShell',
 'bug_id': '86474',
 'result': '1:bundles/org.eclipse.ui.workbench/Eclipse UI/org/eclipse/ui/internal/contexts/ws/WorkbenchContextSupport.java',
 'commit': 'a694733',
 'id': '4774'}

In [129]:
# bug_reports['a694733']

In [5]:
# English stop words
stop_words = set(['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves',
'you', 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself',
'she', 'her', 'hers', 'herself', 'it', 'its', 'itself', 'they', 'them', 'their',
'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', 'these',
'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has',
'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but',
'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with',
'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after',
'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over',
'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where',
'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other',
'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too',
'very', 's', 't', 'can', 'will', 'just', 'don', 'should', 'now', 'd', 'll', 'm',
'o', 're', 've', 'y', 'ain', 'aren', 'couldn', 'didn', 'doesn', 'hadn', 'hasn',
'haven', 'isn', 'ma', 'mightn', 'mustn', 'needn', 'shan', 'shouldn', 'wasn',
'weren', 'won', 'wouldn', 'b', 'c', 'e', 'f', 'g', 'h', 'j', 'k', 'l', 'n', 'p',
'q', 'u', 'v', 'w', 'x', 'z', 'us'])

# Java language keywords
java_keywords = set(['abstract', 'assert', 'boolean', 'break', 'byte', 'case',
'catch', 'char', 'class', 'const', 'continue', 'default', 'do', 'double',
'else', 'enum', 'extends', 'false', 'final', 'finally', 'float', 'for', 'goto',
'if', 'implements', 'import', 'instanceof', 'int', 'interface', 'long',
'native', 'new', 'null', 'package', 'private', 'protected', 'public', 'return',
'short', 'static', 'strictfp', 'super', 'switch', 'synchronized', 'this',
'throw', 'throws', 'transient', 'true', 'try', 'void', 'volatile', 'while'])
def clean_string_report(string):
    outtmp=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
#     outtmp=[token for token in outtmp if token not in stop_words]
#     outtmp= [token for token in outtmp if token not in java_keywords]
    outtmp=[token for token in outtmp if token.isalnum() ]
    return ' '.join(outtmp)
print(clean_string_report(current_bug_report['summary']))
description=clean_string_report(current_bug_report['description'])
description

Bug 86474 Widget is disposed in WorkbenchContextSupport unregisterShell


'N20050224 0010 Thanks for fixing the leak in WorkbenchContextSupport However there is now a widget is disposed exception in unregisterShell This can happen if the shell being unregistered is already disposed which is perfectly legitimate The test case is to use the Next Previous editor dialogs CyclePartAction'

In [136]:
# tok_report

In [134]:
token_report=tokenizer.tokenize(description)
idx_report=tokenizer.convert_tokens_to_ids(token_report)
tok_report=tokenizer.convert_ids_to_tokens(idx_report)

In [76]:
outstring=current_bug_report['description']
for char in ['\r\n', '\r', '\n']:
        outstring = outstring.replace(char, ' ')

In [6]:
#获取code信息
# data_prefix='/data/hdj/tracking_buggy_files/tomcat/tomcat'
# ast_cache_db = UnQLite(data_prefix+"_ast_cache_collection_db")
project='eclipse'
ast_cache_collection_db=UnQLite("/data/hdj/tracking_buggy_files/"+project+'/'+project+"_ast_cache_collection_db",
                                             flags=0x00000100 | 0x00000001)
# ast=[item for item in ast_cache_collection_db]

# for key,val in tomcat_ast_file.items():
#     print(key,type(val),len(val))

In [119]:
# ast[1]
#TODO TODO

In [192]:
# ast_file = pickle.loads(ast_cache_collection_db['48f689905f38c99a399d9654e8843fec6ef54cda'])


In [7]:
def clean_code_names(ast_file):
    names=ast_file['classNames']+ast_file['superclassNames']+ast_file['interfaceNames']+ast_file['methodNames']+ast_file['variableNames']
    names=[' '.join(name.split('.')) for name in names]
    print(names)
    return ' '.join(names)
# clean_string_code(ast_file['rawSourceContent'])
# names=clean_code_names(ast_file)

In [288]:
# names=[name.split('.') for name in names]
# tokenizer.tokenize(names)
names

'org aspectj weaver bcel HierarchyDependsTestCase junit framework TestCase HierarchyDependsTestCase testToDo'

In [112]:
tokenizer.convert_tokens_to_ids('Ġaspect'),tokenizer.convert_ids_to_tokens(6659)

(6659, 'Ġaspect')

In [317]:
# tokenizer.tokenize(' '.join(names))
# print(ast_file['rawSourceContent'])

In [314]:
sourceCode=clean_string_code(ast_file['rawSourceContent'])
sourceCode

'package org . aspectj . weaver . bcel ; junit . framework . TestCase ; public class HierarchyDependsTestCase extends TestCase { public HierarchyDependsTestCase ( String arg0 ) { super ( arg0 ) ; } public void testToDo ( ) { } }'

In [80]:
method=clean_string_code(ast_file['methodContent'][0])
method

'public Relationship ( String name , Kind kind , String sourceHandle , List targets , boolean runtimeTest ) { this . name = name ; this . isAffects = name . equals ( "advises" ) name . equals ( "declares on" ) name . equals ( "softens" ) name . equals ( "matched by" ) name . equals ( "declared on" ) name . equals ( "annotates" ) ; this . kind = kind ; this . sourceHandle = sourceHandle ; this . targets = targets ; this . hasRuntimeTest = runtimeTest ; }'

In [79]:
tokenizer.convert_tokens_to_ids(' test'),tokenizer.convert_ids_to_tokens(3)

(3, '<unk>')

In [91]:
len(idx)

326

In [89]:
tok=tokenizer.tokenize(sourceCode)
idx=tokenizer.convert_tokens_to_ids(tok)
tokenizer.convert_ids_to_tokens(idx)

['package',
 'Ġorg',
 'Ġ.',
 'Ġaspect',
 'j',
 'Ġ.',
 'Ġas',
 'm',
 'Ġ.',
 'Ġinternal',
 'Ġ;',
 'Ġimport',
 'Ġjava',
 'Ġ.',
 'Ġutil',
 'Ġ.',
 'ĠList',
 'Ġ;',
 'Ġimport',
 'Ġorg',
 'Ġ.',
 'Ġaspect',
 'j',
 'Ġ.',
 'Ġas',
 'm',
 'Ġ.',
 'ĠI',
 'Relations',
 'hip',
 'Ġ;',
 'Ġpublic',
 'Ġclass',
 'ĠRelationship',
 'Ġimplements',
 'ĠI',
 'Relations',
 'hip',
 'Ġ{',
 'Ġprivate',
 'Ġstatic',
 'Ġfinal',
 'Ġlong',
 'Ġserial',
 'Version',
 'UID',
 'Ġ=',
 'Ġ38',
 '55',
 '166',
 '39',
 '79',
 '57',
 '609',
 '120',
 'L',
 'Ġ;',
 'Ġprivate',
 'ĠString',
 'Ġname',
 'Ġ;',
 'Ġprivate',
 'ĠKind',
 'Ġkind',
 'Ġ;',
 'Ġprivate',
 'Ġboolean',
 'Ġis',
 'A',
 'ffect',
 's',
 'Ġ;',
 'Ġprivate',
 'ĠString',
 'Ġsource',
 'Handle',
 'Ġ;',
 'Ġprivate',
 'ĠList',
 'Ġtargets',
 'Ġ;',
 'Ġprivate',
 'Ġboolean',
 'Ġhas',
 'Runtime',
 'Test',
 'Ġ;',
 'Ġpublic',
 'ĠRelationship',
 'Ġ(',
 'ĠString',
 'Ġname',
 'Ġ,',
 'ĠKind',
 'Ġkind',
 'Ġ,',
 'ĠString',
 'Ġsource',
 'Handle',
 'Ġ,',
 'ĠList',
 'Ġtargets',
 'Ġ,',
 'Ġboolean

In [137]:
# print(ast_file['rawSourceContent'])

In [50]:
res=clean_string_report('public Relationship(\n\t\tString name, \n\t\tKind kind,\n\t\tString sourceHandle,\n\t\tList targets,\n\t\tboolean runtimeTest) {\n\t\t\t\n\t\tthis.name = name;\n\t\tthis.isAffects = \n\t\t\tname.equals("advises") || \n\t        name.equals("declares on") || \n\t        name.equals("softens") ||\n\t        name.equals("matched by") || \n\t        name.equals("declared on") || \n\t        name.equals("annotates");\n\t\tthis.kind = kind;\n\t\tthis.sourceHandle = sourceHandle;\n\t\tthis.targets = targets;\n\t\tthis.hasRuntimeTest = runtimeTest;\n\t}')
res

'public Relationship String name Kind kind String sourceHandle List targets boolean runtimeTest this name name this isAffects name equals name equals name equals name equals name equals name equals this kind kind this sourceHandle sourceHandle this targets targets this hasRuntimeTest runtimeTest'

In [24]:
tokenizer = RobertaTokenizer.from_pretrained('roberta-base', do_lower_case=False)

In [56]:
tokenizer.convert_tokens_to_ids(['Ġhas', 'Ġruntime', 'Ġtest']),tokenizerNoLower.convert_tokens_to_ids(['has', 'Ġruntime', 'test'])

([34, 44190, 1296], [7333, 44190, 21959])

In [54]:
tokenizer.convert_ids_to_tokens(34)

'Ġhas'

In [28]:
tokenizerNoLower = RobertaTokenizer.from_pretrained('roberta-base', do_lower_case=True)

In [52]:
res

'public Relationship String name Kind kind String sourceHandle List targets boolean runtimeTest this name name this isAffects name equals name equals name equals name equals name equals name equals this kind kind this sourceHandle sourceHandle this targets targets this hasRuntimeTest runtimeTest'

In [58]:
token=tokenizer.tokenize(res)
idx=tokenizer.convert_tokens_to_ids(token)

In [62]:
# token

In [63]:
# tokenizer.convert_ids_to_tokens(idx)

In [64]:
# tokenizerNoLower.tokenize(res)

In [36]:
out=tokenizer.tokenize('hasRuntimeTest')
out=[string.lower() for string in out]
out

['has', 'runtime', 'test']

In [79]:
# swt_ast[0]
for idx in has:
#     print(idx)
    swt_ast_file = pickle.loads(swt_ast_cache_collection_db[idx.split('_')[1]])
    # swt_ast_file
#     print(idx,len(swt_ast_file['methodContent']))
    top_k_method,num=get_method_top_k(swt_ast_file['methodContent'],10)
#     print(len(top_k_method))
#     for key,val in swt_ast_file.items():
#         print(key,type(val),len(val))


In [33]:
swt_ast_file['methodContent']
top_k_method,num=get_method_top_k(swt_ast_file['methodContent'],10)

In [80]:
# top_k_method

# 生成PLI需要的数据 采用set去重 只取6个tokenized内容

In [15]:
def camel_case_split(identifier):
    matches = finditer('.+?(?:(?<=[a-z])(?=[A-Z])|(?<=[A-Z])(?=[A-Z][a-z])|$)', identifier)
    return [m.group(0) for m in matches]
def mergeTokenziedSource(tokenizedSource):#dict 类型
    return ' '.join(tokenizedSource.keys())
removed = u'!"#%&\'()*+,-./:;<=>?@[\]^_`{|}~1234567890'
utf_translate_table = dict((ord(char), u' ') for char in removed)
stop_words = set(stopwords.words('english'))

def tokenize(text, stemmer):
    sanitized_text = text.translate(utf_translate_table)
    tokens = wordpunct_tokenize(sanitized_text)
    all_tokens = []
    for token in tokens:
        additional_tokens = camel_case_split(token)
        if len(additional_tokens)>1:
            for additional_token in additional_tokens:
                all_tokens.append(additional_token)
        all_tokens.append(token)
    return Counter([stemmer.stem(token) for token in all_tokens if token.lower() not in stop_words])
def convert_dict2string_set(dict_list):
    counter_list = set()
    for dict_item in dict_list:
        for k,v in dict_item.items():
            if len(k)<=2:
                continue
            counter_list.add(k)
#     print('len dict_set :',len(dict_list),'merge len :',len(counter_list))
    return ' '.join(counter_list)
def convert_dict2string_list(dict_list):
    counter_list = []
    for dict_item in dict_list:
        for k,v in dict_item.items():
            counter_list.append(k)
#     print('len dict_list :',len(dict_list),'merge len :',len(counter_list))
    return ' '.join(counter_list)  
def clean_string_code(string):
    m = re.compile(r'/\*.*?\*/', re.S)
    outstring = re.sub(m, '', string)
    m = re.compile(r'import*', re.S)
    outstring = re.sub(m, '', outstring)
    m = re.compile(r'//.*')
    outtmp = re.sub(m, '', outstring)
    for char in ['\r\n', '\r', '\n']:
        outtmp = outtmp.replace(char, ' ')
    outtmp=' '.join(outtmp.split())
    outtmp=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',outtmp)
    return ' '.join(outtmp)
def get_method_top_k(choosed_methods:list,k=50):
    method_list=[]
    for string_bef in choosed_methods:
#         print('string_bef :',string_bef)
        string=clean_string_code(string_bef)
        if '{'  in string and '}'in string :
            method_list.append(string)
#     print('函数体的方法数量: ',len(method_list))
    num=len(method_list)
    method_list = sorted(method_list,key = lambda string:len(string.split()),reverse=True)
    if len(method_list)==0:
        for string_bef in choosed_methods:
#         print('string_bef :',string_bef)
            string=clean_string(string_bef)
            method_list.append(string)
        method_list = sorted(method_list,key = lambda string:len(string.split()),reverse=True)
        num=len(method_list)
        return method_list[:k],num
#     print(len(method_list))
#     for method in method_list:
#         print(method)
    return method_list[:k],num
# method_top_k,num=get_method_top_k(swt_ast_file['methodContent'],10)  
# num

In [82]:

# train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv' 
# train_k=pd.read_csv(train_k_path)
# train_k.set_index(['bid','fid'], inplace = True)
# train_k.head(10)
# all_ast_index=list(train_k.index.get_level_values(1).unique())
# method_len=[]
# for ast_index in all_ast_index:
# #     print(ast_index)
#     ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
#     print('method len',len(ast_file['methodContent']))
#     method_top_k=get_method_top_k(ast_file['methodContent'],10)  
#     print('method_top_k :',len(method_top_k))
#     method_len.append(len(method_top_k))
    

In [52]:
statis(method_len,'method_len')

method_len code 的 10% 0.0
20 : 4.0
30 : 12.0
40 : 21.0
50 : 33.0
60 : 54.0
70 : 71.0
80 : 106.40000000000009
90 : 153.0


In [95]:
# with open('/data/hdj/BERT_PLI/train_1_tokenzied2_15_stage2.json','r',encoding='utf-8') as f_in:
#     for i,line in enumerate(f_in):
#         line=eval(line)
#         print(len(line['c_paras']))
#         if i==100:
#             break
# for ast_index in all_ast_index:
#     print(ast_index)
#     ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
#     print(ast_file['methodContent'])
#     res=get_method_top_k(ast_file['methodContent'],10)
#     print(len(res))
# swt_ast_cache_collection_db

In [21]:

def generate_pli(train_k_path,out_path):
    #生成PLI需要的数据集
    task1_list=[]
    #train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv' 
    #out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.txt'
    train_k=pd.read_csv(train_k_path)
    train_k.set_index(['bid','fid'], inplace = True)
    train_k.head(10)
    #取bid所对应的report
    bid_list=list(train_k.index.get_level_values(0).unique())
    len(bid_list)
    summarys=[]
    descriptions=[]
    for bug_report_id in bid_list:
        current_bug_report = bug_reports[bug_report_id]['bug_report']
        summarys.append(current_bug_report['summary'])
        descriptions.append(current_bug_report['description'])
    report_dataFrame=pd.DataFrame({'summary':summarys,'description':descriptions},index=bid_list)
    report_dataFrame.index.names=['bid']
    def remove_twoHeadWord(string):
        contents=string.split(' ')[2:]
        return ' '.join(contents)
    report_dataFrame.fillna("",inplace=True)
    report_dataFrame['summary']=report_dataFrame['summary'].apply(remove_twoHeadWord)
    report_dataFrame['summary']=report_dataFrame['summary'].apply(clean_string_report)
    report_dataFrame['description']=report_dataFrame['description'].apply(clean_string_report)
    report_dataFrame.head()
    all_ast_index=list(train_k.index.get_level_values(1).unique())
    type(all_ast_index)
#     all_ast_file_tokenizedSource=[]
    all_ast_file_tokenizedMethods=[]
    all_ast_file_tokenizedClassNames =[]
    all_ast_file_tokenizedMethodNames=[]
    all_ast_file_tokenizedVariableNames=[]
    all_ast_file_tokenizedComments =[]
    all_ast_file_methods=[]
    for ast_index in all_ast_index:
    #     print(ast_index)
        ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
#         all_ast_file_tokenizedSource.append(convert_dict2string_set([ast_file['tokenizedSource']]))
        all_ast_file_tokenizedMethods.append(convert_dict2string_set(ast_file['tokenizedMethods']))
        top_k_method,num=get_method_top_k(ast_file['methodContent'],10)
        print('total method num :',len(ast_file['methodContent']),' 有方法体的函数数量 :',num,' choosed method num :',len(top_k_method))
        all_ast_file_methods.append(top_k_method )
        all_ast_file_tokenizedClassNames.append(convert_dict2string_set(ast_file['tokenizedClassNames']))
        all_ast_file_tokenizedMethodNames.append(convert_dict2string_set(ast_file['tokenizedMethodNames']))
        all_ast_file_tokenizedVariableNames.append(convert_dict2string_set(ast_file['tokenizedVariableNames']))
        all_ast_file_tokenizedComments.append(convert_dict2string_set(ast_file['tokenizedComments']))
    # all_ast_index
    all_ast_index_dataframe=pd.DataFrame({'all_ast_file_methods':all_ast_file_methods,'tokenizedMethods':all_ast_file_tokenizedMethods,
                                          'tokenizedClassNames':all_ast_file_tokenizedClassNames,'tokenizedMethodNames':all_ast_file_tokenizedMethodNames,
                                          'tokenizedVariableNames':all_ast_file_tokenizedVariableNames,'tokenizedComments':all_ast_file_tokenizedComments},index=all_ast_index)
    # print(all_ast_index_dataframe.head())
    print(all_ast_index_dataframe.shape)
    # all_ast_index_dataframe.set_index(["ast_index"], inplace=True)
    # all_ast_index_dataframe
    all_ast_index_dataframe.index.names=['fid']
    all_ast_index_dataframe.head(2)
    #开始连接字段
    all_methodContent_index_dataframe=all_ast_index_dataframe.join(train_k,how='inner')
    all_methodContent_index_dataframe.head()
    all_report_methodContent_index_dataframe=report_dataFrame.join(all_methodContent_index_dataframe,how='inner')
    all_report_methodContent_index_dataframe.head()
    
    task1_list=[]
    all_report_methodContent_index_dataframe.fillna("",inplace=True)
    sum_label=0
    for i,(index, row) in enumerate(all_report_methodContent_index_dataframe.iterrows()):
    #     print(index[0],index[1],row['summary'],row['description'],row['methodContent'],row['used_in_fix'])
#         if len(row['tokenizedSource'])==0:
#             continue
        guid='_'.join([index[0],index[1]])
        
#         q_paras=[mergeTokenziedSource(tokenize(row['summary'],stemmer)),mergeTokenziedSource(tokenize(row['description'],stemmer))]
        q_paras=[row['summary'],row['description']]
        print('tokenizedMethods len :',len(row['tokenizedMethods']))
        c_paras=[row['tokenizedMethods'],row['tokenizedClassNames'],
                 row['tokenizedMethodNames'],row['tokenizedVariableNames'],row['tokenizedComments'],]
#         print('all_ast_file_methods :',len(row['all_ast_file_methods']))
        c_paras.extend(row['all_ast_file_methods'])
#         c_paras=row['all_ast_file_methods']
#         print(i,'summary :',type(row['summary']),'description :',type(row['description']),'len summary :',len(q_paras.split()),'source :',len(c_paras.split()))
        summary_len.append(len(q_paras[0].split()))
        description_len.append(len(q_paras[1].split()))
#         tokenizedSource_len.append(len(c_paras[0].split()))

#         tokenizedMethods_len.append(len(c_paras[1].split()))      
#         tokenizedClassNames_len.append(len(c_paras[2].split()))   
#         tokenizedMethodNames_len.append(len(c_paras[3].split()))   
#         tokenizedVariableNames_len.append(len(c_paras[4].split())) 
#         tokenizedComments_len.append(len(c_paras[5].split()))
        label=int(row['used_in_fix'])
        task1=dict()
        task1['guid']=guid
        task1['q_paras']=q_paras
        task1['c_paras']=c_paras
        task1['label']=label
        task1_list.append(task1)
#         if i==10:
#             break
    print(task1_list[0])
    with open(out_path,'w',encoding='utf-8') as f_out:
        for task1 in task1_list:
            out_line = json.dumps(task1, ensure_ascii=False) + '\n'
            f_out.write(out_line)
summary_len=[]
description_len=[]
tokenizedSource_len=[]
tokenizedMethods_len=[]
tokenizedClassNames_len=[]
tokenizedMethodNames_len=[]
tokenizedVariableNames_len=[]
tokenizedComments_len=[]
train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_3hard_1.csv' 
train_out_path='/data/hdj/BERT_PLI/train_3hard_1_5_10method.json' 
generate_pli(train_k_path,train_out_path)

test_2_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/test_3hard_2.csv' 
test_2_out_path='/data/hdj/BERT_PLI/test_3hard_2_5_10method.json'  
generate_pli(test_2_k_path,test_2_out_path)

test_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/test_half_hardeasy_3.csv' 
test_out_path='/data/hdj/BERT_PLI/test_half_hardeasy_3.json'  
# generate_pli(test_k_path,test_out_path)



total method num : 8  有方法体的函数数量 : 8  choosed method num : 8
total method num : 617  有方法体的函数数量 : 107  choosed method num : 10
total method num : 7  有方法体的函数数量 : 7  choosed method num : 7
total method num : 8  有方法体的函数数量 : 8  choosed method num : 8
total method num : 7  有方法体的函数数量 : 7  choosed method num : 7
total method num : 8  有方法体的函数数量 : 8  choosed method num : 8
total method num : 7  有方法体的函数数量 : 7  choosed method num : 7
total method num : 14  有方法体的函数数量 : 14  choosed method num : 10
total method num : 224  有方法体的函数数量 : 221  choosed method num : 10
total method num : 56  有方法体的函数数量 : 56  choosed method num : 10
total method num : 60  有方法体的函数数量 : 60  choosed method num : 10
total method num : 154  有方法体的函数数量 : 154  choosed method num : 10
total method num : 22  有方法体的函数数量 : 22  choosed method num : 10
total method num : 147  有方法体的函数数量 : 147  choosed method num : 10
total method num : 66  有方法体的函数数量 : 66  choosed method num : 10
total method num : 618  有方法体的函数数量 : 107  choosed method num : 10


total method num : 167  有方法体的函数数量 : 167  choosed method num : 10
total method num : 158  有方法体的函数数量 : 158  choosed method num : 10
total method num : 88  有方法体的函数数量 : 88  choosed method num : 10
total method num : 52  有方法体的函数数量 : 52  choosed method num : 10
total method num : 17  有方法体的函数数量 : 17  choosed method num : 10
total method num : 192  有方法体的函数数量 : 192  choosed method num : 10
total method num : 153  有方法体的函数数量 : 153  choosed method num : 10
total method num : 24  有方法体的函数数量 : 24  choosed method num : 10
total method num : 26  有方法体的函数数量 : 26  choosed method num : 10
total method num : 27  有方法体的函数数量 : 27  choosed method num : 10
total method num : 103  有方法体的函数数量 : 103  choosed method num : 10
total method num : 12  有方法体的函数数量 : 12  choosed method num : 10
total method num : 95  有方法体的函数数量 : 95  choosed method num : 10
total method num : 143  有方法体的函数数量 : 143  choosed method num : 10
total method num : 196  有方法体的函数数量 : 196  choosed method num : 10
total method num : 167  有方法体的函数数量 : 167  

total method num : 151  有方法体的函数数量 : 151  choosed method num : 10
total method num : 162  有方法体的函数数量 : 162  choosed method num : 10
total method num : 170  有方法体的函数数量 : 170  choosed method num : 10
total method num : 71  有方法体的函数数量 : 71  choosed method num : 10
total method num : 99  有方法体的函数数量 : 99  choosed method num : 10
total method num : 65  有方法体的函数数量 : 65  choosed method num : 10
total method num : 63  有方法体的函数数量 : 63  choosed method num : 10
total method num : 69  有方法体的函数数量 : 69  choosed method num : 10
total method num : 129  有方法体的函数数量 : 129  choosed method num : 10
total method num : 42  有方法体的函数数量 : 42  choosed method num : 10
total method num : 39  有方法体的函数数量 : 39  choosed method num : 10
total method num : 65  有方法体的函数数量 : 65  choosed method num : 10
total method num : 62  有方法体的函数数量 : 62  choosed method num : 10
total method num : 66  有方法体的函数数量 : 66  choosed method num : 10
total method num : 57  有方法体的函数数量 : 57  choosed method num : 10
total method num : 60  有方法体的函数数量 : 60  choosed 

total method num : 73  有方法体的函数数量 : 73  choosed method num : 10
total method num : 126  有方法体的函数数量 : 126  choosed method num : 10
total method num : 6  有方法体的函数数量 : 6  choosed method num : 6
total method num : 103  有方法体的函数数量 : 103  choosed method num : 10
total method num : 63  有方法体的函数数量 : 63  choosed method num : 10
total method num : 158  有方法体的函数数量 : 158  choosed method num : 10
total method num : 616  有方法体的函数数量 : 1  choosed method num : 1
total method num : 53  有方法体的函数数量 : 53  choosed method num : 10
total method num : 62  有方法体的函数数量 : 62  choosed method num : 10
total method num : 51  有方法体的函数数量 : 51  choosed method num : 10
total method num : 52  有方法体的函数数量 : 52  choosed method num : 10
total method num : 7  有方法体的函数数量 : 7  choosed method num : 7
total method num : 71  有方法体的函数数量 : 71  choosed method num : 10
total method num : 45  有方法体的函数数量 : 45  choosed method num : 10
total method num : 18  有方法体的函数数量 : 18  choosed method num : 10
total method num : 18  有方法体的函数数量 : 18  choosed method nu

total method num : 20  有方法体的函数数量 : 20  choosed method num : 10
total method num : 60  有方法体的函数数量 : 60  choosed method num : 10
total method num : 42  有方法体的函数数量 : 42  choosed method num : 10
total method num : 29  有方法体的函数数量 : 29  choosed method num : 10
total method num : 89  有方法体的函数数量 : 89  choosed method num : 10
total method num : 84  有方法体的函数数量 : 84  choosed method num : 10
total method num : 129  有方法体的函数数量 : 129  choosed method num : 10
total method num : 81  有方法体的函数数量 : 81  choosed method num : 10
total method num : 26  有方法体的函数数量 : 26  choosed method num : 10
total method num : 31  有方法体的函数数量 : 31  choosed method num : 10
total method num : 22  有方法体的函数数量 : 22  choosed method num : 10
total method num : 25  有方法体的函数数量 : 25  choosed method num : 10
total method num : 60  有方法体的函数数量 : 60  choosed method num : 10
total method num : 37  有方法体的函数数量 : 37  choosed method num : 10
total method num : 58  有方法体的函数数量 : 58  choosed method num : 10
total method num : 52  有方法体的函数数量 : 52  choosed method

...

tokenizedMethods len : 14477
tokenizedMethods len : 12399
tokenizedMethods len : 12647
tokenizedMethods len : 2714
tokenizedMethods len : 6492
tokenizedMethods len : 6205
tokenizedMethods len : 12803
tokenizedMethods len : 9441
tokenizedMethods len : 13255
tokenizedMethods len : 2831
tokenizedMethods len : 9202
tokenizedMethods len : 2131
tokenizedMethods len : 4528
tokenizedMethods len : 6545
tokenizedMethods len : 5363
tokenizedMethods len : 609
tokenizedMethods len : 8721
tokenizedMethods len : 6928
tokenizedMethods len : 4280
tokenizedMethods len : 15198
tokenizedMethods len : 8058
tokenizedMethods len : 12830
tokenizedMethods len : 2324
tokenizedMethods len : 3428
tokenizedMethods len : 6263
tokenizedMethods len : 12177
tokenizedMethods len : 11220
tokenizedMethods len : 8490
tokenizedMethods len : 789
tokenizedMethods len : 783
tokenizedMethods len : 693
tokenizedMethods len : 3248
tokenizedMethods len : 7174
tokenizedMethods len : 2948
tokenizedMethods len : 7816
tokenizedMethod

tokenizedMethods len : 3145
tokenizedMethods len : 2443
tokenizedMethods len : 6263
tokenizedMethods len : 3872
tokenizedMethods len : 3428
tokenizedMethods len : 2524
tokenizedMethods len : 8058
tokenizedMethods len : 16036
tokenizedMethods len : 3014
tokenizedMethods len : 4891
tokenizedMethods len : 7000
tokenizedMethods len : 8490
tokenizedMethods len : 6492
tokenizedMethods len : 2311
tokenizedMethods len : 7820
tokenizedMethods len : 7934
tokenizedMethods len : 6205
tokenizedMethods len : 3319
tokenizedMethods len : 13033
tokenizedMethods len : 1802
tokenizedMethods len : 8395
tokenizedMethods len : 14477
tokenizedMethods len : 3017
tokenizedMethods len : 13255
tokenizedMethods len : 4423
tokenizedMethods len : 4256
tokenizedMethods len : 12830
tokenizedMethods len : 14474
tokenizedMethods len : 4528
tokenizedMethods len : 6663
tokenizedMethods len : 4891
tokenizedMethods len : 14495
tokenizedMethods len : 6942
tokenizedMethods len : 7000
tokenizedMethods len : 4256
tokenizedMeth

tokenizedMethods len : 9202
tokenizedMethods len : 6263
tokenizedMethods len : 7854
tokenizedMethods len : 6591
tokenizedMethods len : 17159
tokenizedMethods len : 8825
tokenizedMethods len : 10784
tokenizedMethods len : 14477
tokenizedMethods len : 3174
tokenizedMethods len : 9463
tokenizedMethods len : 12803
tokenizedMethods len : 2812
tokenizedMethods len : 4736
tokenizedMethods len : 9072
tokenizedMethods len : 20411
tokenizedMethods len : 4514
tokenizedMethods len : 12447
tokenizedMethods len : 12177
tokenizedMethods len : 4810
tokenizedMethods len : 13255
tokenizedMethods len : 12830
tokenizedMethods len : 9441
tokenizedMethods len : 8358
tokenizedMethods len : 6042
tokenizedMethods len : 14494
tokenizedMethods len : 2218
tokenizedMethods len : 3872
tokenizedMethods len : 3145
tokenizedMethods len : 4636
tokenizedMethods len : 12647
tokenizedMethods len : 11220
tokenizedMethods len : 2574
tokenizedMethods len : 9202
tokenizedMethods len : 16036
tokenizedMethods len : 12803
tokeni

tokenizedMethods len : 12177
tokenizedMethods len : 9441
tokenizedMethods len : 12447
tokenizedMethods len : 13255
tokenizedMethods len : 20411
tokenizedMethods len : 6263
tokenizedMethods len : 12803
tokenizedMethods len : 1869
tokenizedMethods len : 6545
tokenizedMethods len : 8346
tokenizedMethods len : 1776
tokenizedMethods len : 9202
tokenizedMethods len : 2474
tokenizedMethods len : 2171
tokenizedMethods len : 16036
tokenizedMethods len : 8721
tokenizedMethods len : 4538
tokenizedMethods len : 2067
tokenizedMethods len : 15198
tokenizedMethods len : 12647
tokenizedMethods len : 12830
tokenizedMethods len : 1545
tokenizedMethods len : 2010
tokenizedMethods len : 1137
tokenizedMethods len : 7000
tokenizedMethods len : 11220
tokenizedMethods len : 4877
tokenizedMethods len : 6591
tokenizedMethods len : 7854
tokenizedMethods len : 2804
tokenizedMethods len : 2958
tokenizedMethods len : 6042
tokenizedMethods len : 4810
tokenizedMethods len : 2131
tokenizedMethods len : 5383
tokenizedM

tokenizedMethods len : 6396
tokenizedMethods len : 6784
tokenizedMethods len : 8825
tokenizedMethods len : 9082
tokenizedMethods len : 14477
tokenizedMethods len : 14507
tokenizedMethods len : 409
tokenizedMethods len : 952
tokenizedMethods len : 421
tokenizedMethods len : 428
tokenizedMethods len : 1181
tokenizedMethods len : 719
tokenizedMethods len : 3167
tokenizedMethods len : 426
tokenizedMethods len : 382
tokenizedMethods len : 785
tokenizedMethods len : 397
tokenizedMethods len : 445
tokenizedMethods len : 389
tokenizedMethods len : 403
tokenizedMethods len : 994
tokenizedMethods len : 877
tokenizedMethods len : 10784
tokenizedMethods len : 469
tokenizedMethods len : 1478
tokenizedMethods len : 917
tokenizedMethods len : 956
tokenizedMethods len : 998
tokenizedMethods len : 731
tokenizedMethods len : 1878
tokenizedMethods len : 13033
tokenizedMethods len : 2565
tokenizedMethods len : 1069
tokenizedMethods len : 12447
tokenizedMethods len : 2713
tokenizedMethods len : 443
tokeniz

In [25]:
s= "int BrowseCallbackProc ( int hwnd , int uMsg , int lParam , int lpData ) { switch ( uMsg ) { case OS . BFFM_INITIALIZED : if ( filterPath ! = null filterPath . length ( ) ! = 0 ) { TCHAR buffer = new TCHAR ( 0 , filterPath . replace ( / , ) , true ) ; OS . SendMessage ( hwnd , OS . BFFM_SETSELECTION , 1 , buffer ) ; } if ( title ! = null title . length ( ) ! = 0 ) { TCHAR buffer = new TCHAR ( 0 , title , true ) ; OS . SetWindowText ( hwnd , buffer ) ; } break ; case OS . BFFM_VALIDATEFAILEDA : case OS . BFFM_VALIDATEFAILEDW : TCHAR buffer = new TCHAR ( 0 , 256 ) ; int byteCount = buffer . length ( ) * TCHAR . sizeof ; OS . MoveMemory ( buffer , lParam , byteCount ) ; directoryPath = buffer . toString ( 0 , buffer . strlen ( ) ) ; break ; } return 0 ; }"
len(s.split(' '))

185

In [15]:
# summary_len=[]
def statis(sourceLen,name):#list
    a = np.array(sourceLen)
    print(name,'code 的 10%', np.percentile(a, 10))
    print('20 :', np.percentile(a, 20))
    print('30 :', np.percentile(a, 30))
    print('40 :', np.percentile(a, 40))
    print('50 :', np.median(a))
    print('60 :', np.percentile(a, 60))
    print('70 :', np.percentile(a, 70))
    print('80 :', np.percentile(a, 80))
    print('90 :', np.percentile(a, 90))
statis(summary_len,'summary_len')
statis(description_len,'description_len')
statis(tokenizedSource_len,'tokenizedSource_len')
statis(tokenizedMethods_len,'tokenizedMethods_len')
statis(tokenizedClassNames_len,'tokenizedClassNames_len')
statis(tokenizedMethodNames_len,'tokenizedMethodNames_len')
statis(tokenizedVariableNames_len,'tokenizedVariableNames_len')
statis(tokenizedComments_len,'tokenizedComments_len')


summary_len code 的 10% 4.0
20 : 5.0
30 : 5.0
40 : 6.0
50 : 6.0
60 : 7.0
70 : 7.0
80 : 8.0
90 : 10.0
description_len code 的 10% 0.0
20 : 12.0
30 : 17.0
40 : 22.0
50 : 28.0
60 : 35.0
70 : 45.0
80 : 59.0
90 : 93.0
tokenizedSource_len code 的 10% 60.0
20 : 96.0
30 : 158.0
40 : 261.8000000000002
50 : 388.0
60 : 513.0
70 : 644.0
80 : 775.0
90 : 1093.3000000000002
tokenizedMethods_len code 的 10% 0.0
20 : 40.0
30 : 108.0
40 : 213.0
50 : 337.0
60 : 456.0
70 : 572.6999999999989
80 : 711.0
90 : 991.3000000000002
tokenizedClassNames_len code 的 10% 5.0
20 : 5.0
30 : 5.0
40 : 5.0
50 : 7.0
60 : 7.0
70 : 8.0
80 : 9.0
90 : 10.0
tokenizedMethodNames_len code 的 10% 0.0
20 : 8.0
30 : 23.0
40 : 42.0
50 : 68.0
60 : 95.0
70 : 127.0
80 : 191.0
90 : 240.0
tokenizedVariableNames_len code 的 10% 5.0
20 : 11.0
30 : 17.0
40 : 32.0
50 : 58.0
60 : 82.0
70 : 105.0
80 : 146.0
90 : 232.30000000000018
tokenizedComments_len code 的 10% 34.0
20 : 44.0
30 : 61.0
40 : 128.0
50 : 192.0
60 : 256.0
70 : 321.0
80 : 416.0
90 : 532.

In [10]:
# convert_dict2string_list([swt_ast_file['tokenizedSource']])

In [ ]:
source

In [22]:
# methods=convert_dict2string_list(swt_ast_file['tokenizedMethods'])
# methods

In [23]:
# methods=convert_dict2string_set(swt_ast_file['tokenizedMethods'])
# methods

In [42]:
ClassNames=convert_dict2string(swt_ast_file['tokenizedClassNames'])
ClassNames

len dict_list : 1 merge len : 5


'eclips intern org swt cairo'

In [24]:
# MethodNames=convert_dict2string_list(swt_ast_file['tokenizedMethodNames'])
# MethodNames

In [25]:
# convert_dict2string_set(swt_ast_file['tokenizedMethodNames'])

In [26]:
# VariableNames=convert_dict2string(swt_ast_file['tokenizedVariableNames'])
# VariableNames


In [ ]:
# Comments=convert_dict2string_list(swt_ast_file['tokenizedComments'])
# Comments


In [ ]:
# swt_ast_file['tokenizedComments']

In [14]:
convert_dict2string_list(swt_ast_file['tokenizedComments'])

len dict_list : 496 merge len : 89


'kind contributor param screen destroy C const sourc right use swt size public cr dpi font languag corp reserv glyph copi pattern famili matrix pixmap path limit user cast complianc ibm result flag extent impli face method distribut subject key func mpl text surfac char file specif www copyright long b interfac unsign display content cairo block end dynam drawabl except org begin option src may nativ without version govern obtain bind target dest void basi permit data constant express warranti licens softwar utf see mozilla visual http either'

In [43]:
swt_ast_file['tokenizedClassNames'],swt_ast_file['classNames'],

([{'org': 1, 'intern': 1, 'eclips': 1, 'swt': 1, 'cairo': 2}],
 ['org.eclipse.swt.internal.cairo.Cairo'])

In [37]:
# swt_ast_file['tokenizedSource']

In [2]:
# summary=0
# for method in swt_ast_file['tokenizedMethods']:
# #     print(len(method))
#     summary+=len(method)
# print(summary)

In [268]:
import re
import pandas as pd
import nltk
import string
import glob
import string
import inflection
import json
import subprocess
from unqlite import UnQLite
import pickle
from scipy import sparse
import numpy as np
from skopt import *
import torch

In [6]:
import pandas as pd

In [269]:
import pandas as pd
project='eclipse'
# swt_testing_fold_1=pd.read_pickle('/data/hdj/tracking_buggy_files/swt/swt_testing_fold_0')
swt_all_results_df_before=pd.read_pickle('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/all_results_df_before.pickle')
# # swt_all_results_df_before
# swt_testing_fold_1

In [2]:
swt_all_results_df_before.head(10)

used_in_fix        f1  \
bid     fid                                                               
a0c9251 aa245982fa51518c22c1817fd56ac88b4b921f80          0.0  0.030239   
        38b760ae592520a29eecbc29ac4b6665c9e9bf61          0.0  0.010100   
        ebde7ae63aa647dc84eb1c29f1fa2133b4d1e705          0.0  0.026023   
        0b6789bd6c4f2ad5b82d0e4800e6c3924bc45589          0.0  0.026685   
        bc6b590ab782fc46728d0561c084f3c5fa843a68          0.0  0.040819   
        ff61ae210626fdc50b30503a5efb87661e4bd208          0.0  0.026143   
        0d3adbcb22efd9b83162c22e2ed0c2fb0e08f31b          0.0  0.014304   
        0d1b738723aab355917bbba1b0b102f7ec0c1597          0.0  0.009769   
        343df4ffbec9bf3a2e4f5870c2a90f344a98430f          0.0  0.015205   
        dd1510f2a0c527a8254a91f7d766a2edc58a47b7          0.0  0.028439   

                                                    result  
bid     fid                                                 
a0c9251 aa245982fa51518c22c1817fd56ac88b4b921f80  0.588582  
        38b760ae592520a29eecbc29ac4b6665c9e9bf61  0.556395  
        ebde7ae63aa647dc84eb1c29f1fa2133b4d1e705  0.549675  
        0b6789bd6c4f2ad5b82d0e4800e6c3924bc45589  0.550011  
        bc6b590ab782fc46728d0561c084f3c5fa843a68  0.600155  
        ff61ae210626fdc50b30503a5efb87661e4bd208  0.603358  
        0d3adbcb22efd9b83162c22e2ed0c2fb0e08f31b  0.585748  
        0d1b738723aab355917bbba1b0b102f7ec0c1597  0.549967  
        343df4ffbec9bf3a2e4f5870c2a90f344a98430f  0.574148  
        dd1510f2a0c527a8254a91f7d766a2edc58a47b7  0.625167

In [22]:
with open('/data/hdj/BERT_PLI/train_1_tokenzied2_6_stage2.json','r',encoding='utf-8') as f_in:
    with open('/data/hdj/BERT_PLI/train_1_tokenzied2_6_stage2_replace.json','w',encoding='utf-8') as f_out:
        for line in f_in:
            line=eval(line)
#             out=dict()
#             out['guid']=line['guid']
#             out['q_paras']=line['text_a']
#             out['c_paras']=line['text_b']
#             out['label']=line['label']
            if line['label']==1 or line['label']=='1':
                for i in range(10):
                    out_line = json.dumps(line, ensure_ascii=False) + '\n'
                    f_out.write(out_line)
            else:
                out_line = json.dumps(line, ensure_ascii=False) + '\n'
                f_out.write(out_line)

In [8]:
# for id in stage2_result.index.unique():
#     print(id)

In [7]:
# count=0
# for id in stage2_result.index.unique():
#     bug_report_files_dataframe=stage2_result.loc[id]
#     min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
#     bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
#     sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
#     print(sorted_df.shape)
#     if sorted_df.shape[0]<=20:
#         count+=1
# print(count)

In [34]:
168/500

0.336

In [20]:
k_range=range(1, 21)
average_precision_per_bug_report = []
reciprocal_ranks = []
# calculate per each query (bug report)
accuracy_at_k = dict.fromkeys(k_range, 0)
bug_report_number = 0
for bug_report, bug_report_files_dataframe in stage2_result.groupby(level=0, sort=False):
        min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
        bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
        sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
#         print(sorted_df)
        precision_at_k = []
        # precision per k in range
        tmp = sorted_df
        a = range(1, tmp.shape[0] + 1)
        tmp['position'] = pd.Series(a, index=tmp.index)
        precision_at_k = []
        # precision per k in range
        tmp = sorted_df
        a = range(1, tmp.shape[0] + 1)
        tmp['position'] = pd.Series(a, index=tmp.index)
        print(tmp)
        large_k_p = tmp[(tmp['used_in_fix'] == 1.0)]['position'].tolist()
#         print('large_k_p :',large_k_p)
        unique_results = sorted_df['result'].unique().tolist()
        unique_results.sort()
#         print('unique_results',unique_results)
        for fk in large_k_p:
            k = int(fk)
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = (largest_at_k['used_in_fix'] == 1.0).sum()

            p = float(real_fixes_at_k) / float(k)
            precision_at_k.append(p)
#         print('precision_at_k :',precision_at_k)
        average_precision = pd.Series(precision_at_k).mean()
#         print('average_precision :',average_precision)
        
        # accuracy
        for k in k_range:
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = largest_at_k['used_in_fix'][(largest_at_k['used_in_fix'] == 1.0)].count()
            if real_fixes_at_k >= 1:
                accuracy_at_k[k] += 1
        print('accuracy_at_k :',accuracy_at_k)
        
        # reciprocal rank
        indexes_of_fixes = np.flatnonzero(sorted_df['used_in_fix'] == 1.0)
        if indexes_of_fixes.size == 0:
            reciprocal_ranks.append(0.0)
        else:
            first_index = indexes_of_fixes[0]
            reciprocal_rank = 1.0 / (first_index + 1)
            reciprocal_ranks.append(reciprocal_rank)
        # bug number
        bug_report_number += 1
        print('reciprocal_ranks :',reciprocal_ranks)
        if bug_report_number==15:
            break

         used_in_fix    result  position
bid                                     
d2fc065            0  0.245010         1
d2fc065            0  0.187732         2
d2fc065            0  0.174126         3
d2fc065            0  0.170090         4
d2fc065            0  0.158262         5
d2fc065            0  0.154582         6
d2fc065            0  0.142874         7
d2fc065            0  0.133595         8
d2fc065            0  0.130270         9
d2fc065            0  0.129583        10
d2fc065            0  0.128816        11
d2fc065            0  0.125114        12
d2fc065            0  0.124748        13
d2fc065            0  0.121525        14
d2fc065            1  0.118382        15
accuracy_at_k : {1: 0, 2: 0, 3: 0, 4: 0, 5: 0, 6: 0, 7: 0, 8: 0, 9: 0, 10: 0, 11: 0, 12: 0, 13: 0, 14: 0, 15: 1, 16: 1, 17: 1, 18: 1, 19: 1, 20: 1}
reciprocal_ranks : [0.06666666666666667]
         used_in_fix    result  position
bid                                     
13de9cb            0  0.174151  

accuracy_at_k : {1: 0, 2: 0, 3: 0, 4: 0, 5: 0, 6: 0, 7: 1, 8: 1, 9: 1, 10: 1, 11: 1, 12: 1, 13: 2, 14: 2, 15: 3, 16: 3, 17: 4, 18: 4, 19: 4, 20: 4}
reciprocal_ranks : [0.06666666666666667, 0.058823529411764705, 0.03125, 0.07692307692307693, 0.02040816326530612, 0.025, 0.024390243902439025, 0.021739130434782608, 0.023255813953488372, 0.029411764705882353, 0.14285714285714285]
         used_in_fix    result  position
bid                                     
c9dfe7c            0  0.200119         1
c9dfe7c            0  0.186298         2
c9dfe7c            0  0.181839         3
c9dfe7c            0  0.173913         4
c9dfe7c            0  0.170960         5
c9dfe7c            0  0.167831         6
c9dfe7c            0  0.162003         7
c9dfe7c            0  0.155552         8
c9dfe7c            0  0.154997         9
c9dfe7c            0  0.153126        10
c9dfe7c            0  0.150775        11
c9dfe7c            0  0.143549        12
c9dfe7c            0  0.143471        13
c9dfe7c

In [ ]:
# task1_list=[]
# for line in res:
#     print(line)
#     task1=dict()
#     task1['id_']=line[0]
#     task1['res']=line[1]
#     task1_list.append(task1)
# with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task2/sort_2_6_train_0524_nolabel.json','w',encoding='utf-8') as f_out:
#     for task1 in task1_list:
#         out_line = json.dumps(task1, ensure_ascii=False) + '\n'
#         f_out.write(out_line)

In [3]:
swt_all_results_df_before.reset_index(level=1, drop=True, inplace=True)

In [4]:
swt_all_results_df_before.head()

used_in_fix        f1    result
bid                                     
a0c9251          0.0  0.030239  0.588582
a0c9251          0.0  0.010100  0.556395
a0c9251          0.0  0.026023  0.549675
a0c9251          0.0  0.026685  0.550011
a0c9251          0.0  0.040819  0.600155

# 使用tokenizedSource summary+description，按照CodeSearch组织数据

In [11]:
from nltk.corpus import stopwords
from collections import Counter
from nltk import wordpunct_tokenize
from nltk.stem.porter import PorterStemmer
from re import finditer
stemmer = PorterStemmer()

In [12]:
def camel_case_split(identifier):
    matches = finditer('.+?(?:(?<=[a-z])(?=[A-Z])|(?<=[A-Z])(?=[A-Z][a-z])|$)', identifier)
    return [m.group(0) for m in matches]
def mergeTokenziedSource(tokenizedSource):#dict 类型
    return ' '.join(tokenizedSource.keys())
removed = u'!"#%&\'()*+,-./:;<=>?@[\]^_`{|}~1234567890'
utf_translate_table = dict((ord(char), u' ') for char in removed)
stop_words = set(stopwords.words('english'))

def tokenize(text, stemmer):
    sanitized_text = text.translate(utf_translate_table)
    tokens = wordpunct_tokenize(sanitized_text)
    all_tokens = []
    for token in tokens:
        additional_tokens = camel_case_split(token)
        if len(additional_tokens)>1:
            for additional_token in additional_tokens:
                all_tokens.append(additional_token)
        all_tokens.append(token)
    return Counter([stemmer.stem(token) for token in all_tokens if token.lower() not in stop_words])

In [ ]:
mergeTokenziedSource(tokenize('DirectoryDialog There is no disk in the drive . Please insert a disk into drive Device Harddisk0 DR0 Any operation which brings up a file dialog box rooted at "My Computer" tosses up a dialog box with the above error message whenever a harddrive is expanded . Click cancel or try again on dialog ( has cancel , try again , and continue ) twice , and then it opens up the disk , and proceeds normally . If you un - expand a drive , it does the same thing . Then again when you re - expand a drive . Examples : Import - > File System - > click Browse Feature . xml - > Export - > click Browse I have seen this all the way back through M4 . May have existed sooner . Currently using RC3 . Platform : Windows 2K SP3',stemmer))

In [13]:
#TODO
project='swt'
def clean_string_report(string):
    outtmp=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
#     outtmp=[token for token in outtmp if token not in stop_words]
#     outtmp= [token for token in outtmp if token not in java_keywords]
    outtmp=[token for token in outtmp if token.isalnum() ]
    return ' '.join(outtmp)
def clean_string(string):
    outstring_list=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
    return ' '.join(outstring_list)
def mergeTokenziedSource(tokenizedSource):#dict 类型
    return ' '.join(tokenizedSource.keys())
def clean_code_names(ast_file):
    names=ast_file['classNames']+ast_file['superclassNames']+ast_file['interfaceNames']+ast_file['methodNames']+ast_file['variableNames']
    names=[' '.join(name.split('.')) for name in names]
#     print(names)
    return ' '.join(names)

def generate_from_raw(train_k_path,out_path):
    #生成fine-tune需要的数据集
    #train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv' 
    #out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.txt'
    train_k=pd.read_csv(train_k_path)
    train_k.set_index(['bid','fid'], inplace = True)
    train_k.head(10)
    #取bid所对应的report
    bid_list=list(train_k.index.get_level_values(0).unique())
    len(bid_list)
    summarys=[]
    descriptions=[]
    for bug_report_id in bid_list:
        current_bug_report = bug_reports[bug_report_id]['bug_report']
        summarys.append(current_bug_report['summary'])
        descriptions.append(current_bug_report['description'])
        
    report_dataFrame=pd.DataFrame({'summary':summarys,'description':descriptions},index=bid_list)
    report_dataFrame.index.names=['bid']
    def remove_twoHeadWord(string):
        contents=string.split(' ')[2:]
        return ' '.join(contents)
    
    report_dataFrame['summary']=report_dataFrame['summary'].apply(remove_twoHeadWord)
    report_dataFrame.head()
    all_ast_index=list(train_k.index.get_level_values(1).unique())
    type(all_ast_index)
    all_ast_file_source=[]
    all_ast_file_names=[]
    all_ast_file_methods=[]
    for ast_index in all_ast_index:
    #     print(ast_index)
        ast_file = pickle.loads(ast_cache_collection_db[ast_index])
        all_ast_file_source.append(clean_string_code(ast_file['rawSourceContent']))
        all_ast_file_names.append(clean_code_names(ast_file))
        top_k_method,num=get_method_top_k(ast_file['methodContent'],10)
        print('total method num :',len(ast_file['methodContent']),' 有方法体的函数数量 :',num,' choosed method num :',len(top_k_method))
        all_ast_file_methods.append(top_k_method )
     
    # all_ast_index 
    all_ast_index_dataframe=pd.DataFrame({'all_ast_file_methods':all_ast_file_methods,
                                          'source':all_ast_file_source,'names':all_ast_file_names},index=all_ast_index)#,'tokenizedComments':all_ast_file_tokenizedComments
#     for ast_index in all_ast_index:
#     #     print(ast_index)
#         ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
        
#         all_ast_file_methodContent.append(mergeTokenziedSource(ast_file['tokenizedSource']))
    # all_ast_index
#     all_ast_index_dataframe=pd.DataFrame({'tokenizedSource':all_ast_file_methodContent},index=all_ast_index)
    # print(all_ast_index_dataframe.head())
    print(all_ast_index_dataframe.shape)
    # all_ast_index_dataframe.set_index(["ast_index"], inplace=True)
    # all_ast_index_dataframe
    all_ast_index_dataframe.index.names=['fid']
    all_ast_index_dataframe.head(2)
    #开始连接字段
    all_methodContent_index_dataframe=all_ast_index_dataframe.join(train_k,how='inner')
    all_methodContent_index_dataframe.head()
    all_report_methodContent_index_dataframe=report_dataFrame.join(all_methodContent_index_dataframe,how='inner')
    all_report_methodContent_index_dataframe.head()
    
    task1_list=[]
    all_report_methodContent_index_dataframe.fillna("",inplace=True)
  
    sum_label=0
    for i,(index, row) in enumerate(all_report_methodContent_index_dataframe.iterrows()):
    #     print(index[0],index[1],row['summary'],row['description'],row['methodContent'],row['used_in_fix'])
#         if len(row['tokenizedSource'])==0:
#             continue
        guid='_'.join([index[0],index[1]])
        
#         q_paras=clean_string(row['summary']+' '+row['description'])
#         q_paras_tokenzied=[mergeTokenziedSource(tokenize(row['summary']+' '+row['description'],stemmer))]
        q_paras_not_tokenzied=[clean_string_report(row['summary']+' '+row['description'])]
#         c_paras=[row['source']]#,row['tokenizedComments'],,row['tokenizedClassNames'],,row['names']
#                  row['tokenizedMethodNames'],row['tokenizedVariableNames']
        c_paras=[]
        c_paras.extend(row['all_ast_file_methods'])
#         print(i,'summary :',type(row['summary']),'description :',type(row['description']),'len summary :',len(q_paras.split()),'source :',len(c_paras.split()))
#         summary_len.append(len(q_paras[0].split()))
#         source_len.append(len(c_paras.split()))
        label=str(int(row['used_in_fix']))
#         for q in q_paras_tokenzied:
#             for c in c_paras:
#                 list_all=[label,guid,'hdj',q,c]
#                 task1_list.append('<CODESPLIT>'.join(list_all))
#         c_paras=[]
#         c_paras.extend(row['all_ast_file_methods'])
        for q in q_paras_not_tokenzied:
            for c in c_paras:
                list_all=[label,guid,'hdj',q,c]
                task1_list.append('<CODESPLIT>'.join(list_all))
#         list_all=[label,guid,'hdj',q_paras,c_paras]
#         task1_list.append('<CODESPLIT>'.join(list_all))
#         if i==10:
#             break
    print(task1_list[0])
    with open(out_path,'w',encoding='utf-8') as f_out:
        for task1 in task1_list:
            f_out.write(task1+'\n')
train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1_train.csv' 
train_out_path='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1_train_source_nomethod.txt'  
val_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1_val.csv'
val_out_path='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/train_2hard_1_val_source_nomethod.txt'
test_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/test_2hard_2.csv'
test_out_path='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/test_2hard_2_source_nomethod.txt'
summary_len=[]
source_len=[]
generate_from_raw(train_k_path,train_out_path)
generate_from_raw(val_k_path,val_out_path)
generate_from_raw(test_k_path,test_out_path)

NameError: name 'pd' is not defined

In [ ]:
def mergeTokenziedSource(tokenizedSource):#dict 类型
    return ' '.join(tokenizedSource.keys())
     
def generate(train_k_path,out_path):
    #生成fine-tune需要的数据集
    #train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv' 
    #out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.txt'
    train_k=pd.read_csv(train_k_path)
    train_k.set_index(['bid','fid'], inplace = True)
    train_k.head(10)
    #取bid所对应的report
    bid_list=list(train_k.index.get_level_values(0).unique())
    len(bid_list)
    summarys=[]
    descriptions=[]
    for bug_report_id in bid_list:
        current_bug_report = bug_reports[bug_report_id]['bug_report']
        summarys.append(current_bug_report['summary'])
        descriptions.append(current_bug_report['description'])
        
    report_dataFrame=pd.DataFrame({'summary':summarys,'description':descriptions},index=bid_list)
    report_dataFrame.index.names=['bid']
    def remove_twoHeadWord(string):
        contents=string.split(' ')[2:]
        return ' '.join(contents)
    report_dataFrame['summary']=report_dataFrame['summary'].apply(remove_twoHeadWord)
    report_dataFrame.head()
    all_ast_index=list(train_k.index.get_level_values(1).unique())
    type(all_ast_index)
    all_ast_file_tokenizedSource=[]
    all_ast_file_methodContent=[]
    all_ast_file_tokenizedMethods=[]
    all_ast_file_tokenizedClassNames =[]
    all_ast_file_tokenizedMethodNames=[]
    all_ast_file_tokenizedVariableNames=[]
    all_ast_file_tokenizedComments =[]
    all_ast_file_methods=[]
    for ast_index in all_ast_index:
    #     print(ast_index)
        ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
        all_ast_file_tokenizedSource.append(convert_dict2string_set([ast_file['tokenizedSource']]))
        all_ast_file_tokenizedMethods.append(convert_dict2string_set(ast_file['tokenizedMethods']))
        top_k_method,num=get_method_top_k(ast_file['methodContent'],20)
        print('total method num :',len(ast_file['methodContent']),' 有方法体的函数数量 :',num,' choosed method num :',len(top_k_method))
        all_ast_file_methods.append(top_k_method )
        all_ast_file_tokenizedClassNames.append(convert_dict2string_set(ast_file['tokenizedClassNames']))
        all_ast_file_tokenizedMethodNames.append(convert_dict2string_set(ast_file['tokenizedMethodNames']))
        all_ast_file_tokenizedVariableNames.append(convert_dict2string_set(ast_file['tokenizedVariableNames']))
        all_ast_file_tokenizedComments.append(convert_dict2string_set(ast_file['tokenizedComments']))
    # all_ast_index 
    all_ast_index_dataframe=pd.DataFrame({'all_ast_file_methods':all_ast_file_methods,'tokenizedSource':all_ast_file_tokenizedSource,'tokenizedMethods':all_ast_file_tokenizedMethods,
                                          'tokenizedClassNames':all_ast_file_tokenizedClassNames,'tokenizedMethodNames':all_ast_file_tokenizedMethodNames,
                                          'tokenizedVariableNames':all_ast_file_tokenizedVariableNames},index=all_ast_index)#,'tokenizedComments':all_ast_file_tokenizedComments
#     for ast_index in all_ast_index:
#     #     print(ast_index)
#         ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
        
#         all_ast_file_methodContent.append(mergeTokenziedSource(ast_file['tokenizedSource']))
    # all_ast_index
#     all_ast_index_dataframe=pd.DataFrame({'tokenizedSource':all_ast_file_methodContent},index=all_ast_index)
    # print(all_ast_index_dataframe.head())
    print(all_ast_index_dataframe.shape)
    # all_ast_index_dataframe.set_index(["ast_index"], inplace=True)
    # all_ast_index_dataframe
    all_ast_index_dataframe.index.names=['fid']
    all_ast_index_dataframe.head(2)
    #开始连接字段
    all_methodContent_index_dataframe=all_ast_index_dataframe.join(train_k,how='inner')
    all_methodContent_index_dataframe.head()
    all_report_methodContent_index_dataframe=report_dataFrame.join(all_methodContent_index_dataframe,how='inner')
    all_report_methodContent_index_dataframe.head()
    
    task1_list=[]
    all_report_methodContent_index_dataframe.fillna("",inplace=True)
    def clean_string(string):
        outstring_list=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
        return ' '.join(outstring_list)
    sum_label=0
    for i,(index, row) in enumerate(all_report_methodContent_index_dataframe.iterrows()):
    #     print(index[0],index[1],row['summary'],row['description'],row['methodContent'],row['used_in_fix'])
#         if len(row['tokenizedSource'])==0:
#             continue
        guid='_'.join([index[0],index[1]])
        
#         q_paras=clean_string(row['summary']+' '+row['description'])
        q_paras_tokenzied=[mergeTokenziedSource(tokenize(row['summary']+' '+row['description'],stemmer))]
        q_paras_not_tokenzied=[clean_string_report(row['summary']+' '+row['description'])]
        c_paras=[row['tokenizedSource'],row['tokenizedMethods']]#,row['tokenizedComments'],,row['tokenizedClassNames'],
#                  row['tokenizedMethodNames'],row['tokenizedVariableNames']
#         c_paras=[]
#         c_paras.extend(row['all_ast_file_methods'])
#         print(i,'summary :',type(row['summary']),'description :',type(row['description']),'len summary :',len(q_paras.split()),'source :',len(c_paras.split()))
#         summary_len.append(len(q_paras[0].split()))
#         source_len.append(len(c_paras.split()))
        label=str(int(row['used_in_fix']))
        for q in q_paras_tokenzied:
            for c in c_paras:
                list_all=[label,guid,'hdj',q,c]
                task1_list.append('<CODESPLIT>'.join(list_all))
        c_paras=[]
        c_paras.extend(row['all_ast_file_methods'])
        for q in q_paras_not_tokenzied:
            for c in c_paras:
                list_all=[label,guid,'hdj',q,c]
                task1_list.append('<CODESPLIT>'.join(list_all))
#         list_all=[label,guid,'hdj',q_paras,c_paras]
#         task1_list.append('<CODESPLIT>'.join(list_all))
#         if i==10:
#             break
    print(task1_list[0])
    with open(out_path,'w',encoding='utf-8') as f_out:
        for task1 in task1_list:
            f_out.write(task1+'\n')
train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/train_2hard_1_train.csv' 
train_out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/train_2hard_1_train_2tok5meth_data.txt'  
val_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/train_2hard_1_val.csv'
val_out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/train_2hard_1_val_2tok5meth_data.txt'
test_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/test_2hard_2.csv'
test_out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/test_2hard_2_2tok5meth_data.txt'
summary_len=[]
source_len=[]
generate(train_k_path,train_out_path)
generate(val_k_path,val_out_path)
generate(test_k_path,test_out_path)

total method num : 8  有方法体的函数数量 : 8  choosed method num : 5
total method num : 617  有方法体的函数数量 : 107  choosed method num : 5
total method num : 7  有方法体的函数数量 : 7  choosed method num : 5
total method num : 8  有方法体的函数数量 : 8  choosed method num : 5
total method num : 7  有方法体的函数数量 : 7  choosed method num : 5
total method num : 8  有方法体的函数数量 : 8  choosed method num : 5
total method num : 224  有方法体的函数数量 : 221  choosed method num : 5
total method num : 56  有方法体的函数数量 : 56  choosed method num : 5
total method num : 60  有方法体的函数数量 : 60  choosed method num : 5
total method num : 154  有方法体的函数数量 : 154  choosed method num : 5
total method num : 22  有方法体的函数数量 : 22  choosed method num : 5
total method num : 147  有方法体的函数数量 : 147  choosed method num : 5
total method num : 72  有方法体的函数数量 : 72  choosed method num : 5
total method num : 64  有方法体的函数数量 : 64  choosed method num : 5
total method num : 624  有方法体的函数数量 : 1  choosed method num : 1
total method num : 80  有方法体的函数数量 : 80  choosed method num : 5
total meth

total method num : 234  有方法体的函数数量 : 231  choosed method num : 5
total method num : 103  有方法体的函数数量 : 103  choosed method num : 5
total method num : 323  有方法体的函数数量 : 318  choosed method num : 5
total method num : 66  有方法体的函数数量 : 66  choosed method num : 5
total method num : 71  有方法体的函数数量 : 71  choosed method num : 5
total method num : 74  有方法体的函数数量 : 74  choosed method num : 5
total method num : 158  有方法体的函数数量 : 158  choosed method num : 5
total method num : 6  有方法体的函数数量 : 6  choosed method num : 5
total method num : 14  有方法体的函数数量 : 14  choosed method num : 5
total method num : 65  有方法体的函数数量 : 65  choosed method num : 5
total method num : 229  有方法体的函数数量 : 226  choosed method num : 5
total method num : 119  有方法体的函数数量 : 119  choosed method num : 5
total method num : 15  有方法体的函数数量 : 15  choosed method num : 5
total method num : 157  有方法体的函数数量 : 157  choosed method num : 5
total method num : 47  有方法体的函数数量 : 47  choosed method num : 5
total method num : 34  有方法体的函数数量 : 34  choosed method num 

total method num : 19  有方法体的函数数量 : 19  choosed method num : 5
total method num : 60  有方法体的函数数量 : 60  choosed method num : 5
total method num : 89  有方法体的函数数量 : 89  choosed method num : 5
total method num : 79  有方法体的函数数量 : 79  choosed method num : 5
total method num : 68  有方法体的函数数量 : 68  choosed method num : 5
total method num : 53  有方法体的函数数量 : 53  choosed method num : 5
total method num : 9  有方法体的函数数量 : 9  choosed method num : 5
total method num : 34  有方法体的函数数量 : 34  choosed method num : 5
total method num : 69  有方法体的函数数量 : 69  choosed method num : 5
total method num : 26  有方法体的函数数量 : 26  choosed method num : 5
total method num : 23  有方法体的函数数量 : 23  choosed method num : 5
total method num : 69  有方法体的函数数量 : 69  choosed method num : 5
total method num : 71  有方法体的函数数量 : 71  choosed method num : 5
total method num : 65  有方法体的函数数量 : 65  choosed method num : 5
total method num : 315  有方法体的函数数量 : 310  choosed method num : 5
total method num : 65  有方法体的函数数量 : 65  choosed method num : 5
total me

total method num : 24  有方法体的函数数量 : 24  choosed method num : 5
total method num : 107  有方法体的函数数量 : 107  choosed method num : 5
total method num : 629  有方法体的函数数量 : 1  choosed method num : 1
total method num : 88  有方法体的函数数量 : 88  choosed method num : 5
total method num : 57  有方法体的函数数量 : 57  choosed method num : 5
total method num : 10  有方法体的函数数量 : 10  choosed method num : 5
total method num : 48  有方法体的函数数量 : 48  choosed method num : 5
total method num : 31  有方法体的函数数量 : 31  choosed method num : 5
total method num : 14  有方法体的函数数量 : 14  choosed method num : 5
total method num : 319  有方法体的函数数量 : 314  choosed method num : 5
total method num : 91  有方法体的函数数量 : 91  choosed method num : 5
total method num : 37  有方法体的函数数量 : 37  choosed method num : 5
total method num : 9  有方法体的函数数量 : 9  choosed method num : 5
total method num : 63  有方法体的函数数量 : 63  choosed method num : 5
total method num : 12  有方法体的函数数量 : 12  choosed method num : 5
total method num : 13  有方法体的函数数量 : 13  choosed method num : 5
total 

total method num : 326  有方法体的函数数量 : 321  choosed method num : 5
total method num : 42  有方法体的函数数量 : 42  choosed method num : 5
total method num : 47  有方法体的函数数量 : 47  choosed method num : 5
total method num : 25  有方法体的函数数量 : 25  choosed method num : 5
total method num : 27  有方法体的函数数量 : 27  choosed method num : 5
total method num : 17  有方法体的函数数量 : 17  choosed method num : 5
total method num : 33  有方法体的函数数量 : 33  choosed method num : 5
total method num : 329  有方法体的函数数量 : 324  choosed method num : 5
total method num : 158  有方法体的函数数量 : 158  choosed method num : 5
total method num : 641  有方法体的函数数量 : 1  choosed method num : 1
total method num : 75  有方法体的函数数量 : 75  choosed method num : 5
total method num : 74  有方法体的函数数量 : 74  choosed method num : 5
total method num : 65  有方法体的函数数量 : 65  choosed method num : 5
total method num : 1  有方法体的函数数量 : 1  choosed method num : 1
total method num : 326  有方法体的函数数量 : 321  choosed method num : 5
total method num : 8  有方法体的函数数量 : 8  choosed method num : 5
tota

...

total method num : 112  有方法体的函数数量 : 112  choosed method num : 5
total method num : 1  有方法体的函数数量 : 1  choosed method num : 1
total method num : 109  有方法体的函数数量 : 109  choosed method num : 5
total method num : 179  有方法体的函数数量 : 179  choosed method num : 5
total method num : 71  有方法体的函数数量 : 71  choosed method num : 5
total method num : 33  有方法体的函数数量 : 33  choosed method num : 5
total method num : 247  有方法体的函数数量 : 247  choosed method num : 5
total method num : 86  有方法体的函数数量 : 86  choosed method num : 5
total method num : 92  有方法体的函数数量 : 92  choosed method num : 5
total method num : 93  有方法体的函数数量 : 93  choosed method num : 5
total method num : 226  有方法体的函数数量 : 226  choosed method num : 5
total method num : 260  有方法体的函数数量 : 260  choosed method num : 5
total method num : 72  有方法体的函数数量 : 72  choosed method num : 5
total method num : 189  有方法体的函数数量 : 189  choosed method num : 5
total method num : 169  有方法体的函数数量 : 169  choosed method num : 5
total method num : 179  有方法体的函数数量 : 179  choosed method 

total method num : 4  有方法体的函数数量 : 4  choosed method num : 4
total method num : 110  有方法体的函数数量 : 110  choosed method num : 5
total method num : 396  有方法体的函数数量 : 396  choosed method num : 5
total method num : 104  有方法体的函数数量 : 104  choosed method num : 5
total method num : 35  有方法体的函数数量 : 35  choosed method num : 5
total method num : 51  有方法体的函数数量 : 51  choosed method num : 5
total method num : 91  有方法体的函数数量 : 91  choosed method num : 5
total method num : 3  有方法体的函数数量 : 3  choosed method num : 3
total method num : 31  有方法体的函数数量 : 31  choosed method num : 5
total method num : 20  有方法体的函数数量 : 20  choosed method num : 5
total method num : 25  有方法体的函数数量 : 25  choosed method num : 5
total method num : 192  有方法体的函数数量 : 192  choosed method num : 5
total method num : 136  有方法体的函数数量 : 136  choosed method num : 5
total method num : 143  有方法体的函数数量 : 143  choosed method num : 5
total method num : 396  有方法体的函数数量 : 396  choosed method num : 5
total method num : 275  有方法体的函数数量 : 275  choosed method num 

total method num : 21  有方法体的函数数量 : 21  choosed method num : 5
total method num : 24  有方法体的函数数量 : 24  choosed method num : 5
total method num : 24  有方法体的函数数量 : 24  choosed method num : 5
total method num : 21  有方法体的函数数量 : 21  choosed method num : 5
total method num : 1  有方法体的函数数量 : 1  choosed method num : 1
total method num : 67  有方法体的函数数量 : 67  choosed method num : 5
total method num : 71  有方法体的函数数量 : 71  choosed method num : 5
total method num : 72  有方法体的函数数量 : 72  choosed method num : 5
total method num : 37  有方法体的函数数量 : 37  choosed method num : 5
total method num : 195  有方法体的函数数量 : 195  choosed method num : 5
total method num : 97  有方法体的函数数量 : 97  choosed method num : 5
total method num : 113  有方法体的函数数量 : 113  choosed method num : 5
total method num : 141  有方法体的函数数量 : 141  choosed method num : 5
total method num : 146  有方法体的函数数量 : 146  choosed method num : 5
total method num : 316  有方法体的函数数量 : 314  choosed method num : 5
total method num : 92  有方法体的函数数量 : 92  choosed method num : 5


total method num : 175  有方法体的函数数量 : 175  choosed method num : 5
total method num : 114  有方法体的函数数量 : 114  choosed method num : 5
total method num : 121  有方法体的函数数量 : 121  choosed method num : 5
total method num : 173  有方法体的函数数量 : 173  choosed method num : 5
total method num : 204  有方法体的函数数量 : 204  choosed method num : 5
total method num : 171  有方法体的函数数量 : 171  choosed method num : 5
total method num : 73  有方法体的函数数量 : 73  choosed method num : 5
total method num : 112  有方法体的函数数量 : 112  choosed method num : 5
total method num : 104  有方法体的函数数量 : 104  choosed method num : 5
total method num : 96  有方法体的函数数量 : 96  choosed method num : 5
total method num : 15  有方法体的函数数量 : 15  choosed method num : 5
total method num : 164  有方法体的函数数量 : 164  choosed method num : 5
total method num : 166  有方法体的函数数量 : 166  choosed method num : 5
total method num : 29  有方法体的函数数量 : 29  choosed method num : 5
total method num : 146  有方法体的函数数量 : 146  choosed method num : 5
total method num : 57  有方法体的函数数量 : 57  choosed m

total method num : 627  有方法体的函数数量 : 627  choosed method num : 5
total method num : 41  有方法体的函数数量 : 41  choosed method num : 5
total method num : 61  有方法体的函数数量 : 61  choosed method num : 5
total method num : 92  有方法体的函数数量 : 92  choosed method num : 5
total method num : 71  有方法体的函数数量 : 71  choosed method num : 5
total method num : 93  有方法体的函数数量 : 93  choosed method num : 5
total method num : 2609  有方法体的函数数量 : 1216  choosed method num : 5
total method num : 113  有方法体的函数数量 : 113  choosed method num : 5
total method num : 45  有方法体的函数数量 : 45  choosed method num : 5
total method num : 195  有方法体的函数数量 : 195  choosed method num : 5
total method num : 67  有方法体的函数数量 : 67  choosed method num : 5
total method num : 117  有方法体的函数数量 : 117  choosed method num : 5
total method num : 50  有方法体的函数数量 : 50  choosed method num : 5
total method num : 420  有方法体的函数数量 : 420  choosed method num : 5
total method num : 7  有方法体的函数数量 : 7  choosed method num : 5
total method num : 63  有方法体的函数数量 : 63  choosed method num 

In [16]:
class InputFeatures(object):
    """A single training/test features for a example."""
    def __init__(self,
                 code_tokens,
                 code_ids,
                 nl_tokens,
                 nl_ids,
                 url,
                 label

    ):
        self.code_tokens = code_tokens
        self.code_ids = code_ids
        self.nl_tokens = nl_tokens
        self.nl_ids = nl_ids
        self.url=url
        self.label=label
        
def convert_examples_to_features(js,tokenizer,args):
    #code
    if args.code:
        code=js['code_tokens']
        code_tokens=tokenizer.tokenize(code)[:args.code_length-2]
        code_tokens =[tokenizer.cls_token]+code_tokens+[tokenizer.sep_token]
        code_ids =  tokenizer.convert_tokens_to_ids(code_tokens)
        padding_length = args.code_length - len(code_ids)
        code_ids+=[tokenizer.pad_token_id]*padding_length
        nl_tokens=[]
        nl_ids=[]
    else: 
        nl=js['docstring_tokens']
        nl_tokens=tokenizer.tokenize(nl)[:args.nl_length-2]
        nl_tokens =[tokenizer.cls_token]+nl_tokens+[tokenizer.sep_token]
        nl_ids =  tokenizer.convert_tokens_to_ids(nl_tokens)
        padding_length = args.nl_length - len(nl_ids)
        nl_ids+=[tokenizer.pad_token_id]*padding_length    
        code_tokens=[]
        code_ids=[]
    return InputFeatures(code_tokens,code_ids,nl_tokens,nl_ids,js['url'],js['label'])

class TextDataset(Dataset):
    def __init__(self, tokenizer, args, file_path=None):
        self.examples = []
        data=[]
        with open(file_path) as f:
            for i, line in enumerate(f):
                line=line.strip()
                contents=line.split('<CODESPLIT>')
                js=dict()
                js['code_tokens']=contents[4]
                js['docstring_tokens']=contents[3]
                js['url']=contents[1]
                js['label']=contents[0]
                data.append(js)
#                 if i==50:
#                     break
        for js in data:
            self.examples.append(convert_examples_to_features(js,tokenizer,args))
                                      
        
    def __len__(self):
        return len(self.examples)

    def __getitem__(self, i):   
        return (torch.tensor(self.examples[i].code_ids),torch.tensor(self.examples[i].nl_ids))

In [17]:
report_id_set=set()
with open('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/test_2hard_2_data_less.txt','r',encoding='utf-8') as f_in:#test_2hard_2_source_nomethod_less
    with open('/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/report.txt','w',encoding='utf-8') as f_out:
        for i,line in enumerate(f_in):
            contents=line.split('<CODESPLIT>')
#             print(i,contents[1],contents[0])
            report_id=contents[1].split('_')[0]
            if report_id not in report_id_set:
                report_id_set.add(report_id)
                f_out.write(line)
#             if i==300:
#                 break

In [30]:
def calculate_metrics(verification_df, k_range=range(1, 21)):
    average_precision_per_bug_report = []
    reciprocal_ranks = []
    # calculate per each query (bug report)
    accuracy_at_k = dict.fromkeys(k_range, 0)
    bug_report_number = 0
    for bug_report, bug_report_files_dataframe in verification_df.groupby(level=0, sort=False):
        isLabel = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]
        if isLabel.shape[0]==0:
            continue
        min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
        bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
        sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
        if sorted_df.shape[0] == 0:
            sorted_df = bug_report_files_dataframe.copy().sort_values(ascending=False, by=['result'])
            # print((bug_report_files_dataframe['used_in_fix'] == 1.0).sum())

        precision_at_k = []
        # precision per k in range
        tmp = sorted_df
        a = range(1, tmp.shape[0] + 1)
        tmp['position'] = pd.Series(a, index=tmp.index)

        large_k_p = tmp[(tmp['used_in_fix'] == 1.0)]['position'].tolist()
        unique_results = sorted_df['result'].unique().tolist()
        unique_results.sort()
        for fk in large_k_p:
            k = int(fk)
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = (largest_at_k['used_in_fix'] == 1.0).sum()

            p = float(real_fixes_at_k) / float(k)
            precision_at_k.append(p)

        # average precision is sum of k precisions divided by K
        # K is set of positions of relevant documents in the ranked list
        average_precision = pd.Series(precision_at_k).mean()
        # average_precision = pd.Series(precision_at_k).sum() / float(large_k)
        average_precision_per_bug_report.append(average_precision)

        # accuracy
        for k in k_range:
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = largest_at_k['used_in_fix'][(largest_at_k['used_in_fix'] == 1.0)].count()
            if real_fixes_at_k >= 1:
                accuracy_at_k[k] += 1

        # reciprocal rank
        indexes_of_fixes = np.flatnonzero(sorted_df['used_in_fix'] == 1.0)
        if indexes_of_fixes.size == 0:
            reciprocal_ranks.append(0.0)
        else:
            first_index = indexes_of_fixes[0]
            reciprocal_rank = 1.0 / (first_index + 1)
            reciprocal_ranks.append(reciprocal_rank)
        # bug number
        bug_report_number += 1

        del bug_report, bug_report_files_dataframe

    # print("average_precision_per_bug_report", average_precision_per_bug_report)
    mean_average_precision = pd.Series(average_precision_per_bug_report).mean()
    # print('mean average precision', mean_average_precision)
    mean_reciprocal_rank = pd.Series(reciprocal_ranks).mean()
    # print('mean reciprocal rank', mean_reciprocal_rank)
    print('accuracy_at_k :',accuracy_at_k)
    for k in k_range:
        accuracy_at_k[k] = accuracy_at_k[k] / bug_report_number
        # print('accuracy for k', accuracy_at_k[k], k)
    return accuracy_at_k, mean_average_precision, mean_reciprocal_rank
class Model(nn.Module):   
    def __init__(self, encoder):
        super(Model, self).__init__()
        self.encoder = encoder
      
    def forward(self, code_inputs=None, nl_inputs=None): 
        if code_inputs is not None:
            return self.encoder(code_inputs,attention_mask=code_inputs.ne(1))[1]
        else:
            return self.encoder(nl_inputs,attention_mask=nl_inputs.ne(1))[1]
class args(object):
    """A single set of features of data."""

    def __init__(self):
        self.code_length= 512 
        self.nl_length =128
        self.train_batch_size =32 
        self.eval_batch_size =64 
        self.learning_rate= 2e-5 
        
        self.output_dir='/data/hdj/data/CodeBERT/Siamese-model/saved_models/java'
        self.model_name_or_path='microsoft/codebert-base'
        self.device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
args=args()
tokenizer = RobertaTokenizer.from_pretrained('microsoft/codebert-base')
query_file_name='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/report.txt'
args.code=False
query_dataset = TextDataset(tokenizer, args, query_file_name)
query_sampler = SequentialSampler(query_dataset)
query_dataloader = DataLoader(query_dataset, sampler=query_sampler, batch_size=args.eval_batch_size,num_workers=4)

In [2]:
import numpy as np
nl=[[1,2],[3,4]]
np.save("filename.npy",nl)
b = np.load("filename.npy")

In [5]:
type(b[0])

numpy.ndarray

In [31]:
args.code=True
code_file_name='/data/hdj/tracking_buggy_files/joblib_memmap_'+project+'/one_vs_two/test_2hard_2_data_less.txt'
code_dataset = TextDataset(tokenizer, args, code_file_name)
code_sampler = SequentialSampler(code_dataset)
code_dataloader = DataLoader(code_dataset, sampler=code_sampler, batch_size=512,num_workers=4)    

In [21]:
model = RobertaModel.from_pretrained(args.model_name_or_path)    
model=Model(model)

In [22]:
checkpoint_prefix = 'checkpoint-best-mrr/model.bin'
# checkpoint_prefix = 'checkpoint-best-hdj/model.bin'
output_dir = os.path.join(args.output_dir, '{}'.format(checkpoint_prefix)) 
print(output_dir)
model.load_state_dict(torch.load(output_dir),strict=False)      
model.to(args.device)

/data/hdj/data/CodeBERT/Siamese-model/saved_models/java/checkpoint-best-mrr/model.bin


Model(
  (encoder): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0): RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps

In [32]:
model.eval()

nl_vecs=[]
for batch in query_dataloader:  
    nl_inputs = batch[1].to(args.device)
    with torch.no_grad():
        nl_vec = model(nl_inputs=nl_inputs) 
        nl_vecs.append(nl_vec.cpu().numpy()) 
code_vecs=[] 
for batch in code_dataloader:
    code_inputs = batch[0].to(args.device)    
    with torch.no_grad():
        code_vec= model(code_inputs=code_inputs)
        code_vecs.append(code_vec.cpu().numpy())  

In [24]:
nl_vec=torch.tensor(nl_vecs[0]).view(1,-1) 
code_vec=torch.tensor(code_vecs[0]).view(1,-1)

In [39]:
nl_vec.shape,code_vec.shape,torch.arange(2)

(torch.Size([1, 768]), torch.Size([1, 768]), tensor([0, 1]))

In [36]:
scores=torch.einsum("ab,cb->ac",nl_vec,code_vec)

In [8]:
import json
# file_path='/data/hdj/data/CodeBERT/Siamese-model/dataset/java/valid.jsonl'
# with open(file_path,'r') as f:
#     for line in f:
#         line=line.strip()
#         js=json.loads(line)
#         print(js)
#         break
# with open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/one_vs_two/test_2hard_2_data.txt','r') as f:
#     for i,line in enumerate(f):
#         contents=line.split('<CODESPLIT>')
#         print(contents[0],contents[1])
#         if i==35:
#             break

In [33]:
code_vecs=np.concatenate(code_vecs,0)
nl_vecs=np.concatenate(nl_vecs,0)
type(nl_vecs),len(nl_vecs),type(code_vecs),len(code_vecs)

(numpy.ndarray, 37, numpy.ndarray, 20000)

In [34]:
nl_urls=[]
code_urls=[]
for example in query_dataset.examples:
    nl_urls.append(example.url)
    
for example in code_dataset.examples:
    code_urls.append(example.url)
len(nl_urls),len(code_urls)

(37, 20000)

In [35]:
from collections import defaultdict
report2label=defaultdict(list)
idSet=set()
for example in code_dataset.examples:
#     print(example.label,example.url)
    if example.url not in idSet:
        idSet.add(example.url)
        report2label[example.url.split('_')[0]].append(int(example.label))
# report2label
code_urls
report2_codemethod=dict()
report2vec=dict()
for report_id ,nl_vec in zip(nl_urls,nl_vecs):
    report2_codemethod[report_id.split('_')[0]]=defaultdict(list)
    report2vec[report_id.split('_')[0]]=nl_vec
for code_url,code_vec in zip(code_urls,code_vecs):
    report_id=code_url.split('_')[0]
    code_file_id=code_url.split('_')[1]
    report2_codemethod[report_id][code_file_id].append(code_vec)

In [28]:
# len(report2label)
# for key,val in report2label.items():
#     print(key,len(val))

In [36]:
# report2_codemethod
report2code=defaultdict(list)
for key,nl_vec in report2vec.items():
    all_code_files=report2_codemethod[key]
    print(key)
    for code_key,code_vec in all_code_files.items():
#         if code_key=='49140ea044989336a65307203656da26382ef317':
            code_vec=np.array(code_vec)
#             print(type(code_vec),code_vec)
#             print(len(nl_vec))
            scores=np.matmul(nl_vec,code_vec.T)
#             print(key,code_key,)
#             print(len(scores),scores)
            report2code[key].append(max(scores))
#             report2code[key].append(np.mean(scores))
report2code
import pandas as pd
stage2_result=pd.DataFrame()
bid_list=[]
used_in_fix=[]
result=[]

for bid,scores in report2code.items():
#     print(bid,len(scores))
    if sum(report2label[bid])==0:
        continue
    bid_list.extend([bid for _ in range(len(scores))])
    used_in_fix.extend(report2label[bid])
    result.extend(scores)
stage2_result['bid']=bid_list
stage2_result['used_in_fix']=used_in_fix
stage2_result['result']=result
stage2_result.set_index('bid',inplace=True)

calculate_metrics(stage2_result)

6fcdd86
4f39524
a754695
29deb6d
1a14ea6
b9729f2
c9fe93d
05c6b3f
c68f62c
ccd2d5a
9fc8665
2460307
c7591f1
6adfd78
1563c7f
ed640c3
8c2a378
eafab0c
a335a83
32e1464
7b9ce76
2c265bf
259ec5f
b4dfa25
63ba006
2e726b8
8cb9404
6ac6360
696a120
870787f
d2a1d09
b16cc7a
c9eeb92
712033c
1481d03
fae0ba1
cad161b
accuracy_at_k : {1: 4, 2: 7, 3: 10, 4: 10, 5: 13, 6: 15, 7: 17, 8: 18, 9: 18, 10: 18, 11: 20, 12: 20, 13: 20, 14: 20, 15: 20, 16: 21, 17: 22, 18: 22, 19: 22, 20: 24}


({1: 0.11428571428571428,
  2: 0.2,
  3: 0.2857142857142857,
  4: 0.2857142857142857,
  5: 0.37142857142857144,
  6: 0.42857142857142855,
  7: 0.4857142857142857,
  8: 0.5142857142857142,
  9: 0.5142857142857142,
  10: 0.5142857142857142,
  11: 0.5714285714285714,
  12: 0.5714285714285714,
  13: 0.5714285714285714,
  14: 0.5714285714285714,
  15: 0.5714285714285714,
  16: 0.6,
  17: 0.6285714285714286,
  18: 0.6285714285714286,
  19: 0.6285714285714286,
  20: 0.6857142857142857},
 0.18095277668645268,
 0.2441531911735973)

In [26]:
# calculate_metrics(stage2_result)

In [297]:
# bug_report_files_dataframe[bug_report_files_dataframe.used_in_fix==1].index.tolist()
 10: 0.6252587991718427,
 0.2771006071568545,
 0.30574524963316996)
    
 10: 0.5900621118012422,
 0.2283605289273137,
 0.25359767176369724)

['d27f0b9', 'd27f0b9']

In [314]:
# stage2_result.set_index('bid',inplace=True)
# stage2_result.loc['afe9adb']
for bug_report, bug_report_files_dataframe in stage2_result.groupby(level=0, sort=False):
    print(bug_report)
    sort_before=bug_report_files_dataframe.reset_index(drop=True)
    sort_after=bug_report_files_dataframe.sort_values(by="result" , ascending=False).reset_index(drop=True)
    print(sort_before[sort_before.used_in_fix==1].index.tolist())
    print(sort_after[sort_after.used_in_fix==1].index.tolist())
#     break

afe9adb
[2]
[16]
d7f159e
[0]
[5]
ca3d39e
[4]
[6]
9c07aeb
[0]
[6]
9cf10b4
[2]
[14]
d93c3ef
[1, 10, 22]
[2, 15, 48]
5c26252
[10]
[6]
1f4ad6e
[1]
[0]
59888cd
[1]
[14]
bf0a2ac
[3]
[19]
90c1000
[34]
[24]
2dbe5ca
[1]
[13]
b2efb8d
[3]
[7]
ba72543
[0]
[13]
dff6fff
[1]
[8]
5003cff
[1]
[1]
ea99826
[0, 3]
[6, 19]
1619787
[14]
[12]
c776d3d
[1]
[33]
0d6b343
[3]
[1]
a0f2398
[0, 13]
[15, 39]
680ba71
[4]
[4]
19e3cd7
[2]
[22]
138cfd5
[0]
[0]
d927cc7
[1]
[16]
ff9b1f6
[5]
[0]
74f4bcf
[1]
[14]
a482b11
[24]
[0]
53a299e
[3]
[2]
f23e264
[2]
[28]
68ed333
[1]
[7]
c03582c
[18]
[14]
7a70e5b
[24]
[10]
539b766
[0]
[5]
5036d88
[4, 10]
[2, 5]
816e901
[1]
[24]
f679d8f
[2]
[16]
67ae97e
[0, 3]
[14, 15]
e8f7a82
[8, 10, 36]
[2, 4, 9]
af528f8
[1]
[17]
4589ae1
[1]
[26]
67cad5f
[2, 8]
[21, 31]
1e8ac07
[12]
[21]
0fa5ba5
[0, 11]
[15, 24]
f22e8e4
[0]
[1]
93c8c13
[12]
[7]
ae8f2cb
[3]
[17]
c4b481c
[4]
[7]
95e2d2c
[0, 8]
[7, 37]
9d82ea5
[0]
[14]
9f58ed4
[0]
[6]
367f1e7
[0]
[0]
0c333bf
[0]
[5]
b3d658c
[7]
[18]
438a8f3
[8]
[0]
a480

In [304]:
# stage2_result.loc['7ec4eb3']

In [219]:
sum(report2label['391cf4a'])

0

In [ ]:
accuracy_at_k : {1: 16, 2: 22, 3: 30, 4: 36, 5: 40, 6: 44, 7: 48, 8: 54, 9: 57, 10: 60, 11: 62, 12: 67, 13: 69, 14: 75, 15: 78, 16: 78, 17: 80, 18: 82, 19: 83, 20: 85}
({1: 0.15384615384615385,
  10: 0.5769230769230769,
 0.24667848019836008,
 0.2787028915561892)

len:256 5method
accuracy_at_k : {1: 11, 2: 22, 3: 30, 4: 33, 5: 38, 6: 38, 7: 43, 8: 44, 9: 46, 10: 48, 11: 50, 12: 52, 13: 54, 14: 60, 15: 64, 16: 66, 17: 67, 18: 68, 19: 69, 20: 72}
({1: 0.125,
  10: 0.5454545454545454,

 0.25095456180477976,
 0.2770230289860565)

0.22476759871989085,
0.253821817710929)

len:512 5method+source
0.26723728277989595,
 0.2956374002749387)
  
 0.25092035802098117,
 0.28432442917788026)

In [44]:
scores=np.matmul(nl_vecs[:2],code_vecs.T)

In [1]:
# print(len(scores))
# scores

In [46]:
sort_ids=np.argsort(scores, axis=-1, kind='quicksort', order=None)[:,::-1]   
sort_ids

array([[20, 48, 23, 42, 35, 31, 45,  5, 40, 21,  6, 12, 39, 41, 46, 15,
        25,  0,  8, 50, 13, 24,  1, 47, 26, 22, 27, 44, 11,  4, 38, 17,
         2,  7, 36, 19, 37, 16, 14,  3, 32, 10, 30, 29, 33, 28, 18, 43,
        34,  9, 49],
       [20, 48, 23, 42, 35, 31, 45,  5, 40, 21,  6, 12, 39, 41, 46, 15,
        25,  0,  8, 50, 13, 24,  1, 47, 26, 22, 27, 44, 11,  4, 38, 17,
         2,  7, 36, 19, 37, 16, 14,  3, 32, 10, 30, 29, 33, 28, 18, 43,
        34,  9, 49]])

In [35]:
code_vecs

array([[ 0.3248673 ,  0.14371203,  0.31368068, ...,  0.16909367,
         0.0569407 , -0.34460545],
       [-0.13349648, -0.42288607,  0.28738576, ..., -0.09408459,
         0.03718594,  0.25548068],
       [-0.12540057,  0.17259073,  0.5249595 , ..., -0.2345988 ,
         0.20784822, -0.21995267],
       ...,
       [-0.1927527 , -0.2151159 , -0.31969374, ...,  0.19472806,
        -0.2974168 , -0.4969376 ],
       [-0.01196504,  0.21166283, -0.3946086 , ...,  0.20576566,
         0.24125789, -0.22816606],
       [ 0.13414986,  0.09455936,  0.41274974, ..., -0.2236476 ,
         0.12790348,  0.2886108 ]], dtype=float32)

# 验证拆分后的指标开始 分为max mean来测 TODO

In [2]:
from collections import defaultdict
finalDict = defaultdict(list)
labelDict=dict()
pred_path='/data/hdj/tracking_buggy_files/joblib_memmap_eclipse/notebook_0607_test_2hard_2_data.txt'
final_pred_path_last='/data/hdj/tracking_buggy_files/joblib_memmap_eclipse/notebook_0607_test_2hard_2_data_logit.txt'
# final_pred_path_best='/data/hdj/tracking_buggy_files/joblib_memmap_swt/notebook_0602_test_2hard_2_data_logit_last.txt'
with open(pred_path,'r',encoding='utf-8') as f_in:
    for line in f_in:
        contents=line.split('<CODESPLIT>')
        id_=contents[1]
        label=contents[0]
        score=float(contents[-1])
        path=contents[2]
        finalDict[id_].append(score)
        labelDict[id_]=[label,id_,path]
with open(final_pred_path_last,'w',encoding='utf-8') as f_out:          
    for key,val in labelDict.items():
#         if 'aa3c6d8'==key.split('_')[0] or '5d702d1'==key.split('_')[0] :
#             continue
        
        list_all=val+[str(sum(finalDict[key])/len(finalDict[key]))]
#         list_all=val+[str(max(finalDict[key]))]
        f_out.write('<CODESPLIT>'.join(list_all)+'\n')
# with open(final_pred_path,'w',encoding='utf-8') as f_out:          
#     for key,val in labelDict.items():
# #         if 'aa3c6d8'==key.split('_')[0] or '5d702d1'==key.split('_')[0] :
# #             continue
        
# #         list_all=val+[str(sum(finalDict[key])/len(finalDict[key]))]
#         list_all=val+[str(max(finalDict[key]))]
#         f_out.write('<CODESPLIT>'.join(list_all)+'\n')

In [ ]:
with open(final_pred_path,'r',encoding='utf-8') as f_in:          
    for key,val in labelDict.items():
        if 'aa3c6d8'==key.split('_')[0] or '5d702d1'==key.split('_')[0] :
            continue
        
#         list_all=val+[str(sum(finalDict[key])/len(finalDict[key]))]
        list_all=val+[str(max(finalDict[key]))]
        f_out.write('<CODESPLIT>'.join(list_all)+'\n')

In [280]:
with open('/data/hdj/tracking_buggy_files/joblib_memmap_eclipse/one_vs_two/test_2hard_2_source_names_10method_less.txt','r',encoding='utf-8') as f_in:
    for i,line in enumerate(f_in):
        contents=line.split('<CODESPLIT>')
        if contents[0]=='1':
            print('*'*20)
        print(i+1,contents[0],contents[1])
#         if contents[1]=='6fcdd86_f934d48ecf17bc93fbccb36cc78e000142a25199' :#and contents[5]<contents[6]
#             print((i+1),'label :',contents[0],' id :',contents[1],' logit: ',contents[5],contents[6],' report :',contents[3],)#
#             print(' code :',contents[4])
#             print()
        if i==1000:
            break


1 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
2 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
3 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
4 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
5 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
6 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
7 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
8 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
9 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
10 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
11 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
12 0 391cf4a_0e4a82e3fdd2b02652ce2158b1554f61310ccfa2
13 0 391cf4a_56b91d2c55082a44d2ddcfdb492237943be44322
14 0 391cf4a_56b91d2c55082a44d2ddcfdb492237943be44322
15 0 391cf4a_56b91d2c55082a44d2ddcfdb492237943be44322
16 0 391cf4a_56b91d2c55082a44d2ddcfdb492237943be44322
17 0 391cf4a_56b91d2c55082a44d2ddcfdb492237943be44322
18 0 391cf4a_56b91d2c55082a44d2ddcfdb492237943be44322
19 0 391cf4a_56b91d2c55082a44d2ddcfdb

943 0 afe9adb_39cc3cf46cb209367af58122d69584c15fe84255
944 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
945 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
946 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
947 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
948 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
949 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
950 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
951 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
952 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
953 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
954 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
955 0 afe9adb_05ac8b0f895edd6933be47d20f5d4bbf9e7773eb
956 0 afe9adb_7778a3f0d876b3fe3614716afec818ea0c56859f
957 0 afe9adb_7778a3f0d876b3fe3614716afec818ea0c56859f
958 0 afe9adb_7778a3f0d876b3fe3614716afec818ea0c56859f
959 0 afe9adb_7778a3f0d876b3fe3614716afec818ea0c56859f
960 0 afe9adb_7778a3f0d876b3fe3614716afec818ea0c56859f
961 0 afe9

In [121]:

from transformers import (WEIGHTS_NAME, get_linear_schedule_with_warmup, AdamW,
                          RobertaConfig,
                          RobertaForSequenceClassification,
                          RobertaTokenizer)
tokenizer = RobertaTokenizer.from_pretrained('roberta-base', do_lower_case=True)

In [122]:
tokenizer.tokenize('TomcatBaseTest'),tokenizer.tokenize('HelloWorld'),tokenizer.tokenize('gdkdragcontext   '), 

(['tom', 'cat', 'bas', 'et', 'est'],
 ['hell', 'ow', 'orld'],
 ['gd', 'k', 'dr', 'ag', 'context'])

In [60]:
tokenizer.convert_tokens_to_ids(tokenizer.tokenize('setselect   ')),tokenizer.convert_tokens_to_ids(tokenizer.tokenize('xsetselectionown    '))

([8738, 38450], [1178, 8738, 44209, 3355])

In [42]:
from collections import defaultdict
calculate=defaultdict(list)

with open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/0530_test_3hard_2_data_onlymethod_merge_logit.txt','r',encoding='utf-8') as f_in:
    for i,line in enumerate(f_in):
        contents=line.split('<CODESPLIT>')
        calculate[contents[1].split('_')[0]].append(line)
k=0
for key,val in calculate.items():
    if len(val)!=50:
        print(key,len(val))
        k+=1
print(k)

0


In [3]:
idSet=set()
with open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/test_3hard_2.csv','r',encoding='utf-8') as f_in:
    for i,line in enumerate(f_in):
        if i==0:
            continue
#         print(line.split(','))
        line=line.split(',')
        idx=line[0]+'_'+line[1]
        if idx in idSet:
            print(idx)
        else:
            idSet.add(idx)
#         break

aa3c6d8_08a78aa406f4ff1949e9696f6cfb93cb0309a0cd
aa3c6d8_7a66bebb229721ecaf55191d92a911e74561afaf
aa3c6d8_7a66bebb229721ecaf55191d92a911e74561afaf
aa3c6d8_7a66bebb229721ecaf55191d92a911e74561afaf
aa3c6d8_7a66bebb229721ecaf55191d92a911e74561afaf
aa3c6d8_b7dbda53be0a28e0dfb6d833c146fa5732d97eba
aa3c6d8_b7dbda53be0a28e0dfb6d833c146fa5732d97eba
aa3c6d8_b7dbda53be0a28e0dfb6d833c146fa5732d97eba
aa3c6d8_b7dbda53be0a28e0dfb6d833c146fa5732d97eba
5d702d1_4829e2d8889d98119f1a844c33cface7d3410875
5d702d1_4829e2d8889d98119f1a844c33cface7d3410875


In [1]:
#测试增加手动特征
def load_features(file_prefix, commit):
    file_path = file_prefix + '_' + commit[0:7] + '_features.npz'
    features_data = sparse.load_npz(file_path).tocsr()
    return features_data


def load_filenames(file_prefix, commit):
    file_path = file_prefix + '_' + commit[0:7] + '_files'
    with open(file_path, 'r') as f:
        files_list = json.load(f)
        return files_list

In [3]:
import json

file_prefix='/data/hdj/tracking_buggy_files/swt/swt'
commit='0a0326b'
files_list=load_filenames(file_prefix,commit)

In [6]:
from scipy import sparse
features_data=load_features(file_prefix,commit)
len(files_list)

1771

In [8]:
# files_list

In [9]:
fea=features_data[files_list.index('a817010b7e32082e05839657c8ab7431edd0e6f2')].toarray()[0][:-1]

In [19]:
import torch
import numpy as np
nl_vecs=torch.tensor([[0.1,0.2,0.4],[0.4,0.5,0.3]])
code_vecs=torch.tensor([[0.5,0.1,0.4],[0.1,0.8,0.3],[0.4,0.4,0.4],[0.5,0.5,0.3]])
scores=np.matmul(nl_vecs,code_vecs.T)
scores

tensor([[0.2300, 0.2900, 0.2800, 0.2700],
        [0.3700, 0.5300, 0.4800, 0.5400]])

In [24]:
len(scores)

2

In [23]:
ranks=[]
for i in range(len(scores)):
    score=scores[i,i]
    rank=1
    for j in range(len(scores)):
        print(i,j)
        if i!=j and scores[i,j]>=score:
            rank+=1
    ranks.append(1/rank)    
result = {
        "eval_loss": float(1),
        "eval_mrr":float(np.mean(ranks))
    }
result

{'eval_loss': 1.0, 'eval_mrr': 0.75}

In [15]:
import torch
torch.tensor(fea,dtype=torch.float16)

tensor([2.0370e-02, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
        4.7180e-02, 0.0000e+00, 0.0000e+00, 1.1682e-01, 2.9251e-02, 0.0000e+00,
        5.5115e-02, 6.0272e-02, 1.0000e+00, 0.0000e+00, 2.2459e-04, 5.9605e-08,
        0.0000e+00], dtype=torch.float16)

In [21]:
features_data[files_list.index('a817010b7e32082e05839657c8ab7431edd0e6f2')].toarray()[0][:-1]

array([2.03696829e-02, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 4.71759029e-02, 0.00000000e+00,
       0.00000000e+00, 1.16802790e-01, 2.92505585e-02, 0.00000000e+00,
       5.51111600e-02, 6.02588680e-02, 1.00000000e+00, 0.00000000e+00,
       2.24571975e-04, 7.11924717e-08, 0.00000000e+00])

# 验证拆分后指标结束

In [17]:
29052*0.2,29052*0.8,29052-5810,29053-23246,90315/361294

(5810.400000000001, 23241.600000000002, 23242, 5807, 0.24997647345375235)

In [18]:
9604/251820

0.03813835279167659

In [36]:
statis(summary_len)
statis(source_len)

code 的 10% 8.0
20 : 17.0
30 : 20.0
40 : 24.0
50 : 27.0
60 : 33.0
70 : 41.0
80 : 53.0
90 : 79.0
code 的 10% 62.0
20 : 78.0
30 : 89.0
40 : 102.0
50 : 123.0
60 : 149.0
70 : 197.29999999999973
80 : 314.0
90 : 651.0


In [34]:
# summary_len

# 按照CodeSearch组织数据结束

# 生成fine-tune阶段的数据 为每一个fold都生成训练数据

In [50]:
def generate_fine_tune(train_k_path,out_path):
    #生成fine-tune需要的数据集
    #train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv' 
    #out_path='/home/hdj/BERT-PLI-IJCAI2020/examples/task2/data_sample_1.json'
    train_k=pd.read_csv(train_k_path)
    train_k.set_index(['bid','fid'], inplace = True)
    train_k.head(10)
    #取bid所对应的report
    bid_list=list(train_k.index.get_level_values(0).unique())
    len(bid_list)
    summarys=[]
    descriptions=[]
    for bug_report_id in bid_list:
        current_bug_report = bug_reports[bug_report_id]['bug_report']
        summarys.append(current_bug_report['summary'])
        descriptions.append(current_bug_report['description'])
    report_dataFrame=pd.DataFrame({'summary':summarys,'description':descriptions},index=bid_list)
    report_dataFrame.index.names=['bid']
    def remove_twoHeadWord(string):
        contents=string.split(' ')[2:]
        return ' '.join(contents)
    report_dataFrame['summary']=report_dataFrame['summary'].apply(remove_twoHeadWord)
    report_dataFrame.head()
    all_ast_index=list(train_k.index.get_level_values(1).unique())
    type(all_ast_index)
    all_ast_file_methodContent=[]
    for ast_index in all_ast_index:
    #     print(ast_index)
        ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
        all_ast_file_methodContent.append(ast_file['methodContent'])
    # all_ast_index
    all_ast_index_dataframe=pd.DataFrame({'methodContent':all_ast_file_methodContent},index=all_ast_index)
    # print(all_ast_index_dataframe.head())
    print(all_ast_index_dataframe.shape)
    # all_ast_index_dataframe.set_index(["ast_index"], inplace=True)
    # all_ast_index_dataframe
    all_ast_index_dataframe.index.names=['fid']
    all_ast_index_dataframe.head(2)
    #开始连接字段
    all_methodContent_index_dataframe=all_ast_index_dataframe.join(train_k,how='inner')
    all_methodContent_index_dataframe.head()
    all_report_methodContent_index_dataframe=report_dataFrame.join(all_methodContent_index_dataframe,how='inner')
    all_report_methodContent_index_dataframe.head()
    
    task1_list=[]
    all_report_methodContent_index_dataframe.fillna("",inplace=True)
    def clean_string(string):
        outstring_list=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
        return ' '.join(outstring_list)
    sum_label=0
    for i,(index, row) in enumerate(all_report_methodContent_index_dataframe.iterrows()):
    #     print(index[0],index[1],row['summary'],row['description'],row['methodContent'],row['used_in_fix'])
        if len(row['methodContent'])==0:
            continue
        guid='_'.join([index[0],index[1]])
#         print(i,'summary :',type(row['summary']),'description :',type(row['description']))
#         q_paras=[clean_string(row['summary']),clean_string(row['description'])]
#         c_paras=[clean_string(string) for string in row['methodContent']]
        q_paras=[mergeTokenziedSource(tokenize(row['summary'],stemmer)),mergeTokenziedSource(tokenize(row['description'],stemmer))]
        c_paras=[mergeTokenziedSource(tokenize(string,stemmer)) for string in row['methodContent']]
        
        label=int(row['used_in_fix'])

        for q in q_paras:
            if q=="":
                continue
            for c in c_paras:
                if c=="":
                    continue
                task1=dict()

                task1['guid']=guid
                task1['text_a']=q
                task1['text_b']=c
                task1['label']=label
                sum_label+=label
                task1_list.append(task1)
    #     print(task1)
    #     if i==2:
    #         break
    print(len(task1_list),sum_label,sum_label/len(task1_list))
    task1_list[0]
    label=0
    label_0=0
    for task in task1_list:
    #     print(task)
        label+=task['label']
        if task['label']==0:
            label_0+=1
    #     break
    print(label)
    with open(out_path,'w',encoding='utf-8') as f_out:
        for task1 in task1_list:
            out_line = json.dumps(task1, ensure_ascii=False) + '\n'
            f_out.write(out_line)
train_k_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv'
out_path='/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1_fine_tune.txt'
generate_fine_tune(train_k_path,out_path)

(3353, 1)
0 summary : <class 'str'> description : <class 'str'>
1 summary : <class 'str'> description : <class 'str'>
2 summary : <class 'str'> description : <class 'str'>
3 summary : <class 'str'> description : <class 'str'>
4 summary : <class 'str'> description : <class 'str'>
5 summary : <class 'str'> description : <class 'str'>
6 summary : <class 'str'> description : <class 'str'>
7 summary : <class 'str'> description : <class 'str'>
8 summary : <class 'str'> description : <class 'str'>
9 summary : <class 'str'> description : <class 'str'>
10 summary : <class 'str'> description : <class 'str'>
11 summary : <class 'str'> description : <class 'str'>
12 summary : <class 'str'> description : <class 'str'>
16 summary : <class 'str'> description : <class 'str'>
18 summary : <class 'str'> description : <class 'str'>
19 summary : <class 'str'> description : <class 'str'>
24 summary : <class 'str'> description : <class 'str'>
27 summary : <class 'str'> description : <class 'str'>
32 summary

325 summary : <class 'str'> description : <class 'str'>
334 summary : <class 'str'> description : <class 'str'>
335 summary : <class 'str'> description : <class 'str'>
339 summary : <class 'str'> description : <class 'str'>
345 summary : <class 'str'> description : <class 'str'>
362 summary : <class 'str'> description : <class 'str'>
363 summary : <class 'str'> description : <class 'str'>
367 summary : <class 'str'> description : <class 'str'>
371 summary : <class 'str'> description : <class 'str'>
373 summary : <class 'str'> description : <class 'str'>
376 summary : <class 'str'> description : <class 'str'>
377 summary : <class 'str'> description : <class 'str'>
378 summary : <class 'str'> description : <class 'str'>
379 summary : <class 'str'> description : <class 'str'>
380 summary : <class 'str'> description : <class 'str'>
381 summary : <class 'str'> description : <class 'str'>
382 summary : <class 'str'> description : <class 'str'>
383 summary : <class 'str'> description : <class

591 summary : <class 'str'> description : <class 'str'>
597 summary : <class 'str'> description : <class 'str'>
604 summary : <class 'str'> description : <class 'str'>
640 summary : <class 'str'> description : <class 'str'>
641 summary : <class 'str'> description : <class 'str'>
644 summary : <class 'str'> description : <class 'str'>
645 summary : <class 'str'> description : <class 'str'>
646 summary : <class 'str'> description : <class 'str'>
648 summary : <class 'str'> description : <class 'str'>
649 summary : <class 'str'> description : <class 'str'>
653 summary : <class 'str'> description : <class 'str'>
656 summary : <class 'str'> description : <class 'str'>
657 summary : <class 'str'> description : <class 'str'>
658 summary : <class 'str'> description : <class 'str'>
660 summary : <class 'str'> description : <class 'str'>
661 summary : <class 'str'> description : <class 'str'>
669 summary : <class 'str'> description : <class 'str'>
674 summary : <class 'str'> description : <class

851 summary : <class 'str'> description : <class 'str'>
852 summary : <class 'str'> description : <class 'str'>
853 summary : <class 'str'> description : <class 'str'>
854 summary : <class 'str'> description : <class 'str'>
855 summary : <class 'str'> description : <class 'str'>
856 summary : <class 'str'> description : <class 'str'>
857 summary : <class 'str'> description : <class 'str'>
858 summary : <class 'str'> description : <class 'str'>
859 summary : <class 'str'> description : <class 'str'>
860 summary : <class 'str'> description : <class 'str'>
861 summary : <class 'str'> description : <class 'str'>
862 summary : <class 'str'> description : <class 'str'>
863 summary : <class 'str'> description : <class 'str'>
864 summary : <class 'str'> description : <class 'str'>
865 summary : <class 'str'> description : <class 'str'>
866 summary : <class 'str'> description : <class 'str'>
867 summary : <class 'str'> description : <class 'str'>
868 summary : <class 'str'> description : <class

1102 summary : <class 'str'> description : <class 'str'>
1103 summary : <class 'str'> description : <class 'str'>
1104 summary : <class 'str'> description : <class 'str'>
1105 summary : <class 'str'> description : <class 'str'>
1106 summary : <class 'str'> description : <class 'str'>
1107 summary : <class 'str'> description : <class 'str'>
1108 summary : <class 'str'> description : <class 'str'>
1109 summary : <class 'str'> description : <class 'str'>
1110 summary : <class 'str'> description : <class 'str'>
1111 summary : <class 'str'> description : <class 'str'>
1112 summary : <class 'str'> description : <class 'str'>
1113 summary : <class 'str'> description : <class 'str'>
1115 summary : <class 'str'> description : <class 'str'>
1116 summary : <class 'str'> description : <class 'str'>
1117 summary : <class 'str'> description : <class 'str'>
1118 summary : <class 'str'> description : <class 'str'>
1121 summary : <class 'str'> description : <class 'str'>
1122 summary : <class 'str'> de

...

24516 summary : <class 'str'> description : <class 'str'>
24518 summary : <class 'str'> description : <class 'str'>
24522 summary : <class 'str'> description : <class 'str'>
24551 summary : <class 'str'> description : <class 'str'>
24559 summary : <class 'str'> description : <class 'str'>
24564 summary : <class 'str'> description : <class 'str'>
24565 summary : <class 'str'> description : <class 'str'>
24567 summary : <class 'str'> description : <class 'str'>
24570 summary : <class 'str'> description : <class 'str'>
24573 summary : <class 'str'> description : <class 'str'>
24576 summary : <class 'str'> description : <class 'str'>
24579 summary : <class 'str'> description : <class 'str'>
24582 summary : <class 'str'> description : <class 'str'>
24586 summary : <class 'str'> description : <class 'str'>
24593 summary : <class 'str'> description : <class 'str'>
24610 summary : <class 'str'> description : <class 'str'>
24611 summary : <class 'str'> description : <class 'str'>
24615 summary 

24819 summary : <class 'str'> description : <class 'str'>
24820 summary : <class 'str'> description : <class 'str'>
24821 summary : <class 'str'> description : <class 'str'>
24822 summary : <class 'str'> description : <class 'str'>
24823 summary : <class 'str'> description : <class 'str'>
24824 summary : <class 'str'> description : <class 'str'>
24825 summary : <class 'str'> description : <class 'str'>
24826 summary : <class 'str'> description : <class 'str'>
24828 summary : <class 'str'> description : <class 'str'>
24829 summary : <class 'str'> description : <class 'str'>
24830 summary : <class 'str'> description : <class 'str'>
24831 summary : <class 'str'> description : <class 'str'>
24832 summary : <class 'str'> description : <class 'str'>
24833 summary : <class 'str'> description : <class 'str'>
24834 summary : <class 'str'> description : <class 'str'>
24835 summary : <class 'str'> description : <class 'str'>
24836 summary : <class 'str'> description : <class 'str'>
24837 summary 

25108 summary : <class 'str'> description : <class 'str'>
25109 summary : <class 'str'> description : <class 'str'>
25111 summary : <class 'str'> description : <class 'str'>
25112 summary : <class 'str'> description : <class 'str'>
25113 summary : <class 'str'> description : <class 'str'>
25114 summary : <class 'str'> description : <class 'str'>
25115 summary : <class 'str'> description : <class 'str'>
25116 summary : <class 'str'> description : <class 'str'>
25117 summary : <class 'str'> description : <class 'str'>
25118 summary : <class 'str'> description : <class 'str'>
25119 summary : <class 'str'> description : <class 'str'>
25123 summary : <class 'str'> description : <class 'str'>
25125 summary : <class 'str'> description : <class 'str'>
25127 summary : <class 'str'> description : <class 'str'>
25128 summary : <class 'str'> description : <class 'str'>
25129 summary : <class 'str'> description : <class 'str'>
25130 summary : <class 'str'> description : <class 'str'>
25131 summary 

25338 summary : <class 'str'> description : <class 'str'>
25339 summary : <class 'str'> description : <class 'str'>
25340 summary : <class 'str'> description : <class 'str'>
25341 summary : <class 'str'> description : <class 'str'>
25344 summary : <class 'str'> description : <class 'str'>
25346 summary : <class 'str'> description : <class 'str'>
25347 summary : <class 'str'> description : <class 'str'>
25348 summary : <class 'str'> description : <class 'str'>
25349 summary : <class 'str'> description : <class 'str'>
25350 summary : <class 'str'> description : <class 'str'>
25351 summary : <class 'str'> description : <class 'str'>
25352 summary : <class 'str'> description : <class 'str'>
25353 summary : <class 'str'> description : <class 'str'>
25354 summary : <class 'str'> description : <class 'str'>
25355 summary : <class 'str'> description : <class 'str'>
25358 summary : <class 'str'> description : <class 'str'>
25359 summary : <class 'str'> description : <class 'str'>
25360 summary 

25589 summary : <class 'str'> description : <class 'str'>
25591 summary : <class 'str'> description : <class 'str'>
25592 summary : <class 'str'> description : <class 'str'>
25593 summary : <class 'str'> description : <class 'str'>
25594 summary : <class 'str'> description : <class 'str'>
25596 summary : <class 'str'> description : <class 'str'>
25599 summary : <class 'str'> description : <class 'str'>
25600 summary : <class 'str'> description : <class 'str'>
25616 summary : <class 'str'> description : <class 'str'>
25619 summary : <class 'str'> description : <class 'str'>
25621 summary : <class 'str'> description : <class 'str'>
25622 summary : <class 'str'> description : <class 'str'>
25623 summary : <class 'str'> description : <class 'str'>
25624 summary : <class 'str'> description : <class 'str'>
25625 summary : <class 'str'> description : <class 'str'>
25628 summary : <class 'str'> description : <class 'str'>
25629 summary : <class 'str'> description : <class 'str'>
25630 summary 

In [69]:
train_k=pd.read_csv('/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1.csv')
train_k.set_index(['bid','fid'], inplace = True)
train_k.head(10)
#取bid所对应的report
bid_list=list(train_k.index.get_level_values(0).unique())

In [162]:
len(bid_list)
summarys=[]
descriptions=[]
for bug_report_id in bid_list:
    current_bug_report = bug_reports[bug_report_id]['bug_report']
    summarys.append(current_bug_report['summary'])
    descriptions.append(current_bug_report['description'])
report_dataFrame=pd.DataFrame({'summary':summarys,'description':descriptions},index=bid_list)
report_dataFrame.index.names=['bid']
def remove_twoHeadWord(string):
    contents=string.split(' ')[2:]
    return ' '.join(contents)
report_dataFrame['summary']=report_dataFrame['summary'].apply(remove_twoHeadWord)
report_dataFrame.head()

summary  \
bid                                                          
a0c9251   [DirectoryDialog] There is no disk in the dri...   
1c62052              Outline view crashes on WinXP & Win2K   
6fac09a   crash in gtk_editable_delete_selection on GTK...   
b4a3cd3                 Need a locale String from FontData   
8380cc1      [StyledText] ContentWidthCache initialization   

                                               description  
bid                                                         
a0c9251  Any operation which brings up a file dialog bo...  
1c62052  I can reproduce this crash consistently.\n\n1....  
6fac09a  After compiling, running eclipse and looking a...  
b4a3cd3  2.1\n\nWe need a way to get the Locale informa...  
8380cc1                                               None

In [73]:
ast_file = pickle.loads(swt_ast_cache_collection_db['ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01'])
ast_file

{'tokenizedVariableNames': [{'cancel': 1, 'button': 1, 'cancelbutton': 1},
  {'movabl': 1},
  {'default': 1, 'button': 1, 'defaultbutton': 1},
  {'cancel': 1, 'text': 1, 'canceltext': 1},
  {'sizeof': 1},
  {'button': 1, 'helpbutton': 1, 'help': 1},
  {'flag': 1},
  {'text': 1, 'othertext': 1},
  {'default': 1, 'text': 1, 'defaulttext': 1},
  {'posit': 1},
  {'version': 1}],
 'superclassNames': [],
 'interfaceNames': [],
 'tokenizedMethodNames': [],
 'methodVariableTypes': [],
 'tokenizedSuperclassNames': [],
 'classNames': ['org.eclipse.swt.internal.carbon.AlertStdCFStringAlertParamRec'],
 'tokenizedSource': {'www': 1,
  'right': 1,
  'version': 1,
  'int': 6,
  'text': 3,
  'defaultbutton': 1,
  'packag': 1,
  'intern': 1,
  'api': 1,
  'static': 1,
  'param': 1,
  'carbon': 1,
  'contributor': 1,
  'reserv': 1,
  'othertext': 1,
  'sizeof': 1,
  'string': 1,
  'movabl': 1,
  'copyright': 1,
  'licens': 1,
  'help': 1,
  'legal': 1,
  'short': 3,
  'avail': 2,
  'program': 1,
  'butt

In [77]:
all_ast_index=list(train_k.index.get_level_values(1).unique())
type(all_ast_index)
all_ast_file_methodContent=[]
count=0
sourceLen=[]
for ast_index in all_ast_index:
#     print(ast_index)
    ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
    print(ast_index,len(ast_file['tokenizedMethods']),len(ast_file['tokenizedSource']))#TODO
    if len(ast_file['tokenizedMethods'])==0:
        count+=1
    sourceLen.append(len(ast_file['tokenizedSource']))
    all_ast_file_methodContent.append(ast_file['methodContent'])
print(count)

e7a5e5ff9e842566fce2b344076eda8486db4c1a 8 254
146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5 617 2346
5b25a2888e0399ba89b04fd4a9dfb7727f98490e 2 51
ccef4c7df48e1647fb37cf453729e7970c051093 1 64
ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01 0 62
b8181b8e3efce7fde4773e62fc386b0ddb4bb2ea 0 56
efc4b6a37ca49fb1d5f28bccd7301ef06ff85046 0 56
2824b2b3defd96a7b139e5b54cbc8bce4476f043 15 178
e7dd32ae2b70ff5babc76f6de822712139134480 224 1084
43728ad151d9f048e1794736411d2ef330ce2b31 56 710
5817de29bb11272a4ece39543f898bac74167fc1 0 77
df4c0bdec1aa37667c856d1606fb59f5062a9d3b 0 61
e4d952b1518d69422c5da12290644f2d76f7a38d 0 94
36cd3d282070cac6be0ef7c285727f22d8b4c8d2 6 77
973218993061f13095ed58636f133e058d75744c 2 51
f10b4f2d0f2c9a1986aed279d6c24579c570d2f4 72 473
b83ba756853846001f537f70c7a66d930336d7ee 64 488
38d3534e6be61e52f2ebc3faae1759c71108fbf6 12 222
6689c443b14675a828f4b2e56da022c6c7d9ffa3 0 89
62fe34236763c64b546aff2497ad398d071f0fe2 0 102
9abb3fd9159072926ead48e3ef3499ca4f685a70 16 308
c30e3bc94ffb

8ad2ba1b2ed285d31c247d5f93fb2dc81e5108bd 89 853
cf7aed245480aefd08aced90ce9b68235123c3f8 0 48
c96e4048e7ea8065771b09960a43ca06a838550b 0 48
67c2b54c05efcf3a273bbd4754f1c0a97bf2ab89 68 410
5e8245566ccff01034835e223155ad4b3c886435 2 58
d94046dcd02095b666fb5e01356e1c72764277d0 0 51
0f9b47705315f808ca70a39733013340ce9571bc 34 502
1cc5c982db7de05ca023eb73e1b0ff9f9cce6c4b 69 807
1ea560ff4e653400d479721034a8693ec8de43fe 0 47
7b92b82be832c866ae97ac00f19b888584517632 0 44
9224a9323adde47f438477e33506328148c893ad 0 51
1e83a81244bba2cacb8578b479f5b8e5c28956df 0 42
8d09dbc2a38b9c7cc1e95a11566f4440a02a7cdb 69 807
1b3405a452974f961967e1b5c74d24ec9b58ba8a 315 1477
6710188af31fce99316d5c1fc7c4ad92f69344c4 0 55
7d0cd25e9276000295d26e047b3fa5d1aee6aa7a 616 653
847a3f47e6bcec72e5b616c7ea0a855e3ce2371d 92 734
09d50b0966e398d9662fe4df07eea709a47eb0dc 7 67
1977e438d890e6a2a7d1e404fb29b42a9b7d53f4 158 907
fe7be6c6775d5a0382b65d17dd62416d0fe0459d 68 637
b562a8ee3ca507031bdd8c7ab2f7bd9eeaf17849 44 438
8d5aaaf1

bcb42f31c5176eada9015be8d2d77b2e6aa5cdf7 0 48
160306e79df66722d167756c271d4ab12456346e 0 49
9b469db859b273967aaae0130d3bbdafcb6521a2 0 43
755ee943c39dbd22c6d6aa05155ceb4590c5ea09 0 49
bf6858e08a4c7bdcd7647fc2c684a69bc5ef8cde 0 47
22a9c5ea7e16d36ede1156babb41f24eebff40b2 91 651
cf51479e6f16a6d8d97d0bc2a6b45c3f9d3389b8 42 485
b33d7c812ab2ff0bcfc4d7f994bce5429a9b3f3f 16 303
dc980d53103ba88de01e39ec1b23f09f7e310139 14 94
c9992fb427edae0d76aded6ce5096937fdf9f4a4 153 1470
6edf01e0517116a1ccb0854df9f584622ec11b9f 19 321
b3fc9fbc754d78ae219ebfb65f666148f484c6e5 7 115
7dcca8ffaf217ab525e3d6866688b452a7a4c720 0 79
56192d7701c355e905b3c46392955142b073e64a 10 145
7e49f85287d114eecdda63cd35024b50b10e4fa2 7 116
961bdd8e92a44138a074f39b2d817ad973b5ffdd 11 132
acd881944b026aa2182cc4e46b246a7a178ee4a6 0 55
3e0f4aa628e089642394b296dfd8edc05e920ee1 78 525
85a932e664c370400625e563f583cc3e0ad8d55b 0 49
bca5ef9348f91811eca1e916019548c6993ebf4f 10 141
12b526755d7fb4564f9df0978e19ac62dc75660b 39 383
38aeda8c1

2f68acc1bf78d7e0b413b80cf69be2f0fe4735bc 0 64
5d3b7916e2358f0d69e4ca9ac71890a48e906dac 0 87
7a095c43dbaf1b165d636743747b4d5918e47d49 0 87
92c6dc60e3053ca934ba9471a56c8b846a256100 37 186
6c05b7fbea81234f23dd00185abea6ec0f1c0fd6 130 618
15b4d79e969763ec5f8c6a952f75c3c0a8c2583c 10 194
3523c61b3f8255cec00b6a1c947679accba83010 16 279
ed93f2b414f6213c36cdb9e41e9f8b3bdf697ef8 8 132
6973c567458704b14c86e1a526f10a13381e2184 20 337
c3fa2bd47c8ce6cbd3b87735151db71e719c22e0 58 729
df0261df5c11724c9f1bdde9bfb54f763ac64f59 18 262
a7123c01451fe04f6eb79dffa375351544ba5520 11 191
dd48276e5fcda495aa86052763d28c28bbb8693e 3 102
b19aaa2f068d54453cbd7d1e0f7b32919baa44a8 15 191
982aaddd87c17081513b674935f7e739ca39a250 0 39
3a6d92def3afbac7864b5fe5e66f1bf5eeb6a67f 0 64
69b6f7c644347c9e11c0c78943444b2ba4f1bbf8 0 41
763496c960a86091189c0cc6f9adde5766b26452 0 43
a4bc085268ef216408e2d25d88acf2900d202770 0 54
59bb94b4a90f739458187850f5cec6610c7b9758 0 45
c169e27c5545f1a1688dd165cbea5aa2a24c74c0 0 68
6010e3c535948

bdc2b9ce5a2bbe5e34e3eb742cf9b174b8b091c5 705 739
7632ecda9cae72972720ece4f0dbf0ca2e2671a4 0 58
be843fa5c7a1de3eed11c9d30f0f649844fd6dff 56 446
842b46cf8ab3a97e1060ce4816ad9af16f9da4d3 6 674
16b2963d9373bf36e0c830cc6c8c0168a82f5bb2 17 125
ce3705a06f26d70bd78973ce2fa1a7f9b321e19f 21 225
2bef20b283310b85aca25ab99831ae23e0959970 165 252
ebde7ae63aa647dc84eb1c29f1fa2133b4d1e705 11 166
9996302d572a056e5ecd362f14c48517bb9ff5af 7 146
8cab0f6d63bdd20456aed6972167f55872fb0bd6 2 112
66119642f8605f20047149132b83a2dcecaa9fd3 170 753
9539ec23333da13290fb103362386ad63882a299 33 348
c99fa47a1037d804f7f459b99d20aa988a9b4f92 1 42
bcbfbca53ba683f579dd10b83ac345bc73e9960b 0 45
1f0bfd7cda61b2c0f404be9d0af0b3f695746af2 0 47
9a17a81a484dc89ff8c926958361fed145254971 150 898
7639b236147d0f88844623bbaf54d98a29ef60bf 59 549
9431c192aeb4dea8c290db50d0cf02df3eaed03d 27 285
655064dc5b40b78672b08be36cb3e781a4659dd6 119 1005
faee2d7d2dc8f17abb0ab89be20f8f7ceced3416 8 149
5e8eab982907b44c8f20fca05b3764fa22d3c5ef 16 17

a336376b57e758df5a2f51c5c38b66ce0e9c1b6c 0 50
dcf8fd4407b16b56726f519f9163b428440ba67e 5 140
5d5ec4dc6ffe396254294a790a2e8359f14d41a9 0 75
04f6c541a8e18cb8903467d162d01bbbbf30a40b 0 53
405e32a2468bada665a0f5eaebcd7e025dcd3b70 835 796
c587ad544b82c55d69e3b9c8d2405a9dcc6fb456 68 554
94d4f88fc372fb56d0ee3b283069c3afb748e8c2 98 976
636e3af733ee28f250a1b99b4f718feddc799a3c 70 817
abba7378c7502840c23cd70ce844d7e2cf36031f 71 827
5529f6a42749fb2241151790a4784741a2272127 33 382
81c3de10e9297748c5857423cd6f8399ae3b38a7 42 278
7c9cf1a0c4fe31e8412da80d4b25633a021de075 0 54
1579b6802946ed2ea0510deeccda3b429ebfe404 147 762
15563d2458f548ab575a3d971471d89edf990ad2 0 57
5f60f2921727e1c009c0a77f8fc44ea756c66a25 0 50
2a8cdfd6710f7d95acba529da6bd508dca8e9f71 18 177
2e421c22bac029787a63ab66c9b5d351f7fe7b87 45 307
8a325acc4db959540607e30988e5859274510188 5 88
41f0dd0b3a4f93c34cf1d4e30a8cb468e3790ca8 818 779
b1dc1b5dd294da57bf022fe9ac3a8eaa5102a1e0 48 399
392d55b12d45b2e8969ba94063184d9671e47b3b 110 485
e4b

1c16e608aabe8e2c19710da0a04d0553a6559a7d 136 805
7c6f8f9344bbde6c983ca864f055fcbde0165e96 72 449
147d06a92f83231e7cf6542488a7ce739bb22882 0 46
bfdec9f965f451ca3c24b2ab5270e683b3053213 54 490
e269c6fb2b4bcc132f0c8f899c11fa2f9d446527 92 598
d2138e5cf8578b2f0ce3b9f117ff6c6bd5b313ab 11 150
8be498878f75ad240ac2d1b9dc61874127411c92 21 351
a1470d69fa94c356b6012e3fccbe603409d23dc7 136 805
694beb9405584d275d5e0b03b23fd6e1e764f4cd 33 347
19420b95f0f0cd453b51c0b827ca40e1af2ed164 870 817
1f64383f2f7f8203eb9835ac890af7dcab95db5f 49 405
55963e1e560589608467c4d61263c2c9ffe2a861 23 307
f8288cb18e971d865ac3e4fcb96d19140d2d01a9 0 43
a2a3fcc68dbb70e8e59898b2dbc143c0c901d345 0 50
756003b6790ae95c3fd614b889d9dd7330956110 49 554
9f6e5cd6f1c879ab67548e4aed0f549628529882 9 234
31013b2c5647fca20a743ad9246fefa9e9d46fd5 9 105
d29eec2193659a564e46e4f64ad15eb727286d7a 9 105
9017ec0612348273c03e0bf2dff08a3a869ebc44 311 1477
aef667af5a2e0fa03f4c0cd47607eddd43c4befa 26 387
129cf884ecaabb032d661b641f324bd157a3a229 28 

In [78]:
576/len(all_ast_index)


code 的 10% 49.0
20 : 58.0
30 : 68.0
40 : 94.0
50 : 132.0
60 : 240.39999999999986
70 : 389.0
80 : 571.6000000000001
90 : 801.1000000000001


In [164]:
# all_ast_index
all_ast_index_dataframe=pd.DataFrame({'methodContent':all_ast_file_methodContent},index=all_ast_index)
# print(all_ast_index_dataframe.head())
print(all_ast_index_dataframe.shape)
# all_ast_index_dataframe.set_index(["ast_index"], inplace=True)
# all_ast_index_dataframe
all_ast_index_dataframe.index.names=['fid']
all_ast_index_dataframe.head(2)

(1980, 1)


methodContent
fid                                                                                        
e7a5e5ff9e842566fce2b344076eda8486db4c1a  [/**\n * Constructs a new instance of this cla...
146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5  [/** Ansi/Unicode wrappers */\n\npublic static...

In [118]:
all_ast_index_dataframe['methodContent']

fid
e7a5e5ff9e842566fce2b344076eda8486db4c1a    False
146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5    False
ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01    False
b8181b8e3efce7fde4773e62fc386b0ddb4bb2ea    False
efc4b6a37ca49fb1d5f28bccd7301ef06ff85046    False
                                            ...  
533e32ee59ee2e5151e14c81a31fec7ac95f6823    False
e28aa8301795b493bc4370bf9b35266ed278b52d    False
59de314ac6f7c8c5a824cfc7e2f5683d7fc3f935    False
f3372f3ecdc3f8e7438d2e3c07bf98bbb1f99967    False
e5c829bec93cedf7d85b1f0980434c6092cad941    False
Name: methodContent, Length: 1745, dtype: bool

In [165]:
#开始连接字段
all_methodContent_index_dataframe=all_ast_index_dataframe.join(train_k,how='inner')
all_methodContent_index_dataframe.head()

methodContent  \
bid     fid                                                                                           
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a  [/**\n * Constructs a new instance of this cla...   
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5  [/** Ansi/Unicode wrappers */\n\npublic static...   
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e  [public IOleWindow(int address) {\n\tsuper(add...   
        ccef4c7df48e1647fb37cf453729e7970c051093  [/**\n * Constructs a new instance of this cla...   
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01                                                 []   

                                                  used_in_fix        f1  \
bid     fid                                                               
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a          1.0  0.159427   
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5          1.0  0.098763   
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e          0.0  0.013824   
        ccef4c7df48e1647fb37cf453729e7970c051093          0.0  0.009233   
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01          0.0  0.030794   

                                                    result  
bid     fid                                                 
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a  0.926125  
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5  0.657869  
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e  0.548794  
        ccef4c7df48e1647fb37cf453729e7970c051093  0.548793  
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01  0.548622

In [166]:
all_report_methodContent_index_dataframe=report_dataFrame.join(all_methodContent_index_dataframe,how='inner')
all_report_methodContent_index_dataframe.head()

summary  \
bid     fid                                                                                           
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a   [DirectoryDialog] There is no disk in the dri...   
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5   [DirectoryDialog] There is no disk in the dri...   
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e   [DirectoryDialog] There is no disk in the dri...   
        ccef4c7df48e1647fb37cf453729e7970c051093   [DirectoryDialog] There is no disk in the dri...   
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01   [DirectoryDialog] There is no disk in the dri...   

                                                                                        description  \
bid     fid                                                                                           
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a  Any operation which brings up a file dialog bo...   
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5  Any operation which brings up a file dialog bo...   
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e  Any operation which brings up a file dialog bo...   
        ccef4c7df48e1647fb37cf453729e7970c051093  Any operation which brings up a file dialog bo...   
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01  Any operation which brings up a file dialog bo...   

                                                                                      methodContent  \
bid     fid                                                                                           
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a  [/**\n * Constructs a new instance of this cla...   
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5  [/** Ansi/Unicode wrappers */\n\npublic static...   
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e  [public IOleWindow(int address) {\n\tsuper(add...   
        ccef4c7df48e1647fb37cf453729e7970c051093  [/**\n * Constructs a new instance of this cla...   
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01                                                 []   

                                                  used_in_fix        f1  \
bid     fid                                                               
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a          1.0  0.159427   
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5          1.0  0.098763   
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e          0.0  0.013824   
        ccef4c7df48e1647fb37cf453729e7970c051093          0.0  0.009233   
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01          0.0  0.030794   

                                                    result  
bid     fid                                                 
a0c9251 e7a5e5ff9e842566fce2b344076eda8486db4c1a  0.926125  
        146f43ae14ef2b9d67dd1ebc1e89301d7da4f0d5  0.657869  
        5b25a2888e0399ba89b04fd4a9dfb7727f98490e  0.548794  
        ccef4c7df48e1647fb37cf453729e7970c051093  0.548793  
        ca0faf5d670090c4b5c3f4dccbcedefe28fb6b01  0.548622

In [167]:
sum(all_report_methodContent_index_dataframe['used_in_fix'])/all_report_methodContent_index_dataframe.shape[0]

0.25

In [168]:
all_report_methodContent_index_dataframe.fillna("",inplace=True)

In [170]:
task1_list=[]
all_report_methodContent_index_dataframe.fillna("",inplace=True)
def clean_string(string):
    outstring_list=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
    return ' '.join(outstring_list)
sum_label=0
for i,(index, row) in enumerate(all_report_methodContent_index_dataframe.iterrows()):
#     print(index[0],index[1],row['summary'],row['description'],row['methodContent'],row['used_in_fix'])
    if len(row['methodContent'])==0:
        continue
    guid='_'.join([index[0],index[1]])
    print(i,'summary :',type(row['summary']),'description :',type(row['description']))
    q_paras=[clean_string(row['summary']),clean_string(row['description'])]
    c_paras=[clean_string(string) for string in row['methodContent']]
    label=int(row['used_in_fix'])
    
    for q in q_paras:
        if q=="":
            continue
        for c in c_paras:
            if c=="":
                continue
            task1=dict()
            
            task1['guid']=guid
            task1['text_a']=q
            task1['text_b']=c
            task1['label']=label
            sum_label+=label
            task1_list.append(task1)
#     print(task1)
#     if i==2:
#         break


0 summary : <class 'str'> description : <class 'str'>
1 summary : <class 'str'> description : <class 'str'>
2 summary : <class 'str'> description : <class 'str'>
3 summary : <class 'str'> description : <class 'str'>
7 summary : <class 'str'> description : <class 'str'>
8 summary : <class 'str'> description : <class 'str'>
9 summary : <class 'str'> description : <class 'str'>
13 summary : <class 'str'> description : <class 'str'>
15 summary : <class 'str'> description : <class 'str'>
16 summary : <class 'str'> description : <class 'str'>
17 summary : <class 'str'> description : <class 'str'>
19 summary : <class 'str'> description : <class 'str'>
22 summary : <class 'str'> description : <class 'str'>
24 summary : <class 'str'> description : <class 'str'>
25 summary : <class 'str'> description : <class 'str'>
26 summary : <class 'str'> description : <class 'str'>
27 summary : <class 'str'> description : <class 'str'>
28 summary : <class 'str'> description : <class 'str'>
29 summary : <cla

294 summary : <class 'str'> description : <class 'str'>
295 summary : <class 'str'> description : <class 'str'>
296 summary : <class 'str'> description : <class 'str'>
300 summary : <class 'str'> description : <class 'str'>
301 summary : <class 'str'> description : <class 'str'>
302 summary : <class 'str'> description : <class 'str'>
303 summary : <class 'str'> description : <class 'str'>
305 summary : <class 'str'> description : <class 'str'>
306 summary : <class 'str'> description : <class 'str'>
307 summary : <class 'str'> description : <class 'str'>
308 summary : <class 'str'> description : <class 'str'>
309 summary : <class 'str'> description : <class 'str'>
310 summary : <class 'str'> description : <class 'str'>
311 summary : <class 'str'> description : <class 'str'>
312 summary : <class 'str'> description : <class 'str'>
315 summary : <class 'str'> description : <class 'str'>
316 summary : <class 'str'> description : <class 'str'>
318 summary : <class 'str'> description : <class

589 summary : <class 'str'> description : <class 'str'>
590 summary : <class 'str'> description : <class 'str'>
591 summary : <class 'str'> description : <class 'str'>
594 summary : <class 'str'> description : <class 'str'>
595 summary : <class 'str'> description : <class 'str'>
597 summary : <class 'str'> description : <class 'str'>
600 summary : <class 'str'> description : <class 'str'>
604 summary : <class 'str'> description : <class 'str'>
605 summary : <class 'str'> description : <class 'str'>
606 summary : <class 'str'> description : <class 'str'>
607 summary : <class 'str'> description : <class 'str'>
608 summary : <class 'str'> description : <class 'str'>
610 summary : <class 'str'> description : <class 'str'>
611 summary : <class 'str'> description : <class 'str'>
612 summary : <class 'str'> description : <class 'str'>
614 summary : <class 'str'> description : <class 'str'>
616 summary : <class 'str'> description : <class 'str'>
617 summary : <class 'str'> description : <class

881 summary : <class 'str'> description : <class 'str'>
882 summary : <class 'str'> description : <class 'str'>
883 summary : <class 'str'> description : <class 'str'>
884 summary : <class 'str'> description : <class 'str'>
885 summary : <class 'str'> description : <class 'str'>
886 summary : <class 'str'> description : <class 'str'>
887 summary : <class 'str'> description : <class 'str'>
888 summary : <class 'str'> description : <class 'str'>
889 summary : <class 'str'> description : <class 'str'>
890 summary : <class 'str'> description : <class 'str'>
891 summary : <class 'str'> description : <class 'str'>
892 summary : <class 'str'> description : <class 'str'>
893 summary : <class 'str'> description : <class 'str'>
894 summary : <class 'str'> description : <class 'str'>
899 summary : <class 'str'> description : <class 'str'>
900 summary : <class 'str'> description : <class 'str'>
901 summary : <class 'str'> description : <class 'str'>
902 summary : <class 'str'> description : <class

1157 summary : <class 'str'> description : <class 'str'>
1158 summary : <class 'str'> description : <class 'str'>
1160 summary : <class 'str'> description : <class 'str'>
1161 summary : <class 'str'> description : <class 'str'>
1164 summary : <class 'str'> description : <class 'str'>
1165 summary : <class 'str'> description : <class 'str'>
1172 summary : <class 'str'> description : <class 'str'>
1176 summary : <class 'str'> description : <class 'str'>
1177 summary : <class 'str'> description : <class 'str'>
1178 summary : <class 'str'> description : <class 'str'>
1179 summary : <class 'str'> description : <class 'str'>
1180 summary : <class 'str'> description : <class 'str'>
1181 summary : <class 'str'> description : <class 'str'>
1182 summary : <class 'str'> description : <class 'str'>
1183 summary : <class 'str'> description : <class 'str'>
1184 summary : <class 'str'> description : <class 'str'>
1188 summary : <class 'str'> description : <class 'str'>
1189 summary : <class 'str'> de

...

2411 summary : <class 'str'> description : <class 'str'>
2416 summary : <class 'str'> description : <class 'str'>
2418 summary : <class 'str'> description : <class 'str'>
2420 summary : <class 'str'> description : <class 'str'>
2421 summary : <class 'str'> description : <class 'str'>
2422 summary : <class 'str'> description : <class 'str'>
2424 summary : <class 'str'> description : <class 'str'>
2425 summary : <class 'str'> description : <class 'str'>
2426 summary : <class 'str'> description : <class 'str'>
2427 summary : <class 'str'> description : <class 'str'>
2428 summary : <class 'str'> description : <class 'str'>
2429 summary : <class 'str'> description : <class 'str'>
2432 summary : <class 'str'> description : <class 'str'>
2433 summary : <class 'str'> description : <class 'str'>
2434 summary : <class 'str'> description : <class 'str'>
2435 summary : <class 'str'> description : <class 'str'>
2436 summary : <class 'str'> description : <class 'str'>
2437 summary : <class 'str'> de

2652 summary : <class 'str'> description : <class 'str'>
2655 summary : <class 'str'> description : <class 'str'>
2656 summary : <class 'str'> description : <class 'str'>
2659 summary : <class 'str'> description : <class 'str'>
2660 summary : <class 'str'> description : <class 'str'>
2662 summary : <class 'str'> description : <class 'str'>
2663 summary : <class 'str'> description : <class 'str'>
2664 summary : <class 'str'> description : <class 'str'>
2665 summary : <class 'str'> description : <class 'str'>
2666 summary : <class 'str'> description : <class 'str'>
2668 summary : <class 'str'> description : <class 'str'>
2669 summary : <class 'str'> description : <class 'str'>
2670 summary : <class 'str'> description : <class 'str'>
2673 summary : <class 'str'> description : <class 'str'>
2674 summary : <class 'str'> description : <class 'str'>
2675 summary : <class 'str'> description : <class 'str'>
2677 summary : <class 'str'> description : <class 'str'>
2678 summary : <class 'str'> de

2929 summary : <class 'str'> description : <class 'str'>
2930 summary : <class 'str'> description : <class 'str'>
2931 summary : <class 'str'> description : <class 'str'>
2932 summary : <class 'str'> description : <class 'str'>
2942 summary : <class 'str'> description : <class 'str'>
2943 summary : <class 'str'> description : <class 'str'>
2944 summary : <class 'str'> description : <class 'str'>
2947 summary : <class 'str'> description : <class 'str'>
2948 summary : <class 'str'> description : <class 'str'>
2949 summary : <class 'str'> description : <class 'str'>
2950 summary : <class 'str'> description : <class 'str'>
2951 summary : <class 'str'> description : <class 'str'>
2952 summary : <class 'str'> description : <class 'str'>
2953 summary : <class 'str'> description : <class 'str'>
2954 summary : <class 'str'> description : <class 'str'>
2955 summary : <class 'str'> description : <class 'str'>
2956 summary : <class 'str'> description : <class 'str'>
2957 summary : <class 'str'> de

3172 summary : <class 'str'> description : <class 'str'>
3176 summary : <class 'str'> description : <class 'str'>
3177 summary : <class 'str'> description : <class 'str'>
3178 summary : <class 'str'> description : <class 'str'>
3179 summary : <class 'str'> description : <class 'str'>
3180 summary : <class 'str'> description : <class 'str'>
3196 summary : <class 'str'> description : <class 'str'>
3198 summary : <class 'str'> description : <class 'str'>
3200 summary : <class 'str'> description : <class 'str'>
3201 summary : <class 'str'> description : <class 'str'>
3202 summary : <class 'str'> description : <class 'str'>
3203 summary : <class 'str'> description : <class 'str'>
3204 summary : <class 'str'> description : <class 'str'>
3205 summary : <class 'str'> description : <class 'str'>
3206 summary : <class 'str'> description : <class 'str'>
3207 summary : <class 'str'> description : <class 'str'>
3208 summary : <class 'str'> description : <class 'str'>
3210 summary : <class 'str'> de

3452 summary : <class 'str'> description : <class 'str'>
3453 summary : <class 'str'> description : <class 'str'>
3454 summary : <class 'str'> description : <class 'str'>
3455 summary : <class 'str'> description : <class 'str'>
3456 summary : <class 'str'> description : <class 'str'>
3457 summary : <class 'str'> description : <class 'str'>
3458 summary : <class 'str'> description : <class 'str'>
3459 summary : <class 'str'> description : <class 'str'>
3460 summary : <class 'str'> description : <class 'str'>
3464 summary : <class 'str'> description : <class 'str'>
3465 summary : <class 'str'> description : <class 'str'>
3466 summary : <class 'str'> description : <class 'str'>
3467 summary : <class 'str'> description : <class 'str'>
3468 summary : <class 'str'> description : <class 'str'>
3469 summary : <class 'str'> description : <class 'str'>
3470 summary : <class 'str'> description : <class 'str'>
3471 summary : <class 'str'> description : <class 'str'>
3484 summary : <class 'str'> de

In [173]:
print(len(task1_list),sum_label,sum_label/len(task1_list))
task1_list[0]
label=0
label_0=0
for task in task1_list:
#     print(task)
    label+=task['label']
    if task['label']==0:
        label_0+=1
#     break
label
with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task2/data_sample.json','w',encoding='utf-8') as f_out:
    for task1 in task1_list:
        out_line = json.dumps(task1, ensure_ascii=False) + '\n'
        f_out.write(out_line)

214802 190582 0.8872449977188295


In [172]:
label_0+190582

214802

# 生成fine-tune阶段的数据结束

In [39]:
bid_list=list(all_results_df_top_k.index.get_level_values(0).unique())
len(bid_list)
bid_list[0], bug_reports[bid_list[0]]['bug_report']['summary'], bug_reports[bid_list[0]]['bug_report']['description']

('a0c9251',
 'Bug 35837  [DirectoryDialog] There is no disk in the drive. Please insert a disk into drive \\Device\\Harddisk0\\DR0',
 'Any operation which brings up a file dialog box rooted at "My Computer" tosses\nup a dialog box with the above error message whenever a harddrive is expanded. \n\nClick cancel or try again on dialog (has cancel, try again, and continue) twice,\nand then it opens up the disk, and proceeds normally.  \n\nIf you un-expand a drive, it does the same thing.\n\nThen again when you re-expand a drive.\n\nExamples:\nImport -> File System -> click Browse\n\nFeature.xml -> Export -> click Browse\n\nI have seen this all the way back through M4.  May have existed sooner. \nCurrently using RC3.\nPlatform: Windows 2K SP3')

In [40]:
bug_reports
summarys=[]
descriptions=[]
for bug_report_id in bid_list:
    current_bug_report = bug_reports[bug_report_id]['bug_report']
    summarys.append(current_bug_report['summary'])
    descriptions.append(current_bug_report['description'])
report_dataFrame=pd.DataFrame({'summary':summarys,'description':descriptions},index=bid_list)
report_dataFrame.index.names=['bid']
def remove_twoHeadWord(string):
    contents=string.split(' ')[2:]
    return ' '.join(contents)
report_dataFrame['summary']=report_dataFrame['summary'].apply(remove_twoHeadWord)
report_dataFrame.head()

summary  \
bid                                                          
a0c9251   [DirectoryDialog] There is no disk in the dri...   
1c62052              Outline view crashes on WinXP & Win2K   
6fac09a   crash in gtk_editable_delete_selection on GTK...   
b4a3cd3                 Need a locale String from FontData   
8380cc1      [StyledText] ContentWidthCache initialization   

                                               description  
bid                                                         
a0c9251  Any operation which brings up a file dialog bo...  
1c62052  I can reproduce this crash consistently.\n\n1....  
6fac09a  After compiling, running eclipse and looking a...  
b4a3cd3  2.1\n\nWe need a way to get the Locale informa...  
8380cc1                                               None

In [43]:
# all_results_df_top_k.index

In [44]:
bug_reports['9cdad39']['bug_report']

{'status': 'resolved fixed',
 'description': None,
 'timestamp': '1389980000',
 'summary': 'Bug 426009  StyledText without wordWrap is broken with BidiSegmentListener that inserts line breaks',
 'bug_id': '426009',
 'result': '1:bundles/org.eclipse.swt/Eclipse SWT Custom Widgets/common/org/eclipse/swt/custom/StyledText.java',
 'commit': '9cdad39',
 'id': '2'}

In [189]:
# tomcat_ast_file = pickle.loads(tomcat_ast_cache_collection_db['b6437f63a95972f4a2d3de68d4c9d5691c5792fd'])
# tomcat_ast_file

In [49]:
len(all_ast_index)

23145

In [45]:
all_ast_index=list(all_results_df_top_k.index.get_level_values(1).unique())
type(all_ast_index)
all_ast_file_methodContent=[]
for ast_index in all_ast_index:
#     print(ast_index)
    ast_file = pickle.loads(swt_ast_cache_collection_db[ast_index])
    all_ast_file_methodContent.append(ast_file['methodContent'])

In [46]:
count=0
for method in all_ast_file_methodContent:
    if len(method)==0:
        count+=1
print(count,len(all_ast_file_methodContent))

28 23145


In [62]:
# all_ast_index
all_ast_index_dataframe=pd.DataFrame({'methodContent':all_ast_file_methodContent},index=all_ast_index)
# print(all_ast_index_dataframe.head())
print(all_ast_index_dataframe.shape)
# all_ast_index_dataframe.set_index(["ast_index"], inplace=True)
# all_ast_index_dataframe
all_ast_index_dataframe.index.names=['fid']
all_ast_index_dataframe.head(2)

(23145, 1)


methodContent
fid                                                                                        
b5f5e1a2070ba15a8d5a8cd955de857225e0815b  [/**\n * Constructs a new instance of this cla...
6f547898bd6d011af1e621a2c002f10c39856cd4  [/**\n * Constructs a new instance of this cla...

In [59]:
# all_ast_index_dataframe['methodContent'].loc['6f547898bd6d011af1e621a2c002f10c39856cd4']

In [61]:
# all_ast_index_dataframe['methodContent'].loc['b5f5e1a2070ba15a8d5a8cd955de857225e0815b']

In [19]:
all_ast_index_dataframe.columns

Index(['methodContent'], dtype='object')

In [67]:
# all_ast_index_dataframe.to_csv('')
# tomcat_testing_fold_1.lef
# pd.merge(tomcat_testing_fold_1,all_ast_index_dataframe,right_on='ast_index',left_index=True, how='outer')
all_methodContent_index_dataframe=all_ast_index_dataframe.join(all_results_df_top_k,how='inner')

In [68]:
all_methodContent_index_dataframe.head()

methodContent  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  [/**\n * Constructs a new instance of this cla...   
        6f547898bd6d011af1e621a2c002f10c39856cd4  [/**\n * Constructs a new instance of this cla...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3  [/**\n * Constructs a new instance of this cla...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  [/**\n * Constructs a new instance of this cla...   
        638a1fbe3d9de7b7623c1fac1260408526230971  [/**\n * Constructs a new instance of this cla...   

                                                  used_in_fix        f1  \
bid     fid                                                               
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b          0.0  0.185988   
        6f547898bd6d011af1e621a2c002f10c39856cd4          0.0  0.159427   
        b759c9f92786cc5b07329d303f2bfe37239d0db3          0.0  0.159427   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a          1.0  0.159427   
        638a1fbe3d9de7b7623c1fac1260408526230971          0.0  0.233812   

                                                    result  
bid     fid                                                 
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  0.940310  
        6f547898bd6d011af1e621a2c002f10c39856cd4  0.928099  
        b759c9f92786cc5b07329d303f2bfe37239d0db3  0.926931  
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  0.926125  
        638a1fbe3d9de7b7623c1fac1260408526230971  0.924647

In [69]:
report_dataFrame.head()

summary  \
bid                                                          
a0c9251   [DirectoryDialog] There is no disk in the dri...   
1c62052              Outline view crashes on WinXP & Win2K   
6fac09a   crash in gtk_editable_delete_selection on GTK...   
b4a3cd3                 Need a locale String from FontData   
8380cc1      [StyledText] ContentWidthCache initialization   

                                               description  
bid                                                         
a0c9251  Any operation which brings up a file dialog bo...  
1c62052  I can reproduce this crash consistently.\n\n1....  
6fac09a  After compiling, running eclipse and looking a...  
b4a3cd3  2.1\n\nWe need a way to get the Locale informa...  
8380cc1                                               None

In [70]:
sum(all_report_methodContent_index_dataframe.loc['1839d9b']['used_in_fix'])

1.0

In [71]:
all_report_methodContent_index_dataframe=report_dataFrame.join(all_methodContent_index_dataframe,how='inner')
all_report_methodContent_index_dataframe.head()

summary  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b   [DirectoryDialog] There is no disk in the dri...   
        6f547898bd6d011af1e621a2c002f10c39856cd4   [DirectoryDialog] There is no disk in the dri...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3   [DirectoryDialog] There is no disk in the dri...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a   [DirectoryDialog] There is no disk in the dri...   
        638a1fbe3d9de7b7623c1fac1260408526230971   [DirectoryDialog] There is no disk in the dri...   

                                                                                        description  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  Any operation which brings up a file dialog bo...   
        6f547898bd6d011af1e621a2c002f10c39856cd4  Any operation which brings up a file dialog bo...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3  Any operation which brings up a file dialog bo...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  Any operation which brings up a file dialog bo...   
        638a1fbe3d9de7b7623c1fac1260408526230971  Any operation which brings up a file dialog bo...   

                                                                                      methodContent  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  [/**\n * Constructs a new instance of this cla...   
        6f547898bd6d011af1e621a2c002f10c39856cd4  [/**\n * Constructs a new instance of this cla...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3  [/**\n * Constructs a new instance of this cla...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  [/**\n * Constructs a new instance of this cla...   
        638a1fbe3d9de7b7623c1fac1260408526230971  [/**\n * Constructs a new instance of this cla...   

                                                  used_in_fix        f1  \
bid     fid                                                               
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b          0.0  0.185988   
        6f547898bd6d011af1e621a2c002f10c39856cd4          0.0  0.159427   
        b759c9f92786cc5b07329d303f2bfe37239d0db3          0.0  0.159427   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a          1.0  0.159427   
        638a1fbe3d9de7b7623c1fac1260408526230971          0.0  0.233812   

                                                    result  
bid     fid                                                 
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  0.940310  
        6f547898bd6d011af1e621a2c002f10c39856cd4  0.928099  
        b759c9f92786cc5b07329d303f2bfe37239d0db3  0.926931  
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  0.926125  
        638a1fbe3d9de7b7623c1fac1260408526230971  0.924647

In [72]:
all_report_methodContent_index_dataframe=all_report_methodContent_index_dataframe[['summary','description','methodContent','used_in_fix']]
all_report_methodContent_index_dataframe.head()

summary  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b   [DirectoryDialog] There is no disk in the dri...   
        6f547898bd6d011af1e621a2c002f10c39856cd4   [DirectoryDialog] There is no disk in the dri...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3   [DirectoryDialog] There is no disk in the dri...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a   [DirectoryDialog] There is no disk in the dri...   
        638a1fbe3d9de7b7623c1fac1260408526230971   [DirectoryDialog] There is no disk in the dri...   

                                                                                        description  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  Any operation which brings up a file dialog bo...   
        6f547898bd6d011af1e621a2c002f10c39856cd4  Any operation which brings up a file dialog bo...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3  Any operation which brings up a file dialog bo...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  Any operation which brings up a file dialog bo...   
        638a1fbe3d9de7b7623c1fac1260408526230971  Any operation which brings up a file dialog bo...   

                                                                                      methodContent  \
bid     fid                                                                                           
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b  [/**\n * Constructs a new instance of this cla...   
        6f547898bd6d011af1e621a2c002f10c39856cd4  [/**\n * Constructs a new instance of this cla...   
        b759c9f92786cc5b07329d303f2bfe37239d0db3  [/**\n * Constructs a new instance of this cla...   
        e7a5e5ff9e842566fce2b344076eda8486db4c1a  [/**\n * Constructs a new instance of this cla...   
        638a1fbe3d9de7b7623c1fac1260408526230971  [/**\n * Constructs a new instance of this cla...   

                                                  used_in_fix  
bid     fid                                                    
a0c9251 b5f5e1a2070ba15a8d5a8cd955de857225e0815b          0.0  
        6f547898bd6d011af1e621a2c002f10c39856cd4          0.0  
        b759c9f92786cc5b07329d303f2bfe37239d0db3          0.0  
        e7a5e5ff9e842566fce2b344076eda8486db4c1a          1.0  
        638a1fbe3d9de7b7623c1fac1260408526230971          0.0

In [77]:
all_report_methodContent_index_dataframe.fillna("",inplace=True)

In [78]:
task1_list=[]
def clean_string(string):
    outstring_list=re.findall(r'[\w"]+|[.,!?;{}:()\+\-\*\/=><"]',string)
    return ' '.join(outstring_list)
for i,(index, row) in enumerate(all_report_methodContent_index_dataframe.iterrows()):
#     print(index[0],index[1],row['summary'],row['description'],row['methodContent'],row['used_in_fix'])
    task1=dict()
    task1['guid']='_'.join([index[0],index[1]])
    task1['q_paras']=[clean_string(row['summary']),clean_string(row['description'])]
    task1['c_paras']=[clean_string(string) for string in row['methodContent']]
    task1['label']=int(row['used_in_fix'])
    task1_list.append(task1)
#     if i==100:
#         break
with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/case_para_sample.json','w',encoding='utf-8') as f_out:
    for task1 in task1_list:
        out_line = json.dumps(task1, ensure_ascii=False) + '\n'
        f_out.write(out_line)

In [249]:
guids = []
input_ids = []
attention_mask = []
token_type_ids = []
for i in range(3):
    input_ids_item = []
    attention_mask_item = []
    token_type_ids_item = []
    for j in range(2):
        input_ids_row = []
        attention_mask_row = []
        token_type_ids_row = []
        for k in range(10):
            input_ids_row.append([1,1,1])
            attention_mask_row.append([2,2,2])
            token_type_ids_row.append([3,3,3])
        input_ids_item.append(input_ids_row)
        attention_mask_item.append(attention_mask_row)
        token_type_ids_item.append(token_type_ids_row)
    guids.append('guid')
    input_ids.append(input_ids_item)
    attention_mask.append(attention_mask_item)
    token_type_ids.append(token_type_ids_item)

In [250]:
import torch
print(guids)
print(input_ids)
print(attention_mask)
input_ids = torch.LongTensor(input_ids)
attention_mask = torch.LongTensor(attention_mask)
token_type_ids = torch.LongTensor(token_type_ids)

['guid', 'guid', 'guid']
[[[[1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1]], [[1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1]]], [[[1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1]], [[1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1]]], [[[1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1]], [[1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1]]]]
[[[[2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2]], [[2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2]]], [[[2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [

In [25]:
input_ids.shape

torch.Size([3, 2, 10, 3])

In [178]:
from transformers import RobertaTokenizer, RobertaConfig, RobertaModel, AdamW
encoder = RobertaModel.from_pretrained("microsoft/codebert-base")

In [181]:
inputs=input_ids[0,0:2].view(-1,10)
attention=attention_mask[0,0:2].view(-1,10)

In [194]:
torch.arange(4)

tensor([0, 1, 2, 3])

In [182]:
inputs.ne(1)

tensor([[False, False, False, False, False, False, False, False, False, False],
        [False, False, False, False, False, False, False, False, False, False],
        [False, False, False, False, False, False, False, False, False, False],
        [False, False, False, False, False, False, False, False, False, False],
        [False, False, False, False, False, False, False, False, False, False],
        [False, False, False, False, False, False, False, False, False, False]])

In [ ]:
outputs=self.encoder(inputs,attention_mask=inputs.ne(1))[1]

In [29]:
sample1=input_ids[0,0:2]
print(sample1.shape)
sample1

torch.Size([2, 10, 3])


tensor([[[1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1]],

        [[1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1],
         [1, 1, 1]]])

In [20]:
bert = RobertaModel.from_pretrained("microsoft/codebert-base")

In [198]:
tokenizer.convert_ids_to_tokens(1)

'<pad>'

In [261]:
code_inputs=torch.tensor([[0,0,0,1]])
nl_inputs=torch.tensor([[1,1,1,1]])
targets=torch.tensor([-1])
bs=code_inputs.shape[0]
inputs=torch.cat((code_inputs,nl_inputs),0)
embedding_loss(code_inputs,nl_inputs,targets)

tensor(0.)

In [ ]:
-1 tensor(0.6508)
0 tensor(0.4055)
1 tensor(0.4102)

In [203]:
inputs.shape
attention_mask=inputs.ne(1)
attention_mask

tensor([[ True,  True,  True, False],
        [ True,  True,  True, False],
        [ True,  True,  True, False],
        [ True,  True,  True, False],
        [ True,  True,  True, False],
        [ True,  True,  True, False]])

In [214]:
embedding_loss=torch.nn.CosineEmbeddingLoss(margin=0.5, size_average=None, reduce=None, reduction='mean')

tensor(0.5213)

In [206]:
outputs=encoder(inputs,attention_mask=inputs.ne(1))[1]
print('outputs shape :',outputs.shape)
code_vec=outputs[:bs]
print('code_vec shape :',code_vec.shape)
nl_vec=outputs[bs:]
print('nl_vec shape :',nl_vec.shape)
print('nl_vec[:,None,:] shape',nl_vec[:,None,:].shape)
print('code_vec[None,:,:] shape ',code_vec[None,:,:].shape)
print('(nl_vec[:,None,:]*code_vec[None,:,:]) shape ',(nl_vec[:,None,:]*code_vec[None,:,:]).shape)
scores=(nl_vec[:,None,:]*code_vec[None,:,:]).sum(-1)
print('scores shape',scores.shape)
loss_fct = CrossEntropyLoss()
loss = loss_fct(scores, torch.arange(nl_inputs.shape[0], device=scores.device))
print('loss :',loss)

outputs shape : torch.Size([6, 768])
code_vec shape : torch.Size([4, 768])
nl_vec shape : torch.Size([2, 768])
nl_vec[:,None,:] shape torch.Size([2, 1, 768])
code_vec[None,:,:] shape  torch.Size([1, 4, 768])
(nl_vec[:,None,:]*code_vec[None,:,:]) shape  torch.Size([2, 4, 768])
scores shape torch.Size([2, 4])
loss : tensor(0.9564, grad_fn=<NllLossBackward>)


In [266]:
tokenizer.tokenize('sdjk sd')

['sd', 'j', 'k', 'Ġsd']

In [267]:
tokenizer.convert_ids_to_tokens(0),tokenizer.convert_ids_to_tokens(1),tokenizer.sep_token,tokenizer.convert_tokens_to_ids('Ġ[CLS]')

('<s>', '<pad>', '</s>', 3)

In [257]:
from torch.nn import CrossEntropyLoss, MSELoss
for k in range(input_ids.shape[0]):
    for i in range(0,2,2):
        vec,lst=encoder(input_ids[k,i:i+2].view(-1,10),attention_mask=attention_mask[k,i:i+2].view(-1,10))
        print(vec.shape,lst.shape)
        bs=4
        code_vec=vec[:,:bs,:]
        nl_vec=vec[:,bs:,:]
        print(code_vec.shape,nl_vec.shape)
        code_vec_mean=code_vec.mean(axis=1,keepdim=False)
        print(code_vec.mean(axis=1,keepdim=False).shape)  
        nl_vec_mean=nl_vec.mean(axis=1,keepdim=False)
        print(nl_vec.mean(axis=1,keepdim=False).shape)  
        targets=torch.tensor([1,-1,1,-1,1,1])
        loss=embedding_loss(code_vec_mean,nl_vec_mean,targets)
        print(loss)
#         print('score :',nl_vec[:,None,:].shape,code_vec[None,:,:].shape,(nl_vec[:,None,:]*code_vec[None,:,:]).shape)
#         scores=(nl_vec[:,None,:]*code_vec[None,:,:]).sum(-1)
#         print('s :',scores.shape,scores)
#         loss_fct = CrossEntropyLoss()
#         loss = loss_fct(scores, torch.arange(bs, device=scores.device))
#         print('loss :',loss)

torch.Size([6, 10, 768]) torch.Size([6, 768])
torch.Size([6, 4, 768]) torch.Size([6, 6, 768])
torch.Size([6, 768])
torch.Size([6, 768])
tensor(0.1667, grad_fn=<MeanBackward0>)
torch.Size([6, 10, 768]) torch.Size([6, 768])
torch.Size([6, 4, 768]) torch.Size([6, 6, 768])
torch.Size([6, 768])
torch.Size([6, 768])
tensor(0.1667, grad_fn=<MeanBackward0>)
torch.Size([6, 10, 768]) torch.Size([6, 768])
torch.Size([6, 4, 768]) torch.Size([6, 6, 768])
torch.Size([6, 768])
torch.Size([6, 768])
tensor(0.1667, grad_fn=<MeanBackward0>)


In [24]:
_.shape

torch.Size([6, 10, 768])

In [22]:
lst.shape

torch.Size([6, 768])

# 10.10开始跑的

In [16]:
25000/1000,25*10/60

(25.0, 4.166666666666667)

In [11]:
for k in range(input_ids.size()[0]):
    for i in range(0,2,2):
        input_id_tmp=input_ids[k,i:i+2]
        print(k,input_id_tmp.shape)
        input_id_view=input_id_tmp.view(-1,3)
        print(k,input_id_view.shape)

0 torch.Size([2, 10, 3])
0 torch.Size([20, 3])
1 torch.Size([2, 10, 3])
1 torch.Size([20, 3])
2 torch.Size([2, 10, 3])
2 torch.Size([20, 3])


In [3]:
with open('/data/hdj/tracking_buggy_files/joblib_memmap_swt/train_1_tokenzied2_6_stage2.json','r',encoding='utf-8') as f_in:
    label=0
    i=0
    for line in f_in:
        line=eval(line)
        label+=line['label']
        i+=1
    print(label,i,label/i)

907 25907 0.03500984289960243


# 组装成rnn需要的数据格式

In [3]:

label_1=0
j=0
for key,val in guid_label.items():
    j+=1
    label_1+=val
print(label_1)
print(j)
print(label_1/j)

237
7239
0.03273932863655201


In [2]:
len(guid_label)
# guid_label

24981

In [27]:
#这里是在oversample
with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/embedding_sample.json','r',encoding='utf-8') as f_in:
    with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/embedding_sample_label.json','w',encoding='utf-8') as f_out:
        for line in f_in:
            line_dict=eval(line)
    #         for key,val in line.items():
            if line_dict['label']==1:
                for i in range(10):
                    f_out.write(line)
            else:
                f_out.write(line)


In [27]:
#测试新增19个特征
import json
with open('/data/hdj/BERT_PLI/train_1_tokenzied2_15_stage2_humFea.json','r',encoding='utf-8') as f_in:
    with open('/data/hdj/BERT_PLI/train_1_tokenzied2_15_stage2_humFea_plus.json','w',encoding='utf-8') as f_out:
        for line in f_in:
            line=eval(line)
            line['humFea']=[i for i in range(19)]
            out_line = json.dumps(line, ensure_ascii=False) + '\n'
            f_out.write(out_line)
        

In [2]:
#把500个文件分割成20个，看看哪里效果很差 为啥
import collections
import pandas as pd
import numpy as np
out_path_label='/home/hdj/BERT-PLI-IJCAI2020/result/sort_floss_2_15_train_0525_2hard_1easy_right7model_label.json'

all_data=collections.defaultdict(list)
with open(out_path_label,'r',encoding='utf-8') as f_in:
    for i,line in enumerate(f_in):
#         line=eval(line)
        all_data[i//1000].append(line)

In [20]:
with open('/data/hdj/BERT_PLI/test_2_tokenzied2_15_stage2.json','r',encoding='utf-8') as f_in:
    for line in f_in:
        line=eval(line)
        if(line['guid'].split('_')[0]=='8616a65' and line['label']==1):
            print(line['guid'])
            print(line)
#         break

8616a65_fb5d0456d39e8d1fcd4dc3154637093f338ebd33
{'guid': '8616a65_fb5d0456d39e8d1fcd4dc3154637093f338ebd33', 'q_paras': ['Text wider normal toolitem ampersand used', 'Text without ampersands displayed correctly Text ampersand one word wider normal Text one word starting ampersand even wider Mac OS 10 3 The following snippet demonstrates org eclipse swt SWT org eclipse swt layout FillLayout org eclipse swt widgets Bug main String args Display display Display getDefault Shell shell Shell display shell setLayout FillLayout shell setSize 100 100 ToolBar toolbar ToolBar shell SWT NONE fine ToolItem good ToolItem toolbar SWT NONE good setText text somewhat wider normal ToolItem hmm ToolItem toolbar SWT NONE hmm setText single words displayed size ToolItem bad ToolItem toolbar SWT NONE bad setText shell open shell pack shell isDisposed display readAndDispatch display sleep I attach screenshot'], 'c_paras': ['k user helpcont count appear org detail togeth also HI fake transparentpixel helpstr

In [11]:
all_data[2]

['{"id_": "8616a65_ebb5010a053371d478bf37571537e8a3619720e0", "res": [0.9341893792152405, -0.9827346205711365], "label": 0}\n',
 '{"id_": "8616a65_aad2025e8608857074847b13221bcc39be3cca31", "res": [1.1576634645462036, -1.211112380027771], "label": 0}\n',
 '{"id_": "8616a65_1a43845b2bef97d46808b764b4b1b108d96e6f11", "res": [0.9344816207885742, -0.9828246831893921], "label": 0}\n',
 '{"id_": "8616a65_fb5d0456d39e8d1fcd4dc3154637093f338ebd33", "res": [0.9343498945236206, -0.9828810691833496], "label": 1}\n',
 '{"id_": "8616a65_25f1dc48e2fa573703d231678eeda1dd371a855a", "res": [0.9345563650131226, -0.982914924621582], "label": 0}\n',
 '{"id_": "8616a65_286de28d1371f79b5f15263eb337936557da7e58", "res": [0.878926694393158, -0.9240803718566895], "label": 0}\n',
 '{"id_": "8616a65_03bd08ee8a13e849186816f0f1d54c58766bb079", "res": [0.9342120289802551, -0.9827899932861328], "label": 0}\n',
 '{"id_": "8616a65_dc416526d5404314bad5e8068c8d4aa89d70ac6e", "res": [0.8786940574645996, -0.92401415109634

In [10]:
# for i in range(25):
#     print(calculate_metrics(all_data[i]))
calculate_metrics(all_data[2])

/home/hdj/anaconda3/envs/waf/lib/python3.7/site-packages/ipykernel_launcher.py:52: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


({1: 0.0,
  2: 0.05,
  3: 0.05,
  4: 0.1,
  5: 0.15,
  6: 0.15,
  7: 0.2,
  8: 0.2,
  9: 0.2,
  10: 0.2,
  11: 0.2,
  12: 0.2,
  13: 0.25,
  14: 0.25,
  15: 0.25,
  16: 0.25,
  17: 0.25,
  18: 0.3,
  19: 0.3,
  20: 0.3},
 0.06983892429767018,
 0.08136977265526364)

In [5]:
def calculate_metrics(f_in, k_range=range(1, 21)):
    bid_list=[]
    used_in_fix=[]
    result=[]
    for line in f_in:
        line=eval(line)
        bid_list.append(line['id_'].split('_')[0])
        used_in_fix.append(line['label'])
        result.append(line['res'][1])
    stage2_result=pd.DataFrame()
    stage2_result['bid']=bid_list
    stage2_result['used_in_fix']=used_in_fix
    stage2_result['result']=result
    stage2_result.set_index('bid',inplace=True)
    stage2_result.shape
    verification_df=stage2_result
    average_precision_per_bug_report = []
    reciprocal_ranks = []
    # calculate per each query (bug report)
    accuracy_at_k = dict.fromkeys(k_range, 0)
    bug_report_number = 0
    for bug_report, bug_report_files_dataframe in verification_df.groupby(level=0, sort=False):
#         print(bug_report)
        min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
        bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
        sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
        if sorted_df.shape[0] == 0:
            sorted_df = bug_report_files_dataframe.copy().sort_values(ascending=False, by=['result'])
            # print((bug_report_files_dataframe['used_in_fix'] == 1.0).sum())

        precision_at_k = []
        # precision per k in range
        tmp = sorted_df
        a = range(1, tmp.shape[0] + 1)
        tmp['position'] = pd.Series(a, index=tmp.index)
        
        large_k_p = tmp[(tmp['used_in_fix'] == 1.0)]['position'].tolist()
        unique_results = sorted_df['result'].unique().tolist()
        unique_results.sort()
        for fk in large_k_p:
            k = int(fk)
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = (largest_at_k['used_in_fix'] == 1.0).sum()

            p = float(real_fixes_at_k) / float(k)
            precision_at_k.append(p)

        # average precision is sum of k precisions divided by K
        # K is set of positions of relevant documents in the ranked list
        average_precision = pd.Series(precision_at_k).mean()
        # average_precision = pd.Series(precision_at_k).sum() / float(large_k)
        average_precision_per_bug_report.append(average_precision)

        # accuracy
        for k in k_range:
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = largest_at_k['used_in_fix'][(largest_at_k['used_in_fix'] == 1.0)].count()
            if real_fixes_at_k >= 1:
                accuracy_at_k[k] += 1

        # reciprocal rank
        indexes_of_fixes = np.flatnonzero(sorted_df['used_in_fix'] == 1.0)
        if indexes_of_fixes.size == 0:
            reciprocal_ranks.append(0.0)
        else:
            first_index = indexes_of_fixes[0]
            reciprocal_rank = 1.0 / (first_index + 1)
            reciprocal_ranks.append(reciprocal_rank)
        # bug number
        bug_report_number += 1

        del bug_report, bug_report_files_dataframe

    # print("average_precision_per_bug_report", average_precision_per_bug_report)
    mean_average_precision = pd.Series(average_precision_per_bug_report).mean()
    # print('mean average precision', mean_average_precision)
    mean_reciprocal_rank = pd.Series(reciprocal_ranks).mean()
    # print('mean reciprocal rank', mean_reciprocal_rank)
#     print('accuracy_at_k :',accuracy_at_k)
    for k in k_range:
        accuracy_at_k[k] = accuracy_at_k[k] / bug_report_number
        # print('accuracy for k', accuracy_at_k[k], k)
    return accuracy_at_k, mean_average_precision, mean_reciprocal_rank

In [2]:
# swt_testing_fold_1.rename(index={0:'bid',1:'fid'},  inplace=True)
# swt_testing_fold_1.index.names = ['bid','fid']
#TODO 增加label
import json
import numpy as np
import pandas as pd
guid_label=dict()
# with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/case_para_sample_8.json','r',encoding='utf-8') as f_in:
with open('/data/hdj/BERT_PLI/test_3hard_2_5_10method.json','r',encoding='utf-8') as f_in:
    label=0
    i=0
    for line in f_in:
        line=eval(line)
        i+=1
        guid_label[line['guid']]=line['label']

pred_no_label='/home/hdj/BERT-PLI-IJCAI2020/result/0528_test_3hard_2_5_10method.json'
out_path_label='/home/hdj/BERT-PLI-IJCAI2020/result/0528_test_3hard_2_5_10method_label.json'
with open(pred_no_label,'r',encoding='utf-8') as f_in:
    with open(out_path_label,'w',encoding='utf-8') as f_out:
        for line in f_in:
            line=eval(line)
            line['label']=guid_label[line['id_']]
            out_line = json.dumps(line, ensure_ascii=False) + '\n'
            f_out.write(out_line)
print(i)
bid_list=[]
used_in_fix=[]
result=[]
with open(out_path_label,'r',encoding='utf-8') as f_in:
    for line in f_in:
        line=eval(line)
        bid_list.append(line['id_'].split('_')[0])
        used_in_fix.append(line['label'])
        result.append(line['res'][1])
stage2_result=pd.DataFrame()
stage2_result['bid']=bid_list
stage2_result['used_in_fix']=used_in_fix
stage2_result['result']=result
stage2_result.set_index('bid',inplace=True)
stage2_result.shape
def calculate_metrics(verification_df, k_range=range(1, 21)):
    average_precision_per_bug_report = []
    reciprocal_ranks = []
    # calculate per each query (bug report)
    accuracy_at_k = dict.fromkeys(k_range, 0)
    bug_report_number = 0
    for bug_report, bug_report_files_dataframe in verification_df.groupby(level=0, sort=False):
        print(bug_report)
        min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
        bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
        sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
        if sorted_df.shape[0] == 0:
            sorted_df = bug_report_files_dataframe.copy().sort_values(ascending=False, by=['result'])
            # print((bug_report_files_dataframe['used_in_fix'] == 1.0).sum())

        precision_at_k = []
        # precision per k in range
        tmp = sorted_df
        a = range(1, tmp.shape[0] + 1)
        tmp['position'] = pd.Series(a, index=tmp.index)
        
        large_k_p = tmp[(tmp['used_in_fix'] == 1.0)]['position'].tolist()
        unique_results = sorted_df['result'].unique().tolist()
        unique_results.sort()
        for fk in large_k_p:
            k = int(fk)
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = (largest_at_k['used_in_fix'] == 1.0).sum()

            p = float(real_fixes_at_k) / float(k)
            precision_at_k.append(p)

        # average precision is sum of k precisions divided by K
        # K is set of positions of relevant documents in the ranked list
        average_precision = pd.Series(precision_at_k).mean()
        # average_precision = pd.Series(precision_at_k).sum() / float(large_k)
        average_precision_per_bug_report.append(average_precision)

        # accuracy
        for k in k_range:
            k_largest = unique_results[-k:]

            largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
            real_fixes_at_k = largest_at_k['used_in_fix'][(largest_at_k['used_in_fix'] == 1.0)].count()
            if real_fixes_at_k >= 1:
                accuracy_at_k[k] += 1

        # reciprocal rank
        indexes_of_fixes = np.flatnonzero(sorted_df['used_in_fix'] == 1.0)
        if indexes_of_fixes.size == 0:
            reciprocal_ranks.append(0.0)
        else:
            first_index = indexes_of_fixes[0]
            reciprocal_rank = 1.0 / (first_index + 1)
            reciprocal_ranks.append(reciprocal_rank)
        # bug number
        bug_report_number += 1

        del bug_report, bug_report_files_dataframe

    # print("average_precision_per_bug_report", average_precision_per_bug_report)
    mean_average_precision = pd.Series(average_precision_per_bug_report).mean()
    # print('mean average precision', mean_average_precision)
    mean_reciprocal_rank = pd.Series(reciprocal_ranks).mean()
    # print('mean reciprocal rank', mean_reciprocal_rank)
    print('accuracy_at_k :',accuracy_at_k)
    for k in k_range:
        accuracy_at_k[k] = accuracy_at_k[k] / bug_report_number
        # print('accuracy for k', accuracy_at_k[k], k)
    return accuracy_at_k, mean_average_precision, mean_reciprocal_rank

calculate_metrics(stage2_result)

7250
6fcdd86
4f39524
a754695
29deb6d
1a14ea6
b9729f2
c9fe93d
05c6b3f
c68f62c
ccd2d5a
9fc8665
2460307
c7591f1
6adfd78
1563c7f
ed640c3
8c2a378
eafab0c
a335a83

/home/hdj/anaconda3/envs/waf/lib/python3.7/site-packages/ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.



32e1464
7b9ce76
2c265bf
259ec5f
b4dfa25
63ba006
2e726b8
8cb9404
6ac6360
696a120
870787f
d2a1d09
b16cc7a
c9eeb92
712033c
1481d03
fae0ba1
cad161b
e5d64fd
b65d155
4953e90
d7f3b7d
058843e
e916382
aa3c6d8
5d702d1
d0069d7
e718eb8
a874d09
28693b7
791b4b7
eacb643
8619e94
43b30ec
dcbdf5d
592d29b
0a46c6b
be7b110
7d46d43
9ce3caf
1a69ddd
b05ed3b
7b86bb8
f395263
3dd7eb1
c190c30
1b3622f
d453cf5
d3b70aa
1f7643c
aaca3a8
fbb292a
1dacd3e
a41e15e
e55ec02
7c8383f
0f396c8
f176c66
84cc272
2744fe7
cd2045e
fb6bc4c
9d0937b
b22a7d1
6b3c7f0
2d5ae3a
c344dba
1905ff1
4bb2ca6
11ce129
13013d1
9a80949
f6a9fae
f7ed035
a1e0ef9
c7907f9
6b181ae
5db676d
d204b30
082681b
8c4c9f9
a49b153
68e82ef
84e83aa
61ef4aa
80afedd
b271137
afc0fa6
200e623
84ada67
22b8405
599e467
f44fbcf
b0e12cd
89226ef
471ee59
b7e8023
03bf77d
7460be0
b1b4091
ad1bc0e
ef7e4c7
6638802
10c11bd
736f350
cf7344c
e1ed2e3
70a2f2c
15fa06c
dc90724
b018239
6c629e4
2d8f819
46fe45c
5b8cefc
69129a9
b7715ad
a569b2c
157cd36
fd4ff51
481ef89
9920571
3576667
05fe758
247e8fc

({1: 0.020689655172413793,
  2: 0.09655172413793103,
  3: 0.1310344827586207,
  4: 0.1793103448275862,
  5: 0.20689655172413793,
  6: 0.2482758620689655,
  7: 0.296551724137931,
  8: 0.35172413793103446,
  9: 0.4,
  10: 0.46206896551724136,
  11: 0.496551724137931,
  12: 0.5241379310344828,
  13: 0.5517241379310345,
  14: 0.6,
  15: 0.6068965517241379,
  16: 0.6275862068965518,
  17: 0.6275862068965518,
  18: 0.6620689655172414,
  19: 0.6758620689655173,
  20: 0.6896551724137931},
 0.14862041953155286,
 0.1443251076048167)

In [7]:
accuracy_at_k : {1: 1, 2: 1, 3: 2, 4: 3, 5: 3, 6: 3, 7: 3, 8: 4, 9: 6, 10: 6, 11: 6, 12: 6, 13: 6, 14: 7, 15: 7, 16: 8, 17: 9, 18: 9, 19: 9, 20: 9}
({1: 0.05,
  2: 0.05,
  3: 0.1,
  4: 0.15,
  5: 0.15,
  6: 0.15,
  7: 0.15,
  8: 0.2,
  9: 0.3,
  10: 0.3,
  11: 0.3,
  12: 0.3,
  13: 0.3,
  14: 0.35,
  15: 0.35,
  16: 0.4,
  17: 0.45,
  18: 0.45,
  19: 0.45,
  20: 0.45},
 0.12368327715414822,
 0.1230359557255768)

8333.333333333334

In [5]:
with open('/data/hdj/BERT_PLI/test_2_tokenzied2_15_stage2.json','r',encoding='utf-8') as f_in:
    for line in f_in:
        line=eval(line)
        print(line['guid'])
        print(line)
        break
with open('/data/hdj/BERT_PLI/test_3_tokenzied2_15_stage2.json','r',encoding='utf-8') as f_in:
    for line in f_in:
        line=eval(line)
        print(line['guid'])
        print(line)
        break

d2fc065_11b61085ef12101694cade14607e287b6d5f3e96
{'guid': 'd2fc065_11b61085ef12101694cade14607e287b6d5f3e96', 'q_paras': ['Bug List showSelection method', 'List showSelection method always make selection visible The problem calculation bottomIndex bottomIndex Math min topIndex visibleCount 1 count 1 changed bottomIndex Math min topIndex visibleCount 1 count 1'], 'c_paras': ['count appear nitem selectionpolici repeat togeth remain greater also xmbrows Xm nmultipl swt dispos scrollbar length structur ad local either lastindex access tabtransl xtmalloc return lay getstyl xmnbottomattach superclass listfont take newindex fixstr space indexof code max getborderwidth comput possibl po getitemcount setbound cr xmcharset construct action int extend removeal utf state selectionlisten indic codepag affect xmnselecteditem eventt highlight list widgetdefaultselect longest bar four thick parent setfocusindex charset border text showselect new xmstring polici client current switch call getselectioni

# 组装成rnn需要的数据格式 完成

In [18]:
# output_data=dict()
# import json
# with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/embedding_sample_0524_test.json','r',encoding='utf-8') as f_in:
#     with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/embedding_sample_0524_test_label.json','w',encoding='utf-8') as f_out:
#         for line in f_in:
#             line=eval(line)
#             output_data['guid']=line['id_']
#             output_data['res']=line['res']
#             output_data['label']=guid_label[line['id_']]
# #             for key,val in output_data.items():
# #                 print(key)
# #             print(type(line))
#             out_line = json.dumps(output_data, ensure_ascii=False) + '\n'
#             if guid_label==1:
#                 for i in range(10):
#                     f_out.write(out_line)
#             else:
#                 f_out.write(out_line)
# #             break

In [90]:
c_paras_len=[]
c_paras_single_len=[]
for task1 in task1_list:
    c_paras=task1['c_paras']
    c_paras_len.append(len(c_paras))
    single_len=[]
    for para in c_paras:
        single_len.append(len(para.split(' ')))
    c_paras_single_len.append(single_len)


In [16]:
# task1_list[8]

In [ ]:
# for one in c_paras_single_len:
#     print(len(one))

In [102]:
a = np.array(c_paras_len)
print('code 的 10%', np.percentile(a, 10))
print('20 :', np.percentile(a, 20))
print('30 :', np.percentile(a, 30))
print('40 :', np.percentile(a, 40))
print('50 :', np.median(a))
print('60 :', np.percentile(a, 60))
print('70 :', np.percentile(a, 70))
print('80 :', np.percentile(a, 80))
print('90 :', np.percentile(a, 90))

code 的 10% 15.0
20 : 28.0
30 : 44.0
40 : 61.0
50 : 80.0
60 : 101.0
70 : 123.0
80 : 152.0
90 : 204.0


In [111]:
25000/(60*60)

6.944444444444445

In [97]:
val_count=data['len'].value_counts()

In [99]:
val_count.head()

9     2580
88    2568
28    2498
59    2001
14    1997
Name: len, dtype: int64

In [89]:
task1_list[25000-50]['guid'],task1_list[25000-2]['guid'],task1_list[25000-1]['guid'],task1_list[25000]['guid']

('9c87272_3713815078036e455a5e13970365f210d3fee886',
 '9c87272_6f5987f4998ba8bcac88321bccfb968e07ffd0f7',
 '9c87272_20b48d53b722d679b4202f6151def4236ce23865',
 'd2fc065_11b61085ef12101694cade14607e287b6d5f3e96')

In [80]:
with open('/home/hdj/BERT-PLI-IJCAI2020/examples/task1/case_para_sample.json','w',encoding='utf-8') as f_out:
    for task1 in task1_list:
        out_line = json.dumps(task1, ensure_ascii=False) + '\n'
        f_out.write(out_line)

In [ ]:
# public boolean isSubtype ( ObjectType type , ObjectType possibleSupertype ) throws ClassNotFoundException { if ( DEBUG_QUERIES ) { System . out . println ( "isSubtype: check " + type + " subtype of " + possibleSupertype ) ; } if ( type . equals ( possibleSupertype ) ) { if ( DEBUG_QUERIES ) { System . out . println ( "  ==> yes, types are same" ) ; } return true ; } ClassDescriptor typeClassDescriptor = DescriptorFactory . getClassDescriptor ( type ) ; ClassDescriptor possibleSuperclassClassDescriptor = DescriptorFactory . getClassDescriptor ( possibleSupertype ) ; return isSubtype ( typeClassDescriptor , possibleSuperclassClassDescriptor ) ; }
# public boolean isSubtype(ObjectType type, ObjectType possibleSupertype) throws ClassNotFoundException {
#         if (DEBUG_QUERIES) {
#             System.out.println("isSubtype: check " + type + " subtype of " + possibleSupertype);
#         }

#         if (type.equals(possibleSupertype)) {
#             if (DEBUG_QUERIES) {
#                 System.out.println("  ==> yes, types are same");
#             }
#             return true;
#         }
#         ClassDescriptor typeClassDescriptor = DescriptorFactory.getClassDescriptor(type);
#         ClassDescriptor possibleSuperclassClassDescriptor = DescriptorFactory.getClassDescriptor(possibleSupertype);

#         return isSubtype(typeClassDescriptor, possibleSuperclassClassDescriptor);
#     }

In [59]:
# {"guid": "005_001", "q_paras": ["Strickland, J. : This is an application for judicial review of two decisions of the Canadian Human Rights Commission (the Commission), both dated August 27, 2014, declining to deal with the Applicant's complaints, pursuant to s 41(1)(a) of the Canadian Human Rights Act , RSC 1985, c H-6 ( CHR Act ), because the Applicant had not exhausted grievance or review procedures otherwise reasonably available to him. The application for judicial review is brought pursuant to s 18.1 of the Federal Courts Act , RSC 1985, c F-7. Background", "The Applicant is a member of the Canadian Forces (CF), the Respondent herein as represented by the Attorney General of Canada. He alleges that in 2010, while he was serving in Haiti, his immediate superior officer discriminated against him, largely on racial grounds. In June 2010, the Applicant filed a complaint with the CF Ombudsman who decided not to deal with the case because other avenues of redress had not yet been exhausted.", "In August 2010 the Applicant met with his Commanding Officer (CO) and the harassment complaint was discussed. His CO subsequently wrote to him on two occasions in September 2010, requesting additional information so as to determine whether the Applicant's allegations constituted a harassment complaint pursuant to the Harassment Prevention and Resolution Guidelines . No response was received from the Applicant.", "By letter of October 5, 2010 counsel for the Applicant advised the CO, amongst other things, that the Applicant did not intend to avail himself of a harassment complaint pursuant to the Department of Nation Defence/CF Harassment Prevention and Resolution policy but reserved his right to make any such complaints in another forum.", "In December 2010 the Applicant filed a complaint with the Commission. By decisions dated July 6, 2011 the Commission decided not to deal with the complaint at that time, pursuant to s 41(1)(a) of the CHR Act , as the Applicant ought first to exhaust grievance or review procedures otherwise reasonably available to him. It stated that at the end of the grievance or review process, the Applicant could ask the Commission to reactivate the complaint. The Commission's decisions of July 6, 2011 are not under review.", "The Applicant then engaged in the CF Redress of Grievance process. On November 29, 2011 the Commander of Canadian Forces Joint Support Group released terms of reference, thereby convening an administrative investigation into the Applicant's allegations of racist conduct, discrimination and harassment. The Administrative Investigation report of the Initial Authority (IA) was released on April 20, 2012. The Applicant was dissatisfied with the IA decision and requested that his grievance be forwarded for determination by the Final Authority (FA).", "On July 4, 2012 the Applicant's grievance was referred to the Canadian Forces Grievance Board (CFGB) which released its findings and recommendations on September 14, 2012. By letter of March 4, 2013, the Chief of the Defence Staff advised that he concurred with the CFGB findings and recommendations, which included that there were important evidentiary omissions and procedural errors that compromised the integrity of the process and resulted in a fatally flawed Administrative Investigation and, therefore, an equally flawed IA decision. The Chief of the Defence Staff also stated that he was concerned that the Applicant had chosen not to avail himself of the CF harassment process and that this had contributed to the CFGB's findings. Given his finding that the IA decision was invalid, the Chief of the Defence Staff concluded that he could not make a properly informed decision on the validity of the allegations and, therefore, that it was imperative that the Applicant initiate the harassment investigation process. The Applicant was given 90 days to do so. The Chief of the Defence Staff stated that when the investigation was complete the Applicant could grieve its outcome if its conclusions and recommendations were not to his satisfaction.", "On May 14, 2013 the Applicant submitted a copy of his original grievance, not a harassment complaint. The Responsible Officer (RO) wrote to the Applicant on May 22, 2013, requesting submission of a proper complaint and inclusion of any information necessary to enable the conduct of a thorough and complete investigation of the allegations of harassment. The RO sent a second letter on July 19, 2013. The Applicant did not respond to either letter.", "On December 24, 2012, while the grievance process was in progress, the Applicant requested the Commission to reactivate his complaint. While the Commission was considering whether s 41(1)(a) applied to the complaint, the FA decision was issued. The Applicant filed an application for judicial review of the FA on April 24, 2012. A November 4, 2013 Section 40/41 Report recommended that the Commission not deal with the complaint while the judicial review was before this Court. On January 23, 2014, before the Commission decided that matter, the Applicant discontinued his application for judicial review of the FA and asked the Commission to deal with his complaint.", "On May 6, 2014 two Section 40/41 Reports were prepared. The first concerned the Applicant's complaint against the CF (file no 20101251) and the second concerned his complaint against his CO (file no 20101252) (collectively, the Section 40/41 Report). Substantially similar Records of Decision Under Section 40/41 were issued by the Commission on August 27, 2014, for both matters (collectively, the Decision). For the purposes of this judicial review, all references shall be to the Section 40/41 Report and decision of the Commission pertaining to the complaint against the CF.", "On September 26, 2014 the Applicant filed his application for judicial review of the Commission's Decision. Decision Under Review", "The Commission decided not to deal with the complaint pursuant to s 41(1)(a) of the CHR Act , as the Applicant ought to have exhausted grievance or review procedures otherwise reasonably available to him. A decision under s 41(1)(d) of the CHR Act was, therefore, unnecessary. The Commission adopted the conclusion of the May 6, 2014 Section 40/41 Report: The complainant's allegations are serious, and in the public interest. On the other hand, the harassment complaint process was reasonably available to the complainant after the Final Authority decision in 2013. The Final Authority decision included measures to be taken as part of the harassment complaint process in order to address the concerns with timeliness and fairness from the preceding administrative investigation. The complainant was provided multiple opportunities to participate in this harassment complaint process, but he chose not to. He was clearly aware of the inadequacies of the grievance form to initiate a harassment complaint as several attempts were made to obtain the correct information from him. Based on the above, the failure to exhaust that process was attributable to him.", "In rendering its decision the Commission reviewed the December 8, 2010 complaint form, the Section 40/41 Report of May 6, 2014 and Supplemental Section 40/41 Report of June 12, 2014, the Applicant's submissions of June 17, 2014, the CF's submissions of July 2, 2014, and cross-disclosure submissions of the CF dated July 25, 2014.", "The Section 40/41 Report set out the background to the complaint and summarized the positions of the parties based on their submissions. It noted that, based on the CF's position, it appeared that the remaining alternative redress process, the CF's harassment complaint process, was no longer available to the Applicant because he did not file a formal harassment complaint prior to the deadline set out in the FA. The question to be answered was whether the harassment complaint process was reasonably available to the Applicant and, if so, whether he should have exhausted that procedure. And, if that process ought to have been exhausted, whether the failure to do so was solely attributable to the Applicant in accordance with s 42(2) of the CHR Act .", "On the first point, it is expedient to reproduce particular paragraphs of the report as it sets out relevance background information as well as its analysis: Was the harassment complaint process reasonably available to the complainant? 64. Some relevant background information can be found in the \"Findings and Recommendations\" of the Canadian Forces Grievance Board (\"CFGB\"), dated September 14, 2012, which was provided by the complainant. In August 2011, after the Commission's decision not to deal with his complaint at that time, the complainant filed a grievance with the respondent. In March 2012, a final report on the Administrative investigation of the complainant's grievance was issued and disclosed to the grievor who provided comments. On April 20, 2012, the Initial Authority decision was rendered, finding \"professional shortcomings\" on the part of the superior officer but not granting the grievor's requests for apologies, damages, or legal fees. The complainant was unsatisfied with this decision and asked for a decision by the Final Authority. The matter was referred to the CFGB for review and recommendations. 65. The CFGB found that because a harassment investigation did not occur, the Initial Authority did not have adequate information upon which to make his decision, even though he attempted to insert elements of a harassment investigation into the grievance process. This investigation was found to have various defects, such as not all witnesses were interviewed, not all relevant information appeared to be considered, and the fact that the superior officer, alleged to be the harasser, was not provided an opportunity to respond to the investigation. For these reasons, the CFGB recommended that the Final Authority not make a final decision on the matter, but order a new harassment investigation be initiated. It also noted that the respondent's policies should be amended to ensure that harassment complaints are required to be dealt with under the harassment policy prior to resorting to the grievance process, given that neither the CFGB nor the CDS is equipped to conduct its own investigation in such situations. 66. On March 4, 2013, the Final Authority rendered his decision. Referring to the CFGB findings and recommendations, the CDS found that there were \" important evidentiary omissions and procedural errors that compromised the integrity of the process and resulted in what the CFGB quite rightly referred to as a 'fatally flawed' administrative investigation and consequently led to an equally flawed IA decision based solely on that investigation.\" The CDS determined that due to these errors and the incompleteness of the underlying investigation, he could not render \" ...a properly informed decision on the validity and reliability of the allegations... \" 67. The CDS also raised concerns that a harassment investigation did not occur. In the Final Authority decision, the CDS stated: Yet, I am troubled by your allegations and most particularly, by the lack of a proper investigation into their validity. As I mentioned, the CF takes this issue very seriously and consequently, it is imperative that you initiate the harassment investigation process by submitting a formal harassment complaint to the CO of 4 CFMCU. You have 90 days from the receipt of this letter to make your submission. The CO of 4 CFMCU shall, upon receipt of your harassment complaint, initiate a harassment investigation into the allegations therein. Let me be very clear on this point: an investigation will not commence until there is a formal harassment complaint submitted to the CO of 4 CFMCU and you commit, in writing, that you will fully participate in such an investigation to ensure that a thorough and impartial analysis may determine the legitimacy of your allegations. If you do not respond within 90 days, there will be no further action taken on your alleged complaints. Given the complexities of this case, compounded by the length of time that has elapsed since the alleged incidents, the CO of the 4 CFMCU might consider engaging a private consulting firm to assist with the investigation. Such corporations specialize in the investigation of harassment cases. Additionally, a monthly situation report will be sent to the Director General Canadian forces [ sic ] Grievance Authority (DGCFGA) Implementation Officer on the status of the forthcoming harassment investigation. When the investigation has been completed, you may grieve its outcome if the conclusions and recommendations are not to your satisfaction. 68. The CDS suggested that a private consulting firm be engaged to investigate the matter. The complainant is of the view that this demonstrates that the respondent is unable to investigate a complaint of this complexity. He suggests that this is further supported by the finding of the CFGB that the initial administrative investigation to be [ sic ] ' fatally flawed '. 69. The lack of procedural fairness in the IA decision was acknowledged in the Final Authority decision. The CDS attempted to address the concerns for procedural fairness and expediency with his recommendations: a) that the matter be dealt with through a formal harassment complaint; and, b) that they hire an outside firm to investigate the matter. 70. The respondent's \"Harassment Prevention and Resolution Guidelines\" (the Guidelines) outline a complaint process which is overseen by Responsible Officers (ROs) in the respondent's organization. The Guidelines define harassment the same as it is defined under the Act. The Guidelines further provide that other workplace harassment may also be addressed through this process. Once a formal harassment complaint is received, the RO oversees a situational assessment to determine whether or not the complaint is related to harassment - if it is, efforts are made to resolve the matter, identify other possible redress avenues such as mediation, and the appropriate action(s) will be initiated. If mediation is not appropriate, an administrative investigation is to be undertaken by a harassment investigator. The harassment investigator prepares a draft report on which both parties may comment before the final report is completed and submitted to the RO for decision. If any person is not in agreement with the RO's decision, they may file a grievance. Although the harassment and grievance processes do not provide for an independent third party decision-maker, matters dealing with harassment and racist conduct are referred to an independent body (the CFGB, now the MGERC) for findings and recommendation prior to the Final Authority decision being rendered. In addition, a review by the Federal Court is also available. 71. The complainant states that only the Commission will be able to fully deal with all of the matters in his complaint. While the complaint deals with harassment, there are also allegations of adverse differential treatment within the workplace. If the harassment complaint process were still available to him, it is not clear whether it could deal with the allegations with respect to the transfer occurring as a result of his marital status, for example. However, it could have dealt with much [ sic ] of the substantive allegations in the complaint. 72. Timeliness is another consideration with respect to this complaint, which is nearly four years old. It appears that both parties bear some responsibility for the delays in the process. In 2010, the complainant did attempt to speak to his superiors about his allegations, but he did not provide them with the requested information when asked in September 2010. As outlined in paragraph 64, the respondent's process is lengthy, and there appears [ sic ] to have been delays in the processing of the complainant's grievance. 73. In terms of delay, it is not clear that the Commission's process would be more expedient than that of the respondent's internal harassment complaint process, if it were still available. Nonetheless, it appears at this stage, the Commission's process is the only remaining process available to him. 74. The complainant's human rights allegations, if proven, are serious; this is acknowledged by the respondent. The complainant has not provided any information to indicate that he is vulnerable personally, but there is a public interest in investigating allegations of racism in Canadian government institutions such as the Canadian Forces. Although the complainant describes the complaint as one of systemic discrimination, no policy or practice has been identified in the summary of complaint. There is no indication that there is or was any potential for harm to anyone if the respondent's harassment complaint process had been used. 75. The complainant suggests that that [ sic ] requiring him to engage in the harassment complaint process is unfair. Although the complainant's scepticism may be understandable given the results of the IA decision, there is no indication that the respondent's alternate redress procedures overall are so flawed that it could not have dealt with the complainant's allegations within its harassment complaint process. In this instance, the Final Authority made recommendations in order to specifically address the issues that occurred previously, including any potential unfairness and the issue of delay. 76. Having regard for all of the above, it appears that the complainant had another review procedure, the harassment complaint process, reasonably available to him after the Final Authority decision in 2013.", "On the question of whether the failure to exhaust the CF's harassment complaint process was attributable to the Applicant and not another, as set out in s 42(2) of the CHR Act , the Section 40/41 Report noted that the history of the complaint illustrated that much of the discord related to the appropriate process for addressing a complaint that raises a variety of issues such as was the case in this matter, which involved allegations of harassment, abuse of authority and adverse differential treatment.", "Ultimately, however, it concluded that: 80. The complainant acknowledged the internal harassment complaint process. After the Final Authority decision, the complainant sent in his grievance form in lieu of a harassment complaint. In his letter to the complainant dated May 22, 2013, the RO responded to the complainant to explain that the grievance form did not provide the information necessary to initiate a harassment complaint. The letter described what was required in order to file a harassment complaint and also offered assistance to the complainant. On July 19, 2013, the RO sent a follow-up letter to the complainant requesting additional information, but the complainant did not provide it. Therefore, while he acknowledged this process, he refused to participate by not providing the appropriate material in order for it to have any possibility of success. This is solely attributable to the complainant. Relevant Legislation", "The sole issue in this application for judicial review is whether the Commission's interpretation and application of s 41(1)(a) were reasonable.", "Jurisprudence has previously held that the appropriate standard of review with respect to decisions of the Commission not to deal with a complaint pursuant to s 41(1) of the CHR Act is reasonableness ( FRAGMENT_SUPPRESSED).", "Reasonableness is concerned with the existence of justification, transparency and intelligibility within the decision-making process. It is also concerned with whether the decision falls within a range of possible, acceptable outcomes which are defensible in respect of the facts and the law ( FRAGMENT_SUPPRESSED). Preliminary Issue", "A preliminary issue that has been raised by the Respondent is the admissibility of the affidavit of Nathalie Bui sworn October 24, 2014 (the Bui Affidavit). It attaches what the affiant describes as the entire record of official correspondence between the Commission and the Applicant concerning files 20101251 and 20101252.", "As noted by the Respondent, this is the Applicant's second attempt to place this material before the Court. The Applicant previously brought a motion, pursuant to Rule 317 of the Federal Courts Rules , SOR/98-106 [ FC Rules ], seeking to have the Commission's entire file produced as part of the Certified Tribunal Record (CTR).", "By Order dated November 26, 2014, Prothonotary Tabib refused that request on the basis that the Applicant was not entitled to further production, noting, in particular, that the Applicant had not identified any document that might have been considered by the Commission, or might be relevant to the determining of the issues before the Court, and which had not been included in the CTR.", "Therefore, in my view, this Court has already ruled on this issue. The conduct of this judicial review on the merits of the Applicant's claim does not serve as an appeal of the Prothonotary's decision. An appeal of a prothonotary's decision must be brought by motion to the Federal Court ( FC Rules , R 51(1), the Applicant did not bring such a motion and the time within which he was required to do so has elapsed. On that basis alone the Bui Affidavit is inadmissible and submissions made in reliance on it or in reference to it are to be disregarded.", "In any event, this Court has also previously held that material that was not before the decision-maker should generally be excluded for purposes of judicial review ( FRAGMENT_SUPPRESSED). And in this case, the Bui Affidavit does not fall under any of the recognized exceptions to this rule ( FRAGMENT_SUPPRESSED).", "The Commission listed the documentation that was reviewed when making its decision, which was contained in the CTR. Accordingly, the additional material contained in the Bui Affidavit is not relevant to the issue before this Court, being whether the Commission's Decision was reasonable based on the record that was before it.", "Further, the May 6, 2014 Section 40/41 Report specifically acknowledges that the parties had raised facts in their submissions that had occurred prior to the original Section 40/41 Report of July 6, 2011. The May 6, 2014 Section 40/41 Report stated that, because the Commission had already dealt with the alternative redress procedures available to the Applicant prior to July 2011, its current analysis would be based only on information arising after the Commission's original decision (para 61). As seen from the analysis contained in the May 6, 2014 Section 40/41 Report, prior facts which were set out in the parties' submissions do not constitute a part of the analysis.", "For all of these reasons, it is my view that the Bui Affidavit is inadmissible. Accordingly, the Applicant's submissions made in reliance on or in reference to that affidavit have not been considered in this judicial review. Position of the Parties", "The Applicant's position is that he has spent years attempting to satisfy the CF grievance system and acted in good faith including through a CF led biased and fatally flawed investigation and ensuing administrative investigation report. He characterises as cyclical, absurd and unreasonable the suggestion that to satisfy all reasonable steps he should now engage the harassment procedure and, if unsatisfied, pursue a new grievance, potentially all the way to judicial review. That process would create an endless procedural loop that would prevent the Applicant from exercising his right to complain under the CHR Act . Accordingly, the Commission unreasonably concluded that the CF's internal process was reasonably available to him.", "The Applicant further submits that the Commission ought to have accepted his complaint. The CF grievance process was exhausted because the Chief of the Defence Staff failed to make a decision on the grievance and instead passed it off, requiring the harassment procedures to be initiated. Further, the CF has demonstrated an unwillingness and an inability to handle this complex matter.", "The Respondent submits that a review of the reasonableness of the Commission's Decision should include an examination of some or all of the relevant factors ( FRAGMENT_SUPPRESSED), including any delay attributable to the Applicant. It should not include the Applicant's subjective and unsubstantiated view that the harassment process is not reasonably available and inadequate because the Applicant has never engaged the process.", "The Respondent further submits that the Commission's Decision that the Applicant ought to have used the appropriate CF internal process, which was reasonably available, falls within a range of possible acceptable outcomes. Any circularity in the process, as alleged by the Applicant, is purely attributable to his own refusal to utilize the process that the CF, the FA and the Commission all found to be the appropriate avenue for redress. Analysis", "In this matter the Commission adopted the recommendations made in the Section 40/41 Report, which, in that circumstance, constitute the reasons of the Commission ( FRAGMENT_SUPPRESSED). The Applicant takes no issue with the Commission's form of response.", "The Section 40/41 Report stated that s 41(1)(a) and s 42 together mean that the Commission can decide not to deal with a complaint under s 41(1)(a) if it finds that the complainant chose not to finish another process that was reasonably available to him or her. This is not an unreasonable interpretation of these provisions. In FRAGMENT_SUPPRESSED", "The Section 40/41 Report then listed factors that may be considered when deciding under s 41(1)(a) whether or not a complainant should keep using the other complaint or grievance process. These were: why the parties did not finish the other process; how much longer that process was likely to take; whether there is new information in that regard; and whether there is anything other than the amount of time the other process may take, such as vulnerability arising from the complainant's current situation or a risk of harm to any participant, that makes it not \"reasonably available\" to the complainant such that the Commission should deal with the complaint. The Section 40/41 Report also summarized the CF's submissions of February 20, 2014, and the Applicant's submissions of February 21, 2014 and April 10, 2013.", "The question of whether the harassment complaint process was reasonably available to the Applicant is largely a factual question. In my view, there is no question that it was available. The only question being was it reasonably so.", "In July 2011 the Commission decided not to deal with the complaint at that time under s 41(1)(a); instead, it asked the Applicant to use another complaint or grievance process first. At the end of that process the complainant could come back to the Commission and ask it to reactivate the complaint.", "Given this, the Applicant then filed a grievance pursuant to s 29 of the National Defence Act , RSC 1985, c N-5. The process thus engaged is set out in the Queen's Regulations and Orders for the Canadian Forces (QROCF) (online:  ). This envisions consideration and determination of the grievance by the IA (s 7.15). If the complainant is not satisfied with the IA decision, he or she may request that the matter be referred to the FA (s 7.18). The FA for all grievances is the Chief of the Defence Staff ( National Defence Act , s 29) or his delegate (QROCF, s 7.17). Pursuant to s 29.12 of the National Defence Act, the Chief of the Defence Staff shall refer every grievance that is of a type prescribed by regulation to the Grievances Committee for its findings and recommendations before the Chief of the Defence Staff considers and determines the grievance. These types of grievances are set out in s 7.21 of the QROCF. They include any decision of the Chief of the Defence Staff in respect of a particular officer or non-commissioned officer.", "In March 2012 the IA decision was issued. As the Applicant was unsatisfied with that decision, in May 2012 he sought an FA decision. As seen from the March 4, 2013 letter from the Chief of the Defence Staff, the grievance was submitted to the CFGB which conducted an independent review of the grievance and provided findings and recommendations which were disclosed to the Applicant.", "The Chief of the Defence Staff stated that the CFGB had analysed each of the contentions in the grievance file and found that the administrative investigation on which the IA had based its decision was \"fatally flawed\" on several levels.", "He also stated: The CF's policies on racist conduct and on harassment prevention and resolution are outlined in Canadian Forces Administrative Order 19-43 (Racist Conduct) and Defence Administrative Order and Directive (DAOD) 5012-0 (Harassment Prevention and Resolution). Both are unequivocal in their condemnation of any conduct that causes offence or harm to any person through acts, comments, or displays that demean, belittle, and cause personal humiliation or embarrassment, and any act of intimidation or threat. As much as we in the CF would like to think that we are immune from such behaviours, as a microcosm of the society that we serve, we would be very naïve to think that we, as an organization, would not be subject to instances of this insidious conduct. Accordingly, the CF has a comprehensive framework to deal with such instances in the form of the Harassment Prevention and Resolution Guidelines . The CF policy and guidelines flow directly from and are consistent with the Treasury Board's Policy on Harassment Prevention and Resolution in the Workplace and go beyond the requirements of the Canadian Human Rights Act in their scope.", "The Chief of the Defence Staff expressed concern that the Applicant had chosen not to avail himself of the CF harassment process. His lack of cooperation by failing to fulfil the obligation to provide full written details of his complaint was an impediment to the fair, impartial and expedient harassment investigation and contributed to the \"procedural morass\" that followed. The Chief of the Defence Staff went on to say that there had been important evidentiary omissions and procedural errors that compromised the integrity of the administrative investigation process resulting in what the CFGB had rightly referred to as a fatally flawed administrative investigation; consequently, the IA decision that was based on that investigation was equally flawed.", "Although the Chief of the Defence Staff had identified his role as being to determine whether the harassment occurred and whether the Applicant was a victim of mistreatment at the hands of a superior officer, he concluded that in light of the CFGB findings, he could not render a properly informed decision. He therefore decided to order a new harassment investigation.", "The Chief of the Defence Staff's reference to a lack of clarity as to the order in which the CF harassment and grievance processes are to be utilized is of note. He stated that the CFGB had highlighted that there was lack of clear policy direction regarding the relationship between the harassment and grievance processes. DAOD 2017-1 states: The following are situations in which other complaint and mechanisms should be used prior to proceeding with a grievance: • a complaint of harassment or abuse of authority", "While s 4.10 (Coincidental Complaints and Grievances) of the Harassment Prevention and Resolution Guidelines states: If an individual decides to file a grievance on the same issue as a harassment complaint, the applicable grievance mechanism will apply and the harassment complaint will be closed.", "The Chief of the Defence Staff stated that determination of misconduct, as it pertains to harassment or acts of racism, must be ascertained through a procedurally fair and impartial investigation process, such as that outlined in the Harassment Prevention and Resolution Guidelines . The grievance process should be engaged only if the complainant feels they have been wronged as a result of the outcome of the investigation process or if there is an excessive and unjustifiable delay in handling the complaint.", "The Chief of Military Personnel (CMP), in consultation with the Assistant Deputy Minister Human Resources - Civilian, \"will harmonize the Harassment Prevention and Resolution Guidelines with DAOD 2017-1 so that it is very clear that harassment complaints or grievances containing allegations of harassment must be dealt with first under the harassment policy and only after a proper harassment investigation has been completed\".", "The Chief of the Defence Staff decided that:", "am not prepared to grant the redress that you seek. Yet, I am troubled by your allegations and most particularly, by the lack of a proper investigation into their validity. As I mentioned, the CF takes this issue very seriously and consequently, it is imperative that you initiate the harassment investigation process by submitting a formal harassment complaint to the CO of 4 CFMCU. You have 90 days from the receipt of this letter to make your submission. The CO of 4 CFMCU shall, upon receipt of your harassment complaint, initiate a harassment investigation into the allegations therein. Let me be very clear on this point: an investigation will not commence until there is a formal harassment complaint submitted to the CO of 4 CFMCU and you commit, in writing, that you will fully participate in such an investigation to ensure that a thorough and impartial analysis may determine the legitimacy of your allegations. If you do not respond within 90 days, there will be no further action taken on your alleged complaints. Given the complexities of this case, compounded by the length of time that has elapsed since the alleged incidents, the CO of 4 CFMCU might consider engaging a private consulting firm to assist with the investigation ... When the investigation has been completed, you may grieve its outcome if the conclusions and recommendations are not to your satisfaction.", "In my view, regardless of the factual background prior to the Chief of the Defence Staff's decision and regardless of the lack of clarity as to the order in which harassment complaints or grievances containing allegations of harassment were to be dealt with and any delay or confusion that this may have previously caused, as of March 13, 2013, the Applicant was on clear notice of what was required of him, and that was that he initiate a harassment complaint within 90 days. He was also aware that if he failed to do so, there would be no further action taken with respect to the allegations.", "The CF's submission, as summarized by the Section 40/41 Report, stated that on May 14, 2013 it received from the Applicant a photocopy of his original grievance, not a formal harassment complaint as required by the Chief of the Defence Staff. On May 22, 2013, the RO sent the Applicant a letter requesting that he redraft his submission, explain each allegation specifically and provide any information that would enable the harassment investigation to be thorough and complete. The RO also notified the Applicant's current CO in order to ensure that an assistant could be appointed for the Applicant to help him with the process. The Applicant did not respond to the RO's request. The RO sent another letter to the Applicant on July 19, 2013 requesting an update on the preparation of this harassment complaint but again did not receive a response.", "The Section 40/41 Report noted the other factors that were considered in reaching its recommendation, including the attempt of the Chief of the Defence Staff to address the procedural fairness and other concerns by having the matter dealt with by a formal harassment complaint, with an outside firm being hired to investigate. Further, as to timeliness, that both parties bore some responsibility for the prior delays in the process and that it was not clear that the Commission's process would be more expedient than the CF's harassment policy, if it were still available to the Applicant. However, at this stage, the Commission's process was the only one still available to the Applicant. Further, that the Applicant had provided no information to indicate that he was personally vulnerable.", "The Applicant's position is that the harassment complaint process as proposed by the Chief of the Defence Staff cannot be considered to be reasonably available. The Applicant submits that there has already been a considerable delay, that he commenced the grievance process and that, at the end of that process, rather than rendering a decision, the Chief of the Defence Staff instead attempted to effect a harassment investigation. This is \"cyclical\" because he was required to commence the grievance process, which now requires a harassment investigation, which in turn can be grieved, and that this has the potential of becoming an endless loop.", "In my view, this argument cannot succeed. Although the CFGB's report was not in the CTR, it is clear from the Chief of the Defence Staff's letter that there was a lack of clarity regarding the relationship between the harassment and grievance processes. This may well have contributed to the prior delay and procedural missteps in this matter. And, unless the relationship is clarified, it may have the same impact on other matters in the future.", "Regardless, in this case, the decision by the Chief of the Defence Staff had the effect of resetting the clock. While it is true that a grievance from the conclusions and recommendations of the harassment investigation would have been available to the Applicant, this did not mean that an endless procedural circle would follow. The problem identified in the original grievance process initiated by the Applicant was that there was insufficient information to deal with the harassment complaint. This led to the Chief of the Defence Staff's decision that a harassment investigation was required. Had that been carried out, any further grievance process then open to the Applicant would have been based on the findings of the harassment investigation, not the absence of one, and would not have resulted in a decision that a harassment investigation was required. Thus, this does not result in an endless cycle, nor does it establish that the process proposed by the Chief of the Defence Staff was not \"reasonably available\" to the Applicant.", "Further, the original grievance process would have been exhausted if the Applicant had participated in the proposed harassment investigation. The Applicant does not submit that it was beyond the authority of the Chief of the Defence Staff to proceed as he did, by requiring the harassment investigation. In addition, he discontinued his judicial review of the FA.", "also do not agree with the Applicant's submission that the Chief of the Defence Staff admitted that the CF is unable or unwilling to fully and objectively determine a complaint of racial discrimination when he stated the CO \"might consider engaging a private consulting firm to assist the investigation\" in his letter given the complexity of the case, compounded by the length of time that had elapsed since the alleged incidents. A suggestion that an independent third party with experience in the investigation of harassment complaints could be utilized, if anything, would seem to suggest the incorporation of an additional measure to ensure procedural fairness in the process.", "The Applicant also submits that the Chief of the Defence Staff's statement quoted at paragraph 42 above is an acknowledgment that racism exists within the CF, at least to some degree, and that his inaction to combat racism may mean that it will only continue to exist. However, read in whole, the statement clearly expresses that the CF Harassment Prevention Resolution Guidelines are intended to deal with any instance of racism and harassment.", "As to systemic discrimination, the Section 40/41 Report stated that although the Applicant described the complaint as one of systemic discrimination, no policy or practice had been identified in the summary of complaint. A review of the complaint confirms that the complaint clearly pertained to the Applicant's CO and made no allegation of systemic discrimination. At the hearing before me, the Applicant confirmed that this was the case and that systemic discrimination was therefore not pursued as an issue in this matter.", "In summary, the Commission considered the factual basis of this matter and found that there was a review procedure that was reasonably available to the Applicant and that had not been exhausted by the Applicant prior to the expiry of the 90 day deadline set by the Chief of the Defence Staff. Based on the record, this finding was reasonably open to it.", "The Commission also recognised that this finding would leave the Applicant without recourse. However, as noted by the Respondent, this Court has held that the reasonableness of a decision is not affected by the absence of the \"safety net\" of renewed access to the Commission ( FRAGMENT_SUPPRESSED). In this case, while the CF review process itself is no longer available to the Applicant, nor is there a safety net, the Commission recognized this outcome when making its decision.", "In the circumstance of this matter, the Commission's finding that the Applicant was aware of, but refused to participate in, the CF's internal harassment complaint process and that the failure to exhaust the procedure was solely attributable to the Applicant is to be afforded deference ( FRAGMENT_SUPPRESSED) and also fell within a range of possible acceptable outcomes defensible in respect of the facts and law ( FRAGMENT_SUPPRESSED).", "For these reasons the application is dismissed. The parties have agreed to costs in the amount of $2,500.00, accordingly, the Respondent shall have its costs in that amount. JUDGMENT", "THIS COURT'S JUDGMENT is that 1. The application for judicial review is dismissed. 2. The Respondent shall have its costs in the amount of $2,500.00. Application dismissed. Editor: Jana A. Andersen/nmg [End of document]"], "c_paras": ["Russell, J. : This is an application under s. 18.1 of the Federal Courts Act , RSC 1985, c F-7 for judicial review of a decision of the Canadian Human Rights Commission [Commission], dated May 7, 2014 [Decision], which decided not to deal with the Applicant's complaint pursuant to s. 41(1)(d) of the Canadian Human Rights Act , RSC 1985, c H-6 [Act].", "The Applicant started working as a Heavy Equipment Operator for Canadian National Railway Company [CN] in August 1981. He was a member of a bargaining unit represented by the National Automobile, Aerospace, Transportation and General Workers Union of Canada (CAW-Canada) [ Union].", "On December 19, 2012, the Applicant's employment was terminated because he refused to attend a medical assessment to determine his fitness for work. CN requested the medical assessment because the Applicant's position was a safety sensitive position and there were concerns regarding his behaviour. The Applicant says that he refused to attend the medical assessment because he was receiving treatment for drug dependency and believed that was sufficient to address CN's concerns.", "On January 8, 2013, the Union filed a grievance to contest the Applicant's termination.", "On February 14, 2013, the Union closed the Applicant's file. The Union said that the Applicant had not responded to their requests for information and it \"was not in a position to advance the matter with the limited information at hand.\"", "In March 2013, the Applicant submitted a complaint to the Commission. He alleged that CN had discriminated against him on the ground of disability by terminating his employment contrary to s. 7 of the Act. The Commission decided not to deal with the complaint pursuant to s. 41(1)(a) because the Applicant had not exhausted the Respondent's grievance process.", "On April 19, 2013, CN denied the Union's grievance. The Union did not refer the grievance to arbitration.", "On October 1, 2013, the Applicant submitted another complaint to the Commission. He alleged that, again, CN had discriminated against him on the ground of disability by terminating his employment contrary to s. 7 of the Act.", "On October 29, 2013, the Applicant was advised that the Commission would be preparing a s. 40/41 report to determine whether it should deal with his complaint. The Applicant was invited to prepare a letter stating his position on whether the Commission should not deal with the issues because \"the human rights issues in this complaint may have already been dealt with through another process.\" Counsel for the Applicant made submissions to the Commission both in advance of the preparation of the report and after being provided a copy of the s. 40/41 report [Report].", "On May 7, 2014, the Commission decided not to deal with the Applicant's complaint pursuant to s. 41(1)(d) of the Act. The Commission adopted the Report's conclusions and decided that the complaint was vexatious under s. 41(1)(d) of the Act (Applicant's Record at 48): The complainant's human rights allegations have been addressed by an alternate decision maker with authority to consider human rights issues. The allegations raised in the complaint before the Commission are the same as those addressed in the final level grievance response. Given that the alternate decision-maker dealt with the human rights issues raised in this complaint, and that process was fair, the Commission must respect the finality of that decision and should not deal with this complaint. It is therefore plain and obvious that this complaint is vexatious within the meaning of section 41(1)(d) of the Act.", "The Applicant raises the following issues in this application: 1. Whether the Commission unreasonably refused to exercise its jurisdiction; 2. Whether the Commission erred in law by: a) Unreasonably finding the Applicant's complaint to be vexatious; or, b) Having found the complaint to be vexatious, unreasonably ignoring that justice required it to deal with the complaint anyway; and, 3. Whether the Commission unreasonably based its decision on erroneous findings of fact made without regard to the material before it.", "The Supreme Court of Canada in Dunsmuir v New Brunswick , 2008 SCC 9 [ Dunsmuir ] held that a standard of review analysis need not be conducted in every instance. Instead, where the standard of review applicable to a particular question before the court is settled in a satisfactory manner by past jurisprudence, the reviewing court may adopt that standard of review. Only where this search proves fruitless, or where the relevant precedents appear to be inconsistent with new developments in the common law principles of judicial review, must the reviewing court undertake a consideration of the four factors comprising the standard of review analysis: Agraira v Canada (Public Safety and Emergency Preparedness) , 2013 SCC 36 at para 48.", "The Applicant submits that decisions under s. 41(1)(d) of the Human Rights Act are reviewed on a standard of reasonableness: Chan v Canada (Attorney General) , 2010 FC 1232 [ Chan ]. The Respondent submits that the Commission's decision not to deal with a complaint under s. 41 of the Human Rights Act is a discretionary decision reviewable on a standard of reasonableness: Exeter v Canada (Attorney General) , 2011 FC 86 at para 19, aff'd 2012 FCA 119 at para 6 [ Exeter ]; Morin v Canada (Attorney General) , 2007 FC 1355 at para 25, aff'd 2008 FCA 269.", "All of the issues question the reasonableness of the Commission's decision to not deal with the complaint. The Court agrees that these decisions are reviewable on a standard of reasonableness: Chan , above, at para 15; Exeter , above, at para 6.", "When reviewing a decision on the standard of reasonableness, the analysis will be concerned with \"the existence of justification, transparency and intelligibility within the decision-making process [and also with] whether the decision falls within a range of possible, acceptable outcomes which are defensible in respect of the facts and law\": see Dunsmuir , above, at para 47; Canada (Citizenship and Immigration) v Khosa , 2009 SCC 12 at para 59. Put another way, the Court should intervene only if the Decision was unreasonable in the sense that it falls outside the \"range of possible, acceptable outcomes which are defensible in respect of the facts and law.\"", "A. Applicant", "The Applicant submits that the Commission unreasonably refused to exercise its jurisdiction. The Applicant concedes that the Commission is entitled to adopt the Report for its reasons: Chan , above, at paras 39-40. However, the Applicant distinguishes the present proceeding from the Chan case on two grounds. First, the Commission's adoption of the Report was inadequate because it fails to show that the Commission considered the submissions before it and fails to recognize that the human rights issues were not considered in the grievance process: Vancouver International Airport Authority v Public Service Alliance of Canada , 2010 FCA 158. Second, the internal grievance process does not constitute a proper decision-maker. The grievance process is not an independent arbitrator and it failed to provide reasons for its decision on the human rights issues.", "The Applicant characterizes the grievance process as an internal negotiation between the Union and CN. If the Commission does not deal with the complaint then he says the Union's Decision to not refer the grievance to arbitration will have denied him the ability to have his human rights issue considered by a decision-maker. The Union's Decision to not proceed to arbitration was based, in part, on the Applicant's refusal to cooperate but the Applicant says that the nature of his disability carries the need for reasonable flexibility regarding deadlines and expectations. The Union's Decision was also based on other factors including time, money and resources.", "In the alternative, if the internal grievance process constituted a decision-maker, the Decision is unreasonable because the grievance did not address the human rights issues. It referenced \"drug dependency\" and concluded there was insufficient evidence.", "If the complaint was correctly deemed vexatious, then the Applicant submits that the Commission erred in law by ignoring that justice required the Commission to deal with the complaint anyway. The Decision says the internal grievance process was fair but fails to consider the Applicant's reply submissions.", "Finally, the Decision is unreasonable because it relies on the erroneous finding that the Applicant's human rights issues were already addressed by a decision-maker. B. Respondent", "The Respondent submits that it was reasonable for the Commission to refuse to deal with the complaint. The Report constitutes the reasons for the Decision: Canada (Attorney General) v Sketchley , 2005 FCA 404 at para 37 [ Sketchley ]; Bergeron v Canada (Attorney General) , 2013 FC 301 at paras 28-29 [ Bergeron ]. The Applicant had the opportunity to address the human rights issues through the Union but he failed to cooperate with the search for accommodation. The Commission may refuse to deal with a complaint if it is obvious that the complaint cannot succeed. A complainant who refuses to collaborate in the search for accommodation will have his or her complaint dismissed: Central Okanogan School District No 23 v Renaud , [1992] 2 SCR 970.", "The Commission's Decision to refuse to deal with the complaint is also in accordance with Supreme Court of Canada jurisprudence regarding the importance of permitting administrative tribunals to curb abuse of process: British Columbia (Workers' Compensation Board) v Figliola , 2011 SCC 52. It would be an abuse of process to advance a human rights complaint where the complainant has failed to cooperate with their union to have the same human rights issues addressed.", "Contrary to the Applicant's submissions, s. 41(1)(d) does not require that a decision be made by an arbitrator. The Commission is granted great latitude in exercising its discretion and assessing the appropriate factors in performing its screening function: Sketchley , above, at para 38; Bergeron , above, at para 39. Further, the Federal Court has held that s. 41(1)(d) may apply in situations where a union has decided not to pursue a grievance to arbitration: Bergeron , above, at para 38. There is also no evidence that those who decided the Applicant's grievances were not impartial: Bergeron , above, at para 43.", "The Report shows that the Investigator turned her mind to the outcome of the grievance process, the Applicant's allegations relating to substance abuse, and the question of reasonable accommodation. The Commission reasonably concluded that the allegations raised in the complaint had already been addressed in the grievance process and that the grievance process was fair.", "The Applicant raises three (3) grounds for reviewable error but, in the end, they all come back to the issue of the Applicant's own failure to cooperate in the grievance process. Essentially, the Commission came to the conclusion that the Applicant's complaint was vexatious under s. 41(1)(d) of the Act because the Applicant's human rights allegations had already been addressed by the grievance process.", "As the Report found, the Applicant's Union representative filed a grievance on his behalf that raised the same human rights issues as those in the complaint to the Commission. The Union had to close out its grievance file because the Applicant would not cooperate with its attempts at obtaining accommodation for him. The Union concluded that it could not advance the grievance to arbitration because, given Applicant's failure to cooperate in providing the information requested and required for the grievance process, there was insufficient information to advance the matter. In the end, the grievance process was exhausted without going to arbitration because the Applicant failed to cooperate. This was the final decision in the grievance process.", "The Applicant attempted to convince the Commission, and he has attempted to convince this Court, that his disability prevented him from providing the materials and cooperation required by the grievance process. In his submissions to the Commission, he alleged as follows (CTR at 14): Given the nature of [the Applicant's] disability, it follows that it would be logical for the Company to have been in closer contact with the Union in order to determine what the correct situation, and prognosis, for [the Applicant] was. It is understandable that an individual with a disability would encounter difficulty in navigating deadlines without reasonable assistance, and it was further understandable that [the Applicant] mistakenly believed the matter was being dealt with by his Union and his doctor.", "There was no evidence before the Commission, and there is none before me, to support this bare allegation that the Applicant had difficulties with deadlines and mistaken beliefs because of his disability. The Applicant simply expected the Commission, and now asks the Court, to draw an inference to this effect from the nature of his disability which is drug dependency. It is noticeable that, in the affidavit he has filed with this application, the Applicant says nothing about difficulties with deadlines and mistaken beliefs. Further, his evidence before me clearly indicates the considerable lengths to which the Union went to make clear to the Applicant what was required of him and to encourage him to comply. The letter of April 4, 2013 to the Applicant from Mr. Robert Fitzgerald, the Union's National Representative, sets out the whole picture: To date, none of this information has been provided. The Union only has two pieces of medical documentation. One dated January 24, 2013 stating that you will be seeing an addiction counsellor, but no confirmation that you did. The second one verified that you do not have any disability as it relates to psychiatric issues. Although your doctor invited us to follow up with him providing we had the necessary medical release to do so, you failed to return the release form that the Regional Representative provided to you, enclosed with his letter of February 01, 2013. There have been literally hundreds of phone calls between you and the Union at different levels. However, you have not acknowledged the Union's request for information. You have abated the Union's request in must the same way you have declined to cooperate with the Company. In our opinion, the negative connotation of your actions would not be lost on an Arbitrator. At some point you did advise the Company that you had an addiction problem and that you were seeking help for such. However, there is no evidence that you have been diagnosed with such an addiction nor is there any evidence to show that you are being treated for such. As we said earlier, there is only two pieces of medical documentation on file and neither provide a diagnoses or address treatment. If in fact there was a clinical diagnosis of addiction, treatment and rehabilitation, the Company may well have been obligated to provide accommodation. However, with such an obligation, there also comes an onus on the employees to cooperate with the efforts to accommodate. It was put this way by the arbitrator in CROADR case 3354: The Arbitrator must agree. As confirmed by the Supreme Court of Canada in Central Okanogan School District No. 23 v. Renaud,", "2 S.C.R. 970, the obligation of accommodation involves the cooperative participation of the employer, the trade union and the employee . That was reflected in an award of this Office in CROA 3173 : The Arbitrator is satisfied that the approach adopted by the Company is in keeping with its obligations under the Canadian Human Rights Act . It now seems well-established that when an employee seeks accommodation by reason of a status that is protected under the Canadian Human Rights Act, it is incumbent upon the employee concerned to contribute positively to the process , and to accept an offer of reasonable accommodation, even though it might not be the specific accommodation which the employee would prefer. That is reflected, in part, in the decision of the Supreme Court of Canada in Central Okanogan School District No. 23 v. Renaud,", "2 S.C.R. 970. In that decision, for a unanimous court, Sopinkla J. wrote as follows : To facilitate the search for an accommodation, the complainant must do his or her part as well . Concomitant with a search for reasonable accommodation is a duty to facilitate the search for such an accommodation. Thus in determining whether the duty of accommodation has been fulfilled the conduct of the complainant must be considered. [Emphasis in original]", "On the basis of the record that was before the Commission, and that is before me, the only possible inference is that the Union made every effort to advance the Applicant's grievance but had to abandon the process at step III because of the Applicant's refusal to provide the necessary information, a refusal that has not been linked to his alleged disability. The Commission deals with this matter extensively in the Decision by referring to Mr. Fitzgerald's letter and the Step III Grievance Response dated April 19, 2013. The Applicant provided nothing to counter the information regarding his non-cooperation. It has to be remembered that it was the Applicant who provided the letter from Mr. Fitzgerald so that he was well-aware of what it said about him, and it also has to be borne in mind that his non-cooperation is evidenced by his own Union who had supported him in the grievance process. There was nothing to suggest that the Applicant's failure to cooperate had anything to do with his disability.", "It is also noteworthy that the Canadian Industrial Relations Board came to a similar conclusion when the Applicant alleged a violation of s. 37 of the Canada Labour Code , and alleged that the Union breached its duty of fair representation by failing to properly represent him when it decided not to proceed further with his grievance ( Mulligan v National Automobile, Aerospace, Transportation and General Workers Union of Canada (CAW-Canada) (31 July 2013), 29997-C (CIRB):", "In this case, the complainant requests that the Board hold a hearing. Section 16.1 of the Code provides that the Board may decide any matter before it without holding an oral hearing. Having reviewed all of the material on file, the Board is satisfied that the documentation before it is sufficient for it to decide the matter without holding an oral hearing. As mentioned above, the complainant alleges that the union acted in an arbitrary manner and in bad faith when it did not properly investigate his grievance, did not contact him and did not seek the proper information from his doctors and counsellor. The complainant also alleges that the union violated his rights with respect to article 23.2 of the collective agreement. Section 37 of the Code reads as follows: 37. A trade union or representative of a trade union that is the bargaining agent for a bargaining unit shall not act in a manner that is arbitrary, discriminatory or in bad faith in the representation of any of the employees in the unit with respect to their rights under the collective agreement that is applicable to them. The Board's role in the context of a duty of fair representation complaint is to examine the union's conduct in handling the employee's grievance (see Bugay , 1999 CIRB 45). A section 37 complaint cannot serve to appeal a union's decision not to refer a grievance to arbitration, or to assess the merits of the grievance, but it is used to assess how the union handled the grievance (see Presseault , 2001 CIRB 138). In a complaint under section 37, the complainant bears the onus of presenting evidence that is sufficient to raise a presumption that the union has breached its duty of fair representation. The Board will normally find that the union has fulfilled its duty of fair representation if it has investigated the circumstances, considered the merits of the grievance, made a reasoned judgment about whether to pursue the issue, and if it advised the employee of the reason for its ultimate decision not to proceed any further. The duty of a member to cooperate with his union is described in the following passage from McRaeJackson , 2004 CIRB 290:", "The union's duty of fair representation is predicated on the requirement that employees take the necessary steps to protect their own interests. Employees must make the union aware of potential grievances and ask the union to act on their behalf within the time limits provided in the collective agreement. They must cooperate with their union throughout the grievance procedure, for example by providing the union with the information necessary to investigate a grievance, by attending any medical examinations or other assessments. The evidence on file indicates that the union filed a grievance on behalf of the complainant, processed the grievance to step three of the grievance procedure, sent several letters to the complainant seeking medical information and had numerous telephone conversation with the complainant, with limited success in getting the information needed to further his case. In the Board's opinion, the complainant did not provide any evidence of wrongdoing by the union. The documentation submitted indicates that the complainant brought his termination upon himself by not submitting the information requested by the union. Failure by the complainant to take such action, along with his refusal to cooperate with the union, leads the Board to conclude that the union did not act in an arbitrary manner or in bad faith. Having reviewed the facts submitted, the Board finds that the complainant did not provide sufficient facts to establish that the union has violated its duty of fair representation. For the above reasons, the complaint is dismissed.", "This decision by the Canadian Industrial Relations Board was not before the Commission, but it confirms the Commission's conclusions that the Applicant is the one who, for no apparent reason, thwarted the grievance process that the Commission had earlier told him he had to exhaust before bringing his complaint to the Commission.", "As the Report makes clear, all of the Applicant's submissions were considered including the \"issue of consent and ongoing substance use\" that he claims was not addressed by the Respondent, as well as the correspondence from the Applicant's doctor and personnel in the Respondent's Employee Assistance Program.", "can find no reviewable error in the Commission's Decision (which includes the Report), which ably sets out the relevant facts and the governing jurisprudence. This is simply a case where the Applicant, for no apparent reason, refused to cooperate in the grievance process that could have dealt with his human rights issues and left his Union with no alternative but to close out the file.", "The Commission provides full reasons as to why the complaint was vexatious and why justice did not require the Commission to deal with the complaint.", "Subsection 41(1)(d) of the Act does not require a decision by a grievance arbitrator. As Justice Zinn pointed out in Bergeron , above:", "The jurisprudence is clear that the Commission is to be afforded great latitude in exercising its judgment and in assessing the appropriate factors when considering the application of paragraph 41(1)(d) of the CHRA and performing this \"screening function:\" See, e.g., Sketchley at para 38.", "Bergeron , above, makes it clear that s. 41(1)(d) of the Act may apply in situations where a union has decided not to pursue a grievance to arbitration. In the present case, as the Union letter makes clear, the Applicant refused, for no reason that is established, to engage in a grievance process that could have provided him with accommodation and arbitration and that could have dealt with his human rights issues. The Union makes it clear that his failure to cooperate meant that there was no point in proceeding to arbitration. Having failed to exhaust a grievance process that could have provided him with the remedy he sought before the Commission, the Applicant then filed his complaint with the Commission. The Applicant failed to show that his complaint could not have reasonably been dealt with by the grievance process. The Commission's Decision should not be disturbed.", "The Commission's Decision is transparent, intelligible and justifiable. I can find no reviewable error. It falls within the range of possible acceptable outcomes which are defensible in respect of the facts and the law. JUDGMENT", "THIS COURT'S JUDGMENT is that 1. This application is dismissed with costs to the Respondent. Application dismissed. Editor: J. Danielle King/bk [End of document]"], "label": 1}
# task1=dict()
# task1['guid']='1839d9b_d6f26064d6f489ae6e1a681139e58eb7223837a0'
# task1['q_paras']=['Detection of CDE as active WM is platform-spe...','SWT code currently determines the active deskt...']
# task1['c_paras']=['quert_1','query_2']
# task1['label']=1
# task1
# with open('case_para_sample.json','w',encoding='utf-8') as f_out:
#     for i in range(4):
#         f_out.write(str(task1)+'\n')

# 模型需要的输入样例 下面进行模型的测试
{
	"guid": "queryID_docID",
	"q_paras": [...], // a list of paragraphs in query case,
	"c_paras": [...], // a list of parameters in candidate case,
	"label": 0, // 0 or 1, denote the relevance
 }
 
{
	"guid": "queryID_docID",
	"res": [[],...,[]], // N * 768, result of BertPoolOutMax,
	"label": 0, // 0 or 1, denote the relevance
}

In [29]:
import configparser
import os
import functools


class ConfigParser:
    def __init__(self, *args, **params):
        self.default_config = configparser.RawConfigParser(*args, **params)
        self.local_config = configparser.RawConfigParser(*args, **params)
        self.config = configparser.RawConfigParser(*args, **params)

    def read(self, filenames, encoding=None):
        if os.path.exists("config/default_local.config"):
            self.local_config.read("config/default_local.config", encoding=encoding)
        else:
            self.local_config.read("config/default.config", encoding=encoding)

        self.default_config.read("config/default.config", encoding=encoding)
        self.config.read(filenames, encoding=encoding)


def _build_func(func_name):
    @functools.wraps(getattr(configparser.RawConfigParser, func_name))
    def func(self, *args, **kwargs):
        try:
            return getattr(self.config, func_name)(*args, **kwargs)
        except Exception as e:
            try:
                return getattr(self.local_config, func_name)(*args, **kwargs)
            except Exception as e:
                return getattr(self.default_config, func_name)(*args, **kwargs)

    return func


def create_config(path):
    for func_name in dir(configparser.RawConfigParser):
        if not func_name.startswith('_') and func_name != "read":
            setattr(ConfigParser, func_name, _build_func(func_name))

    config = ConfigParser()
    config.read(path)

    return config
config = create_config('/home/hdj/BERT-PLI-IJCAI2020/config/nlp/BertPoolOutMaxTrain.config')

In [19]:
import torch.nn as nn
import torch.nn.functional as F
from pytorch_pretrained_bert import BertModel
from transformers import RobertaTokenizer, RobertaConfig, RobertaModel, AdamW
import torch

class BertPoolOutMax(nn.Module):
    def __init__(self, config, gpu_list, *args, **params):
        super(BertPoolOutMax, self).__init__()
        self.max_para_c = config.getint('model', 'max_para_c')
        self.max_para_q = config.getint('model', 'max_para_q')
        self.step = config.getint('model', 'step')
        self.max_len = config.getint("data", "max_seq_length")
#         self.bert = BertModel.from_pretrained(config.get("model", "bert_path"))
        self.bert = RobertaModel.from_pretrained("microsoft/codebert-base")
        # self.maxpool = nn.MaxPool1d(kernel_size=self.max_para_c)
        self.maxpool = nn.MaxPool2d(kernel_size=(1, self.max_para_c))

    def init_multi_gpu(self, device, config, *args, **params):
        self.bert = nn.DataParallel(self.bert, device_ids=device)

    def forward(self, data, config, gpu_list, acc_result, mode):
        input_ids, attention_mask, token_type_ids = data['input_ids'], data['attention_mask'], data['token_type_ids']

        with torch.no_grad():
            output = []
            for k in range(input_ids.size()[0]):
                q_lst = []
                for i in range(0, self.max_para_q, self.step):
                    # print(input_ids[k, i:i+self.step].view(-1, self.max_len).size())
                    _, lst = self.bert(input_ids[k, i:i+self.step].view(-1, self.max_len),
                                       token_type_ids=token_type_ids[k, i:i+self.step].view(-1, self.max_len),
                                       attention_mask=attention_mask[k, i:i+self.step].view(-1, self.max_len))
                    # print('before view', lst.size())
                    lst = lst.view(self.step, self.max_para_c, -1)
                    # print('after view', lst.size())
                    lst = lst.permute(2, 0, 1)
                    # print('after permute', lst.size())
                    lst = lst.unsqueeze(0)
                    # print('after unsquezze', lst.size())
                    max_out = self.maxpool(lst)
                    # print('after maxpool', max_out.size())
                    max_out = max_out.squeeze()
                    # print('after squeeze', max_out.size())
                    max_out = max_out.transpose(0, 1)
                    q_lst.extend(max_out.cpu().tolist())
                    #input('continue?')
                # print(len(q_lst))
                #exit()
                assert (len(q_lst) == self.max_para_q)
                output.append([data['guid'][k], q_lst])
            return {"output": output}
        

In [4]:
class BertPoint(nn.Module):
    def __init__(self, config, gpu_list, *args, **params):
        super(BertPoint, self).__init__()

        self.output_dim = config.getint("model", "output_dim")
        self.output_mode = config.get('model', 'output_mode')

        # self.bert = BertModel.from_pretrained(config.get("model", "bert_path"))
        self.bert = RobertaModel.from_pretrained("microsoft/codebert-base")
        self.fc = nn.Linear(768, self.output_dim)
        if self.output_mode == 'classification':
            self.criterion = nn.CrossEntropyLoss()
        else:
            self.criterion = nn.MSELoss()
        self.accuracy_function = init_accuracy_function(config, *args, **params)

    def init_multi_gpu(self, device, config, *args, **params):
        self.bert = nn.DataParallel(self.bert, device_ids=device)

    def forward(self, data, config, gpu_list, acc_result, mode):
        input_ids, attention_mask, token_type_ids = data['input_ids'], data['attention_mask'], data['token_type_ids']
        _, y = self.bert(input_ids,
                         # token_type_ids=token_type_ids,
                         attention_mask=attention_mask,
                            # output_all_encoded_layers=False
                         )
        y = y.view(y.size()[0], -1)

        if mode == 'test' and config.getboolean('output', 'pool_out'):
            output = []
            y = y.cpu().detach().numpy().tolist()
            for i, guid in enumerate(data['guid']):
                output.append([guid, y[i]])
            return {"output": output}

        y = self.fc(y)
        y = y.view(y.size()[0], -1)

        if "label" in data.keys():
            label = data["label"]
            loss = self.criterion(y, label.view(-1))
            acc_result = self.accuracy_function(y, label, config, acc_result)
            return {"loss": loss, "acc_result": acc_result}

        else:
            output = []
            y = y.cpu().detach().numpy().tolist()
            for i, guid in enumerate(data['guid']):
                output.append([guid, y[i]])
            return {"output": output}

In [5]:
def init_accuracy_function(config, *args, **params):
    name = config.get("output", "accuracy_method")
    if name in accuracy_function_dic:
        return accuracy_function_dic[name]
    else:
        raise NotImplementedError

def get_prf(res):
    # According to https://github.com/dice-group/gerbil/wiki/Precision,-Recall-and-F1-measure
    if res["TP"] == 0:
        if res["FP"] == 0 and res["FN"] == 0:
            precision = 1.0
            recall = 1.0
            f1 = 1.0
        else:
            precision = 0.0
            recall = 0.0
            f1 = 0.0
    else:
        precision = 1.0 * res["TP"] / (res["TP"] + res["FP"])
        recall = 1.0 * res["TP"] / (res["TP"] + res["FN"])
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1


def gen_micro_macro_result(res):
    precision = []
    recall = []
    f1 = []
    total = {"TP": 0, "FP": 0, "FN": 0, "TN": 0}
    for a in range(0, len(res)):
        total["TP"] += res[a]["TP"]
        total["FP"] += res[a]["FP"]
        total["FN"] += res[a]["FN"]
        total["TN"] += res[a]["TN"]

        p, r, f = get_prf(res[a])
        precision.append(p)
        recall.append(r)
        f1.append(f)

    micro_precision, micro_recall, micro_f1 = get_prf(total)

    macro_precision = 0
    macro_recall = 0
    macro_f1 = 0
    for a in range(0, len(f1)):
        macro_precision += precision[a]
        macro_recall += recall[a]
        macro_f1 += f1[a]

    macro_precision /= len(f1)
    macro_recall /= len(f1)
    macro_f1 /= len(f1)

    return {
        "micro_precision": round(micro_precision, 3),
        "micro_recall": round(micro_recall, 3),
        "micro_f1": round(micro_f1, 3),
        "macro_precision": round(macro_precision, 3),
        "macro_recall": round(macro_recall, 3),
        "macro_f1": round(macro_f1, 3)
    }


def null_accuracy_function(outputs, label, config, result=None):
    return None


def single_label_top1_accuracy(outputs, label, config, result=None):
    if result is None:
        result = []
    id1 = torch.max(outputs, dim=1)[1]
    # id2 = torch.max(label, dim=1)[1]
    id2 = label
    nr_classes = outputs.size(1)
    while len(result) < nr_classes:
        result.append({"TP": 0, "FN": 0, "FP": 0, "TN": 0})
    for a in range(0, len(id1)):
        # if len(result) < a:
        #    result.append({"TP": 0, "FN": 0, "FP": 0, "TN": 0})

        it_is = int(id1[a])
        should_be = int(id2[a])
        if it_is == should_be:
            result[it_is]["TP"] += 1
        else:
            result[it_is]["FP"] += 1
            result[should_be]["FN"] += 1

    return result


def multi_label_accuracy(outputs, label, config, result=None):
    if len(label[0]) != len(outputs[0]):
        raise ValueError('Input dimensions of labels and outputs must match.')

    outputs = outputs.data
    labels = label.data

    if result is None:
        result = []

    total = 0
    nr_classes = outputs.size(1)

    while len(result) < nr_classes:
        result.append({"TP": 0, "FN": 0, "FP": 0, "TN": 0})

    for i in range(nr_classes):
        outputs1 = (outputs[:, i] >= 0.5).long()
        labels1 = (labels[:, i].float() >= 0.5).long()
        total += int((labels1 * outputs1).sum())
        total += int(((1 - labels1) * (1 - outputs1)).sum())

        if result is None:
            continue

        # if len(result) < i:
        #    result.append({"TP": 0, "FN": 0, "FP": 0, "TN": 0})

        result[i]["TP"] += int((labels1 * outputs1).sum())
        result[i]["FN"] += int((labels1 * (1 - outputs1)).sum())
        result[i]["FP"] += int(((1 - labels1) * outputs1).sum())
        result[i]["TN"] += int(((1 - labels1) * (1 - outputs1)).sum())

    return result


def single_label_top2_accuracy(outputs, label, config, result=None):
    raise NotImplementedError
    # still bug here

    if result is None:
        result = []
        # print(label)

    id1 = torch.max(outputs, dim=1)[1]
    # id2 = torch.max(label, dim=1)[1]
    id2 = label
    nr_classes = outputs.size(1)
    while len(result) < nr_classes:
        result.append({"TP": 0, "FN": 0, "FP": 0, "TN": 0})
    for a in range(0, len(id1)):
        # if len(result) < a:
        #    result.append({"TP": 0, "FN": 0, "FP": 0, "TN": 0})

        it_is = int(id1[a])
        should_be = int(id2[a])
        if it_is == should_be:
            result[it_is]["TP"] += 1
        else:
            result[it_is]["FP"] += 1
            result[should_be]["FN"] += 1

    _, prediction = torch.topk(outputs, 2, 1, largest=True)
    prediction1 = prediction[:, 0:1]
    prediction2 = prediction[:, 1:]

    prediction1 = prediction1.view(-1)
    prediction2 = prediction2.view(-1)

    return result
accuracy_function_dic = {
    "SingleLabelTop1": single_label_top1_accuracy,
    "MultiLabel": multi_label_accuracy,
    "Null": null_accuracy_function
}

In [6]:
model =BertPoint(config, 0,'', "BertPoint")


In [14]:
model_list = {
    "BertPoint": BertPoint,
}


def get_model(model_name):
    if model_name in model_list.keys():
        return model_list[model_name]
    else:
        raise NotImplementedError
model = get_model('BertPoint')(config, 0)

In [16]:
parameters = torch.load('/home/hdj/BERT-PLI-IJCAI2020/output/model/task2/1_save.pkl')

In [28]:
def load_state_keywise(model, pretrained_dict):
    model_dict = model.state_dict()
    # print(model_dict.keys())
    # input("continue?")
    tmp_cnt = 0
    for k, v in pretrained_dict.items():
        # kk = k.replace("module.", "")
        # print('k=', k)
        # input("continue?")
        # print('kk=', kk)
        # input("continue?")
        
        if k in model_dict and v.size() == model_dict[k].size():
            model_dict[k] = v
            tmp_cnt += 1
            
            print('here',k)
        else:
            continue
    model.load_state_dict(model_dict)
    return model

In [29]:
model = load_state_keywise(model, parameters["model"])

here fc.weight
here fc.bias


In [1]:
# model_to_save = model.module if hasattr(model, 'module') else model
# if hasattr(model, 'module'):
#     print('这个是存在module的****')
# elif hasattr(model,'modules'):
#     print('这个是存在modules的////')
# else:
#     print('什么都么有++++')
# for key, val in model_to_save.state_dict().items():
#     print('&'*10,key)

In [18]:
#TODO 
parameters = torch.load('/home/hdj/BERT-PLI-IJCAI2020/output/model/task2/1.pkl')

In [53]:
for key,val in parameters.items():
    print(key)

model
optimizer_name
optimizer
trained_epoch
global_step


In [20]:
if hasattr(model, 'module'):
    print('has module')
else:
    print('model')

model


In [64]:
# for key,val in model.state_dict().items():
#     print(key)

In [8]:
# for key in model.modules().state_dict():
#     print(key)

In [7]:
# model_dict = model.state_dict()
# for (key1,val1),(key2,val2) in zip(model_dict.items(),parameters['model'].items()):
#     print(key1,' *** ',key2,' // ',key1.endswith(key2) )
# # for key,val in model.children:
# #     print(key)

In [6]:
from transformers import AutoTokenizer, AutoModel

model = AutoModel.from_pretrained("/data/hdj/data/CodeBERT/codesearch/java_model_codesearch/512_0202_del_import_0.62_0.14_0.18/checkpoint-best")

In [46]:
output=None
for i in range(2):
    a=torch.tensor([[1,1,1],[2,2,2]])
    print(a.shape)
    # b=torch.tensor([[3,3,3],[4,4,4]])
    if   output==None:
        output=a.reshape(1,-1)
    else:
        
        output=torch.cat([output,a.view(1,-1)],axis=0)
#     output.append()
output

torch.Size([2, 3])
torch.Size([2, 3])


tensor([[1, 1, 1, 2, 2, 2],
        [1, 1, 1, 2, 2, 2]])

In [35]:
a=torch.tensor([[1,1,2,2,2]])
output1=torch.cat([a,a],axis=0)
output1

tensor([[1, 1, 2, 2, 2],
        [1, 1, 2, 2, 2]])

In [63]:
# if hasattr(model, 'module'):
#     print('t')
# else:
#     print('f')
# for key,val in model.state_dict().items():
#     print(key)
# model_to_save = model.module if hasattr(model, 'module') else model
# save_params = {
#         "model": model_to_save.state_dict(),
#         "optimizer_name": 'no_exists',
#         "optimizer": 'optimizer.state_dict()',
#         "trained_epoch": 3,
#         "global_step":1
# }
# torch.save(save_params, '/home/hdj/BERT-PLI-IJCAI2020/output/filenamed.pkl')

In [8]:
filename=torch.load('/home/hdj/BERT-PLI-IJCAI2020/output/filenamed.pkl')
filenameModel=filename['model']

In [13]:

# fine_tune=torch.load('/home/hdj/BERT-PLI-IJCAI2020/output/model/task2/1.pkl')
# fine_tuneModel=fine_tune['model']

In [ ]:
# model.state_dict()

In [47]:
# filenameModel

In [12]:
# for key,val in filename['model'].items():
#     print(key)

In [11]:
# for key,val in parameters.items():
#     print(key)


# 模型需要的样例结束

In [62]:
# tomcat_ast_file = pickle.loads(tomcat_ast_cache_collection_db['5d3a94c94ec7de55d2d83b0c8ba4ca4689626309'])
# tomcat_ast_file['methodContent']

# 根据bid 和fid获取相应的字符结束

In [66]:
all_results_df_top_k.index.get_level_values(0).unique().shape[0]
3645/500

7.29

In [64]:
all_results_df_top_k.loc[500:999].shape,all_results_df_top_k.loc[1000:1499]

((11300, 3),
             used_in_fix        f1    result
 bid  fid                                   
 1000 49145          0.0  0.705370  1.017476
      51842          0.0  0.469063  1.010488
      48469          0.0  0.382648  1.005852
      59764          0.0  0.365029  0.981343
      56397          1.0  0.613496  0.971999
 ...                 ...       ...       ...
 1496 65114          0.0  0.146357  0.704480
 1497 61536          1.0  0.806280  1.068151
 1498 60362          1.0  0.836437  1.183161
 1499 58744          0.0  0.605660  1.088062
      53823          1.0  0.286494  1.078769
 
 [10038 rows x 3 columns])

In [50]:
print(all_results_df_top_k.loc[4143].shape)
all_results_df_top_k.loc[4143]

(6, 3)


used_in_fix        f1    result
fid                                    
192560          0.0  0.501966  0.977433
194161          0.0  0.567927  0.933350
196790          0.0  0.523463  0.874957
197560          0.0  0.068011  0.834388
196903          0.0  0.422107  0.825218
191432          1.0  0.523463  0.815574

In [6]:
top_k=sorted_df[:50]

In [13]:
# print(top_k.head())
print(top_k.shape)
top_k_pos=top_k['used_in_fix'].sum()
all_pos=sorted_df['used_in_fix'].sum()
print('top_k :',top_k_pos)
print('all :',all_pos)
print('recall :',top_k_pos/all_pos)

(50, 3)
top_k : 1.0
all : 2.0
recall : 2.0
(50, 3)
top_k : 1.0
all : 2.0
recall : 2.0
(50, 3)
top_k : 1.0
all : 2.0
recall : 2.0
(50, 3)
top_k : 1.0
all : 2.0
recall : 2.0


# 计算前k个的recall，将前k个文件保存起来结束

In [2]:
# sum_val=0
# average_precision_per_bug_report = []
# reciprocal_ranks = []
# k_range=range(1, 21)
# bug_report_number = 0
# accuracy_at_k = dict.fromkeys(k_range, 0)
# for i,(bug_report, bug_report_files_dataframe)  in enumerate(all_results_df_before.groupby(level=0, sort=False)):
#     print('index :',i,bug_report,bug_report_files_dataframe.shape[0])
#     sum_val+=bug_report_files_dataframe.shape[0]
# #     print(bug_report_files_dataframe)
#     min_fix_result = bug_report_files_dataframe[bug_report_files_dataframe['used_in_fix'] == 1.0]['result'].min()
#     bug_report_files_dataframe2 = bug_report_files_dataframe[bug_report_files_dataframe["result"] >= min_fix_result]
# #     print('取fix得分最小值之前的所有文件 ',bug_report_files_dataframe2.shape,' 过滤前大小 :',bug_report_files_dataframe.shape,
# #           ' min_fix_result :',min_fix_result)
#     sorted_df = bug_report_files_dataframe2.sort_values(ascending=False, by=['result'])
#     #假如过滤后没有值，直接用原始的dataframe
#     if sorted_df.shape[0] == 0:
#         sorted_df = bug_report_files_dataframe.copy().sort_values(ascending=False, by=['result'])
#     #为了代码的健壮性
    
#     #保存在k位置正例的比例
#     precision_at_k = []
    
#     # precision per k in range
#     #给原始数据增加一列position，使用tmp保存
#     tmp = sorted_df
#     a = range(1, tmp.shape[0] + 1)
#     tmp['position'] = pd.Series(a, index=tmp.index)
# #     print(tmp)
#     #保存的是fix的排序位置
#     large_k_p = tmp[(tmp['used_in_fix'] == 1.0)]['position'].tolist()
# #     print('large_k_p :',large_k_p)
#     #保存的是result的升序排列
#     unique_results = sorted_df['result'].unique().tolist()
#     unique_results.sort()
# #     print('unique_results :',unique_results)
#     #计算在k位置前有多少正例,计算的是MAP的值
#     for fk in large_k_p:#[4, 186]
#         k = int(fk)
#         #取
#         k_largest = unique_results[-k:]
#         largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
#         real_fixes_at_k = (largest_at_k['used_in_fix'] == 1.0).sum()
#         #正例个数/位置k
#         p = float(real_fixes_at_k) / float(k)
#         precision_at_k.append(p)
# #     print('precision_at_k :',precision_at_k)
#     average_precision = pd.Series(precision_at_k).mean()
#     average_precision_per_bug_report.append(average_precision)
# #     print('average_precision_per_bug_report :',average_precision_per_bug_report)
#     #保存MAP完毕
    
#     #计算TOP20
#     for k in k_range:
#         k_largest = unique_results[-k:]
#         largest_at_k = sorted_df[sorted_df['result'] >= min(k_largest)]
#         real_fixes_at_k = largest_at_k['used_in_fix'][(largest_at_k['used_in_fix'] == 1.0)].count()
#         if real_fixes_at_k >= 1:
#             accuracy_at_k[k] += 1
#     #计算TOP20完毕
    
#     #计算MRR
#     indexes_of_fixes = np.flatnonzero(sorted_df['used_in_fix'] == 1.0)
# #     print('indexes_of_fixes :',indexes_of_fixes)
#     if indexes_of_fixes.size == 0:
#         reciprocal_ranks.append(0.0)
#     else:
#         first_index = indexes_of_fixes[0]
#         reciprocal_rank = 1.0 / (first_index + 1)
#         reciprocal_ranks.append(reciprocal_rank)
# #     print('reciprocal_ranks :',reciprocal_ranks)
#     #计算MRR完毕
#     bug_report_number += 1
# #     print('*'*10)
# #     if i==10:
# #         break

In [14]:
mean_average_precision = pd.Series(average_precision_per_bug_report).mean()
    # print('mean average precision', mean_average_precision)
mean_reciprocal_rank = pd.Series(reciprocal_ranks).mean()
# print('mean reciprocal rank', mean_reciprocal_rank)
for k in k_range:
    accuracy_at_k[k] = accuracy_at_k[k] / bug_report_number

In [17]:
mean_average_precision,mean_reciprocal_rank,accuracy_at_k

(0.40892458362741296,
 0.47245062488563383,
 {1: 0.3429355281207133,
  2: 0.46227709190672156,
  3: 0.5349794238683128,
  4: 0.5914951989026063,
  5: 0.6315500685871056,
  6: 0.6595336076817558,
  7: 0.6858710562414266,
  8: 0.7058984910836763,
  9: 0.725925925925926,
  10: 0.7374485596707819,
  11: 0.7489711934156379,
  12: 0.7602194787379972,
  13: 0.7720164609053498,
  14: 0.7838134430727023,
  15: 0.7906721536351166,
  16: 0.798079561042524,
  17: 0.8021947873799725,
  18: 0.8079561042524005,
  19: 0.8137174211248285,
  20: 0.8200274348422496})

In [75]:
sum([0.25, 0.010752688172043012])/2

0.1303763440860215

# 指标计算结束

In [2]:
all_results_df_before.index.get_level_values(0).unique().shape[0]

3645

In [28]:
fold_test_1 = pd.read_pickle('/data/hdj/tracking_buggy_files/swt/swt_normalized_testing_fold_1')

In [32]:
from skopt import *
fold_number, fold_testing, fold_training = load('/data/hdj/tracking_buggy_files/joblib_memmap_swt/swt/data_memmap', mmap_mode="r")

In [62]:
fold_number,len(fold_testing)

(8, 9)

In [61]:
# all_rows=0
# for i in range(1,9):
#     print(fold_testing[i].shape[0])
#     all_rows+=fold_testing[i].shape[0]
# print(all_rows)

In [10]:
# for i in range(500,1000):
#     print(fold_testing[1].loc[i].shape,all_results_df_before.loc[i].shape)

In [5]:
all_results_df_after.shape,type(all_results_df_after)

((6955822, 3), pandas.core.frame.DataFrame)

In [14]:
all_results_df_after.to_csv('/data/hdj/tracking_buggy_files/joblib_memmap_tomcat/after.csv')

In [3]:
all_results_df_after_check=pd.read_csv('/data/hdj/tracking_buggy_files/joblib_memmap_tomcat/after.csv')
all_results_df_after_check.shape

(883535, 4)

In [47]:
type(queries),type(corpus),len(queries),len(corpus)

(list, dict, 1, 1000)

In [18]:
# corpus.keys()

In [60]:
# # aspectj_test=pd.read_csv('/data/hdj/SourceFile/data/sourceFile_aspectj/aspectj_test.csv')
# all_data=pd.read_csv('/data/hdj/SourceFile/data/sourceFile_aspectj/all_data.csv')
# all_data.head()
# # aspectj_test[['bug_id','files']].head()

In [6]:
all_fixed_files=[]
for file in all_data['files'].values:
    all_fixed_files.extend(eval(file))

In [7]:
len(all_fixed_files)
# all_fixed_files
with open('/data/hdj/SourceFile/data/sourceFile_aspectj/fixed_files.txt','w',encoding='utf-8') as f_out:
    for file in all_fixed_files:
        f_out.write(file+'\n')

In [10]:
src_addresses = glob.glob(str('/data/hdj/SourceFile/data/clean/sourceFile_aspectj/org.aspectj') + '/**/*.java', recursive=True)
len(src_addresses)

2357

In [59]:
# aspectj_test_pos_neg['path'][1000],aspectj_test_pos_neg['path'][2]

In [58]:
# aspectj_test_pos_neg=pd.read_csv('/data/hdj/SourceFile/data/sourceFile_aspectj/aspectj_test_pos_neg.csv')
# aspectj_test_pos_neg.head(1002)

In [25]:
aspectj_test=pd.read_csv('/data/hdj/SourceFile/data/sourceFile_aspectj/aspectj_test.csv')
# aspectj_test[['bug_id','files']].head()
bug_ids=aspectj_test['bug_id'].values
files=aspectj_test['files'].values
for i,(bid,file) in enumerate(zip(bug_ids,files)):
    print(i,bid,file)
    if i==10:
        break
tests/bugs163/pr251326/pkgA/Target.java

0 251326 ['tests/bugs163/pr251326/pkgA/f1a83b5 Listener.java', 'tests/bugs163/pr251326/pkgA/f1a83b5 Target.java', 'tests/src/org/aspectj/systemtest/ajc163/f1a83b5 Ajc163Tests.java']
1 256400 ['asm/src/org/aspectj/asm/internal/155a888 JDTLikeHandleProvider.java']
2 259528 ['tests/multiIncremental/pr259528/base/src/b/2b43e63 IsAdvised.java', 'tests/multiIncremental/pr259528/inc1/src/b/2b43e63 IsAdvised.java']
3 260751 ['org.aspectj.ajdt.core/src/org/aspectj/ajdt/ajc/d9bd46d ConfigParser.java']
4 261808 ['taskdefs/src/org/aspectj/tools/ant/taskdefs/1da1f7c AjcTask.java']
5 263837 ['weaver/src/org/aspectj/weaver/bcel/1b54b4b BcelClassWeaver.java', 'weaver/src/org/aspectj/weaver/bcel/1b54b4b BcelTypeMunger.java', 'weaver/src/org/aspectj/weaver/bcel/1b54b4b BcelWeaver.java']
6 264563 ['asm/src/org/aspectj/asm/internal/0af658e JDTLikeHandleProvider.java']
7 264869 ['org.aspectj.matcher/src/org/aspectj/weaver/9f80317 ShadowMunger.java']
8 266602 ['weaver/src/org/aspectj/weaver/bcel/2f36e7f Bce

In [57]:
# #测试DictVectorizer()如何使用
# import pandas as pd
# from collections import Counter
# from sklearn.feature_extraction import DictVectorizer
# data=[]
# def convert(dict_list):
#     counter_list = []
#     for d in dict_list:
#         counter_list.append(Counter(d))
#     return counter_list
# test_dict={'a':1,'b':2,'d':3}
# data.extend(convert([test_dict]))

# test_list=[{'a':1,'b':2,'e':3},{'a':1,'b':2,'f':3},{'a':1,'b':2,'g':3}]
# data.extend(convert(test_list))

# vectorizer = DictVectorizer()
# vectorized_data = vectorizer.fit_transform(data)
# feature_names = vectorizer.get_feature_names()
# feature_names_lenghts_dict = {}
# for i, feature_name in enumerate(feature_names):
#     feature_names_lenghts_dict[i] = feature_name
# feature_names_lenghts_dict
# # vectorized_data.toarray()

In [ ]:
import numpy as np
import torch

x=[
[[1,2,3,4],[5,6,7,8],[9,10,11,12]],
[[13,14,15,16],[17,18,19,20],[21,22,23,24]]
]
x=torch.tensor(x).float()
#
print("shape of x:")  ##[2,3,4]                                                                      
print(x.shape)                                                                                   
#
print("shape of x.mean(axis=0,keepdim=True):")          #[1, 3, 4]
print(x.mean(axis=0,keepdim=True).shape)                       
#
print("shape of x.mean(axis=0,keepdim=False):")         #[3, 4]
print(x.mean(axis=0,keepdim=False).shape)                     
#
print("shape of x.mean(axis=1,keepdim=True):")          #[2, 1, 4]
print(x.mean(axis=1,keepdim=True).shape)                      
#
print("shape of x.mean(axis=1,keepdim=False):")         #[2, 4]
print(x.mean(axis=1,keepdim=False).shape)                    
#
print("shape of x.mean(axis=2,keepdim=True):")          #[2, 3, 1]
print(x.mean(axis=2,keepdim=True).shape)                     
#
print("shape of x.mean(axis=2,keepdim=False):")         #[2, 3]
print(x.mean(axis=2,keepdim=False).shape) 
————————————————
版权声明：本文为CSDN博主「南瓜派三蔬」的原创文章，遵循CC 4.0 BY-SA版权协议，转载请附上原文出处链接及本声明。
原文链接：https://blog.csdn.net/qq_36810398/article/details/104845401